In [2]:
import array as array
from array import array 
import os
import glob

from random import gauss
import numpy as np
#import root_numpy as rtnpy
#from root_numpy import *
#import h5py
#from awkward import JaggedArray, Table
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
import sys
sys.path.insert(0,'../test/')
from DrawHistogram import *
from Samples_dijetSel import checkDict, dictSamples
sys.path.insert(0,'../python/')
import CMS_lumi as CMS_lumi

import tdrstyle as tdrstyle
from variables_dijetSel import nSubVariables as nSubVariables_dijetSel

from root_numpy import array2hist, hist2array
import ROOT
from ROOT import TH1D, TH2D, TTree,TFile, TUnfoldSys, TUnfoldDensity, TUnfold, TDirectoryFile
import yoda

/tmp/ipykernel_1485/2856485812.py:14: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


Welcome to JupyROOT 6.24/06



### Get list of nanoskim files to run over and sum gen event weights (ie, n_events) for a given samples

In [3]:
lumi=0.
canvas = {}
textBox=ROOT.TLatex()
textBox.SetTextSize(0.10)
textBox.SetTextAlign(12)

In [4]:
def Fill1D(h0,h,bins):
    N=h0.GetNbinsX()
    content=np.zeros((len(bins)-1),dtype=float)
    errors=np.zeros((len(bins)-1),dtype=float)

    for i in range(len(bins)-1):
        content[i]=0
    for i in range(N):
        center=h0.GetBinCenter(i+1)
        index=np.digitize(np.array([center]),bins)
        if index[0] < len(bins):
            content[index[0]-1]+=h0.GetBinContent(i+1)
            errors[index[0]-1]+=h0.GetBinError(i+1)
    for i in range(len(bins)-1):
        h.SetBinContent(i+1,content[i])
        h.SetBinError(i+1,errors[i])

def Fill2D(h0,h,binx,biny):
    Nx=h0.GetNbinsX()
    Ny=h0.GetNbinsY()
    hx=h0.ProjectionX()
    hy=h0.ProjectionY()
    content=np.zeros((len(binx)-1,len(biny)-1),dtype=float)
    errors=np.zeros((len(binx)-1,len(biny)-1),dtype=float)
    for i in range(len(binx)-1):
        for j in range(len(biny)-1):
            content[i][j]=0
    for i in range(Nx):
        for j in range(Ny):
            centerx=hx.GetBinCenter(i+1)
            indexx=np.digitize(np.array([centerx]),binx)
            centery=hy.GetBinCenter(j+1)
            indexy=np.digitize(np.array([centery]),biny)
            if indexx[0] < len(binx) and indexy[0] < len(biny):
                content[indexx[0]-1][indexy[0]-1]+=h0.GetBinContent(i+1,j+1)
                errors[indexx[0]-1][indexy[0]-1]+=ROOT.TMath.Power(h0.GetBinError(i+1,j+1),2)
                
    for i in range(len(binx)-1):
        for j in range(len(biny)-1):
            h.SetBinContent(i+1,j+1,content[i][j])
            h.SetBinError(i+1,j+1,ROOT.TMath.Sqrt(errors[i][j]))


In [5]:
def correlation_from_covariance(covariance,hist): #pythonic, need to rootify
    covariance = hist2array(covariance)
    v = np.sqrt(np.diag(covariance))
    outer_v = np.outer(v, v)
    correlation = covariance / outer_v
    correlation[covariance == 0] = 0
    return array2hist(correlation,hist)


In [6]:
def DoUnfolding(Response,Reco):
    tunfolder = ROOT.TUnfoldDensity(Response,
                                    ROOT.TUnfold.kHistMapOutputHoriz,
                                    ROOT.TUnfold.kRegModeCurvature, 
                                    ROOT.TUnfold.kEConstraintNone, 
                                    ROOT.TUnfoldDensity.kDensityModeBinWidth)
    tunfolder.SetInput(Reco)
    tunfolder.DoUnfold(0.)
    return tunfolder.GetOutput("MC_unfolded")

def CrossClosure(response1,reco1,response2,reco2):
    unf11=DoUnfolding(response1,reco1)
    unf12=DoUnfolding(response2,reco1)
    unf21=DoUnfolding(response1,reco2)
    unf22=DoUnfolding(response2,reco2)
    return unf11,unf12,unf21,unf22

def SelfClosure(response1,reco2,response2,reco1):
    unf21=DoUnfolding(response1,reco2)
    unf12=DoUnfolding(response2,reco1)
    return unf21,unf12

In [7]:
def getRebinnedRescaledHist(hist_name, file_name, xrange, scale, isMC=True):
    #if not(sample_name in file_name): 
    #    return "File either not available or needs to be renamed to be compatible with this (poorly,) hard-coded piece of software..."
    
    FILE = ROOT.TFile.Open(file_name,'read')
    tree = FILE.Get('jetObservables')
    hist = tree.Get(hist_name)
    hist.SetDirectory(0)
    
    ROOT.TH1.AddDirectory(ROOT.kFALSE);
    
    bins = array('d', np.array(Bin(xrange)))
    
    newHist = ROOT.TH1F(hist.Rebin(len(bins)-1, "%s_rebin"%hist_name, bins))
    #newHist.SetStats(ROOT.kFALSE)
    if isMC==True: newHist.Scale(scale)
    
    return newHist

In [8]:
def getRebinnedHist(hist, xrange, scale, isMC=True):
    #if not(sample_name in file_name): 
    #    return "File either not available or needs to be renamed to be compatible with this (poorly,) hard-coded piece of software..."
    hist.SetDirectory(0)
    
    ROOT.TH1.AddDirectory(ROOT.kFALSE);
    
    bins = array('d', np.array(Bin(xrange)))
    
    newHist = ROOT.TH1F(hist.Rebin(len(bins)-1, "%s_rebin"%hist_name, bins))
        
    return newHist

In [9]:
def Scale(h):
    n=h.Integral()
    h.Scale(1./n,"width")

In [10]:
from array import array
ROOT.gStyle.SetOptStat(0)

In [11]:
##########################################################################
def loadHistograms( samples, var, sel, sysUnc=[], isMC=True, addGenInfo=True, respOnly=False, lumi=1., variables={}, year='2017', process='data' ):
    """docstring for loadHistograms"""

    if sysUnc==[]: SYSUNC = [ '_nom' ] 
    else: sysUnc = [ s+u for u in ['Up', 'Down'] for s in sysUnc if not s.startswith(('_model', '_hdamp', '_Tune', '_CR', '_erdON', '_mtop')) ]
    flip = False
    #print ('All available samples:', samples, sysUnc)
    allHistos = {}
    jesList = [((i.split('_Tune')[0]).split('sysQCD')[1]).split('_HT')[0] for i in sysSignalLabels if 'jes' in i ]
    #print ("Loading Histos", jesList)
    for isam in samples:
        #print ("Sample name", isam)
        if sysUnc!=[]:
            for i in (['_jer', '_isrWeight', '_fsrWeight', '_puWeight', '_pdfWeight']):
                if i in isam:
                    flip=True
                    tmpSYSUNC = [i+u for u in ['Up','Down']]
                    continue
            for k in jesList:
                if k in isam:
                    #print (k)
                    flip=True
                    #k = ((i.split('_Tune')[0]).split('sysQCD')[1]).split('_HT')[0]
                    #print (k)
                    tmpSYSUNC = [k+u for u in ['Up','Down']]
                    continue
            #if sysUnc!=[]: 
            #    flip = True
            #    tmpSYSUNC=SYSUNC
            #print (tmpSYSUNC)           
        if not flip: tmpList = [ 'reco'+var+syst+sel for syst in SYSUNC]
        else: tmpList = ['reco'+var+syst+sel for syst in tmpSYSUNC]
        #print (tmpList)
        #if isMC and addGenInfo: tmpList = tmpList + [ 'gen'+var+sel ] + [ 'resp'+var+syst+sel for syst in SYSUNC ]
        if isMC and addGenInfo and not flip: tmpList = tmpList + [ 'gen'+var+sel] + [ 'resp'+var+syst+sel for syst in SYSUNC]
        
        elif isMC and addGenInfo and flip: 
            tmpList = tmpList + [ 'gen'+var+sel]
            for syst in tmpSYSUNC:
                tmpList = tmpList + ['resp'+var+syst+sel]
        
        if respOnly and not flip: 
            tmpList = [ 'resp'+var+syst+sel for syst in SYSUNC] 
            #print (SYSUNC,tmpList)
        elif respOnly and flip: 
            tmpList = ['resp'+var+syst+sel for syst in tmpSYSUNC ] #+ [ 'missgen'+var+sel ]
            #print (tmpSYSUNC,tmpList)
        
        for ih in tmpList:
            #print ('Processing '+isam+' '+ih, flip)
            #print (samples[isam][0])
            if isMC:
                allHistos[isam+'_'+ih] = samples[isam][0].Get( 'jetObservables/'+ih )
                tmpIsam = 'TT' if isam.startswith('data') else isam
                MCScale = samples[isam][1]['XS'] * lumi / samples[isam][1][year][('nGenWeights') ]
                allHistos[isam+'_'+ih].Scale( MCScale )
            else:
                if sel.startswith('_dijet'):# and process.startswith('data'):
                    tmpdataHistos = {}
                    for it in checkDict( 'JetHT', dictSamples )[year]['triggerList']:
                        tmpdataHistos[ it ] = samples[isam][0].Get( 'jetObservables/'+ih.replace( sel, '_'+it+sel ) )
                        tmpdataHistos[ it ].Scale( checkDict( 'JetHT', dictSamples )[year]['triggerList'][it] )
                    allHistos[ isam+'_'+ih ] = tmpdataHistos[next(iter(tmpdataHistos))].Clone()
                    allHistos[ isam+'_'+ih ].Reset()
                    for i in tmpdataHistos: allHistos[isam+'_'+ih].Add( tmpdataHistos[i] )
                else:
                    allHistos[isam+'_'+ih] = samples[isam][0].Get( 'jetObservables/'+ih )

            if len(variables[var]['bins'])==1:
                genBin = variables[var]['bins'][0]
                recoBin = variables[var]['bins'][0]/2
            else:
                genBin = variables[var]['bins']
                #print (genBin)
                recoBintemp = array('d',[])#np.empty(2*bins.shape[0]-1)#np.array(sorted([ np.round((bins[i]+bins[i+1])/2.,3) for i in range(len(bins)-1) ] + bins))
                for i in range(0,len(variables[var]['bins'])-1):
                    recoBintemp.append(np.round((variables[var]['bins'][i]+variables[var]['bins'][i+1])/2.,3))
                #print (recoBintemp)
                recoBintemp.extend(variables[var]['bins'])
                recoBin = array('d', sorted(recoBintemp))
                #print (recoBin)
                
            if not ih.startswith('resp'):
                if len(variables[var]['bins'])==1:
                    if ih.startswith(('reco','fake', 'true')):
                        allHistos[isam+'_'+ih+'_genBin'] = allHistos[isam+'_'+ih].Clone()
                        allHistos[isam+'_'+ih+'_genBin'].Rebin( genBin )
                        allHistos[isam+'_'+ih].Rebin( recoBin )
                    else: allHistos[isam+'_'+ih].Rebin( genBin )
                else:
                    if ih.startswith(('reco','fake','true')):
                        allHistos[isam+'_'+ih+'_genBin'] = allHistos[isam+'_'+ih].Clone()
                        allHistos[isam+'_'+ih+'_genBin'] = allHistos[isam+'_'+ih+'_genBin'].Rebin( len(genBin)-1, allHistos[isam+'_'+ih].GetName()+"_Rebin_genBin", array( 'd', genBin ) )
                        allHistos[isam+'_'+ih] = allHistos[isam+'_'+ih].Rebin( len(recoBin)-1, allHistos[isam+'_'+ih].GetName()+"_Rebin", array( 'd', recoBin ) )
                    else:
                        allHistos[isam+'_'+ih] = allHistos[isam+'_'+ih].Rebin( len(genBin)-1, allHistos[isam+'_'+ih].GetName()+"_Rebin", array( 'd', genBin ) )
            else:
                if len(variables[var]['bins'])==1: allHistos[isam+'_'+ih].Rebin2D( genBin, recoBin )
                else:

                    #### fancy way to create variable binning TH2D
                    tmpHisto = ROOT.TH2F( allHistos[isam+'_'+ih].GetName()+isam+"_Rebin", allHistos[isam+'_'+ih].GetName()+isam+"_Rebin", len(genBin)-1, array( 'd', genBin), len(recoBin)-1, array( 'd', recoBin) )

                    tmpArrayContent = np.zeros((len(genBin), len(recoBin)))
                    tmpArrayError = np.zeros((len(genBin), len(recoBin)))

#                    for biny in range( 1, allHistos[isam+'_'+ih].GetNbinsY()+1 ):
#                        for binx in range( 1, allHistos[isam+'_'+ih].GetNbinsX()+1 ):
#                            tmpHisto.Fill( allHistos[isam+'_'+ih].GetXaxis().GetBinCenter(binx), allHistos[isam+'_'+ih].GetYaxis().GetBinCenter(biny), allHistos[isam+'_'+ih].GetBinContent( binx, biny ) )

                    for biny in range( 1, allHistos[isam+'_'+ih].GetNbinsY()+1 ):
                        by = allHistos[isam+'_'+ih].GetYaxis().GetBinCenter( biny )
                        for binx in range( 1, allHistos[isam+'_'+ih].GetNbinsX()+1 ):
                            bx = allHistos[isam+'_'+ih].GetXaxis().GetBinCenter(binx)
                            for iX in range( len(genBin)-1 ):
                                for iY in range( len(recoBin)-1 ):
                                    if (bx<genBin[iX+1] and bx>genBin[iX]) and (by<recoBin[iY+1] and by>recoBin[iY]):
                                        jbin = allHistos[isam+'_'+ih].GetBin(binx,biny)
                                        tmpArrayContent[iX][iY] = tmpArrayContent[iX][iY] + allHistos[isam+'_'+ih].GetBinContent( jbin )
                                        tmpArrayError[iX][iY] = tmpArrayError[iX][iY] + ROOT.TMath.Power( allHistos[isam+'_'+ih].GetBinError( jbin ), 2 )

                    for biny in range( 1, tmpHisto.GetNbinsY()+1 ):
                        for binx in range( 1, tmpHisto.GetNbinsX()+1 ):
                            #if (binx <= ((biny+1)/2.)+4) and (binx >= ((biny+1)/2.)-4):
                            tmpHisto.SetBinContent( tmpHisto.GetBin(binx,biny), tmpArrayContent[binx-1][biny-1] )
                            tmpHisto.SetBinError( tmpHisto.GetBin(binx,biny), ROOT.TMath.Sqrt(tmpArrayError[binx-1][biny-1] ) )

                    tmpHisto.Sumw2()
                    allHistos[isam+'_'+ih] = tmpHisto

                #if isMC: allHistos[isam+'_'+ih].Scale( MCScale )
                ##### For tests, projections directly from 2D
                allHistos[isam+'_genJetfrom_'+ih] = allHistos[isam+'_'+ih].ProjectionY()
                allHistos[isam+'_recoJetfrom_'+ih] = allHistos[isam+'_'+ih].ProjectionX()
    #print (allHistos)
    if sel.startswith('_dijet'):
        tmpHistos = { k:v for (k,v) in allHistos.items() if 'Inf' in k }
        for ih in tmpHistos:
            for jh in allHistos:
                if (jh.endswith('0'+ih.split('Inf')[1])) and not ('Inf' in jh ):
                    tmpHistos[ih].Add( allHistos[jh].Clone() )
        if len(tmpHistos)>0: allHistos = tmpHistos
    #print (tmpHistos)
    '''
    if len(samples)<2:
        
        #print (samples[isam][1][year]['skimmerHisto'])
        outFileName = samples[isam][1][year]['skimmerHisto'].split('.root')[0]+'_loadedHistos.root'
        print ("Written loaded/rebinned histos to:", outFileName)
        outFile = ROOT.TFile.Open ( '../test/Samples/'+outFileName ," RECREATE ")
        outHistFile.cd()
        for h in allHistos:
            h.Write()
        outFile.Close()
    '''
    return allHistos

In [12]:
def plotSysComparison( nomHisto, dictUncHistos, outputName, labelX='', log=False, version='', ext='png', year='2017', outputDir='Plots/' ):
    """docstring for plot"""
    colors = [ 2, 4,  9, 8, 28, 30, 42, 13, 12, 40, 46, 3, 24, 26, 219, 92, 48, 49, 37, 38, 33, 17, 50, 205, 225, 94, 221, 16,  225, 128]
    
    
    outputFileName = outputName+'_'+version+'.'+ext
    #print ('Processing.......', outputFileName)

    binWidth = nomHisto.GetBinWidth(1)

    legend=ROOT.TLegend(0.35,0.6,0.80,0.9)
    legend.SetFillStyle(0)
    legend.SetNColumns(3)
    legend.SetTextSize(0.02)
    legend.SetBorderSize(0)

    multiGraph = ROOT.TMultiGraph()
    gnom = ROOT.TGraphAsymmErrors()
    gnom.Divide( nomHisto.Clone(), nomHisto.Clone(), 'pois' )
    gnom.SetLineColor(ROOT.kBlack)
    gnom.SetMarkerStyle(1)
    gnom.SetLineWidth(2)
    legend.AddEntry( gnom, 'Nominal' , 'l' )
    multiGraph.Add( gnom )

    dictgraph = {}
    dummy=0
    
    #print (dictUncHistos)
    for ih in dictUncHistos:
        #print(ih, dummy, len(colors))
        dictgraph[ih] = ROOT.TGraphAsymmErrors()
        dictgraph[ih].Divide( dictUncHistos[ih], nomHisto, 'pois' )
        if not dummy==len(colors)-1:
            dictgraph[ih].SetLineColor( colors[dummy] )
            dictgraph[ih].SetLineStyle( 2 )
            if 'jes' in ih: dictgraph[ih].SetLineStyle( 1 )
            dictgraph[ih].SetMarkerStyle(1)
            dictgraph[ih].SetLineWidth( 1 )
        else:
            dummy = dummy-len(colors)+2
            dictgraph[ih].SetLineColor( colors[dummy] )
            dictgraph[ih].SetLineStyle( 3 )
            if 'jes' in ih: dictgraph[ih].SetLineStyle( 1 )
            dictgraph[ih].SetMarkerStyle(1)
            dictgraph[ih].SetLineWidth( 1 )
        if 'jes' in ih and ('2017' in ih or '2018' in ih): legend.AddEntry( dictgraph[ih], ih.split('_')[1] , 'l' )
        else: legend.AddEntry( dictgraph[ih], ih.split('_')[1] , 'l' )
        multiGraph.Add( dictgraph[ih] )
        dummy=dummy+1

    ROOT.gStyle.SetPadRightMargin(0.05)
    ROOT.gStyle.SetPadLeftMargin(0.15)
    canUnc = ROOT.TCanvas('canUnc', 'canUnc',  10, 10, 750, 500 )
    if log: canUnc.SetLogy()
    multiGraph.GetYaxis().SetTitle( 'Ratio Unc/Nominal' )
    multiGraph.GetXaxis().SetTitle( labelX )
    multiGraph.SetMaximum( 3. )
    multiGraph.SetMinimum( -1.)
    multiGraph.Draw('ALP')

    CMS_lumi.cmsTextOffset = 0.0
    CMS_lumi.relPosX = 0.13
    CMS_lumi.extraText = "Preliminary"
    CMS_lumi.lumi_13TeV = "13 TeV, "+year
    CMS_lumi.CMS_lumi(canUnc, 4, 0)
    legend.Draw()

    canUnc.SaveAs( outputDir + outputFileName )
    if ext.startswith('pdf'):
        canUnc.SaveAs( outputDir + outputFileName.replace('pdf', 'png') )
    del canUnc

In [13]:
def drawClosures(ivar, selection, process, year, genJetHisto, genJetHistoCross, unfoldHisto, unfoldHistoCross,
                 ratioUncHisto, ratiototUncHisto, ratiosystUncHisto, labelX, maxX, tlegendAlignment, outputName ):
    
    """docstring for drawUnfold"""
    #print ("Drawing unfolding")
    ROOT.gStyle.SetPadRightMargin(0.05)
    ROOT.gStyle.SetPadLeftMargin(0.15)
    can = ROOT.TCanvas('can'+ivar, 'can'+ivar,  10, 10, 750, 750 )
    pad1 = ROOT.TPad("pad1"+ivar, "Main",0,0.207,1.00,1.00,-1)
    pad2 = ROOT.TPad("pad2"+ivar, "Ratio",0,0.00,1.00,0.30,-1);
    pad1.Draw()
    pad2.Draw()

    pad1.cd()

    if tlegendAlignment.startswith('right'): legend=ROOT.TLegend(0.65,0.65,0.90,0.88)

    else: legend=ROOT.TLegend(0.20,0.65,0.40,0.88)
    legend.SetFillStyle(0)
    legend.SetTextSize(0.03)
    legend.SetBorderSize(0)

    dataIntegral = genJetHisto.Integral()
    unfoldIntegral = unfoldHisto.Integral()
    if process.startswith('MCCrossClosure'): unfoldcrossIntegral = unfoldHistoCross.Integral()
    #tmpMax = float(unfoldHisto.GetMaximum())
    
    #unfoldHisto.Scale(1, 'width')  ### divide by bin width
    unfoldHisto.Scale(1/unfoldHisto.Integral(), 'width')  ### divide by bin width
    unfoldHisto.SetMarkerStyle(4)
    #unfoldHisto.SetMarkerSize(2)
    unfoldHisto.SetMarkerColor(ROOT.kRed)
    unfoldHisto.SetLineColor(ROOT.kRed)
    unfoldHisto.SetLineWidth(2)
    legend.AddEntry( unfoldHisto, ('Data (self-closure)' if process.startswith('MCSelfClosure') else 'MG5+P8 unf. w/ MG5+P8'), 'pe' )
    
    #genJetHisto.Scale(1, 'width')
    #genJetHisto.Scale(scaleFactor)
    genJetHisto.Scale(1/genJetHisto.Integral(), 'width')  ### divide by bin width
    genJetHisto.SetLineWidth(2)
    genJetHisto.SetLineColor(ROOT.kBlue)
    genJetHisto.SetMarkerStyle(0)
    genJetHisto.SetLineStyle(2)
    legend.AddEntry( genJetHisto, 'MG5+Pythia8 (gen)', 'lp' )
    unfoldHisto.GetYaxis().SetTitle( '#frac{1}{d#sigma} #frac{d#sigma}{d#'+labelX.split('#')[1]+'}' )
    #unfoldHisto.GetYaxis().SetTitleOffset(0.95)
    unfoldHisto.GetYaxis().SetTitleSize(0.05)
    unfoldHisto.SetMaximum( 1.5*max([ genJetHisto.GetMaximum(), unfoldHisto.GetMaximum()] )  )

    unfoldHisto.Draw( "E")
    genJetHisto.Draw( "histe same")
    
    if not process.startswith('MCSelfClosure'):
        #unfoldHisto.Scale(1, 'width')  ### divide by bin width
        unfoldHistoCross.Scale(1/unfoldHistoCross.Integral(), 'width')  ### divide by bin width
        unfoldHistoCross.SetMarkerStyle(26)
        #unfoldHistoCross.SetMarkerSize(2)
        unfoldHistoCross.SetMarkerColor(ROOT.kRed+4)
        unfoldHistoCross.SetLineColor(ROOT.kRed+4)
        unfoldHistoCross.SetLineWidth(2)
        legend.AddEntry( unfoldHistoCross, 'MG5+P8 unf. w/ Herwig7', 'pe' )

        #genJetHisto.Scale(1, 'width')
        #genJetHisto.Scale(scaleFactor)
        genJetHistoCross.Scale(1/genJetHistoCross.Integral(), 'width')  ### divide by bin width
        genJetHistoCross.SetLineWidth(2)
        genJetHistoCross.SetLineColor(ROOT.kMagenta)
        genJetHistoCross.SetMarkerStyle(0)
        genJetHistoCross.SetLineStyle(2)
        legend.AddEntry( genJetHistoCross, 'Herwig7 (gen)', 'lp' )
        
        unfoldHistoCross.Draw( "E same")
        genJetHistoCross.Draw( "histe same")
        

    selText = textBox.Clone()
    selText.SetTextFont(42)
    selText.SetTextSize(0.045)

    selText.SetNDC()

    if selection.startswith("_dijet"): seltext = ( 'Central' if 'Central' in labelX  else 'Outer' )+' dijet region'
    elif selection.startswith("_W"): seltext = ' Boosted W region'
    elif selection.startswith("_top"): seltext = ' Boosted top region'
    selText.DrawLatex( ( 0.2 if tlegendAlignment.startswith('right') else 0.68 ), 0.87, seltext )

    
    legend.Draw()
    if process.startswith('data'):
        CMS_lumi.extraText = "Preliminary"
        CMS_lumi.lumi_13TeV = ('#leq' if selection.startswith('dijet') else '')+str( round( (lumi/1000.), 2 ) )+" fb^{-1}, 13 TeV"+('' if year.startswith('all') else ", "+( '2017+2018' if year.startswith('all') else year ) )
    else:
        CMS_lumi.extraText = "Simulation Preliminary"
        CMS_lumi.lumi_13TeV = "13 TeV, "+ ( '2017+2018' if year.startswith('all') else year )
    CMS_lumi.relPosX = 0.12
    CMS_lumi.CMS_lumi(pad1, 4, 0)

    pad2.cd()
    ROOT.gStyle.SetOptFit(1)
    pad2.SetGrid()
    pad2.SetTopMargin(0.)
    pad2.SetBottomMargin(0.3)
    tmpPad2= pad2.DrawFrame( 0, 0., maxX, 1.9 )
    tmpPad2.GetXaxis().SetTitle( labelX )
    tmpPad2.GetYaxis().SetTitle( "Sim./Data" )
    tmpPad2.GetYaxis().SetTitleOffset( 0.5 )
    tmpPad2.GetYaxis().SetRangeUser(0.4,1.6 )
    tmpPad2.GetYaxis().CenterTitle()
    tmpPad2.SetLabelSize(0.12, 'x')
    tmpPad2.SetTitleSize(0.12, 'x')
    tmpPad2.SetLabelSize(0.12, 'y')
    tmpPad2.SetTitleSize(0.12, 'y')
    tmpPad2.SetNdivisions(505, 'x')
    tmpPad2.SetNdivisions(505, 'y')
    pad2.Modified()
    
    if 'Self' in process:

        hRatioUp = ROOT.TGraphAsymmErrors()
        hRatioUp.Divide( genJetHisto, unfoldHisto, 'pois' )
        hRatioUp.SetLineColor(ROOT.kBlack)
        hRatioUp.SetMarkerColor(ROOT.kBlack)
        hRatioUp.SetLineWidth(2)
        hRatioUp.SetMarkerStyle(25)
        hRatioUp.Draw('P0')

    else:
        hRatioUp2 = ROOT.TGraphAsymmErrors()
        hRatioUp2.Divide( unfoldHistoCross, unfoldHisto, 'pois' )
        hRatioUp2.SetLineColor(ROOT.kBlack)
        hRatioUp2.SetMarkerColor(ROOT.kBlack)
        hRatioUp2.SetLineWidth(2)
        hRatioUp2.SetMarkerStyle(25)
        hRatioUp2.Draw('P0')
    
    '''
    #hRatioDown.Draw('P same')
    ratioUncHisto.SetFillColor(15)
    #ratioUncHisto.SetLineColor(0)
    ratioUncHisto.SetFillStyle(3005)
    ratioUncHisto.SetMarkerStyle(0)
    #ratioUncHisto.Scale(1,'width')
    ratioUncHisto.Draw('E3 same')

    ratiototUncHisto.SetFillColor(8)
    #ratiototUncHisto.SetLineColor(0)
    ratiototUncHisto.SetFillStyle(3004)
    ratiototUncHisto.SetMarkerStyle(0)
    #ratiototUncHisto.Scale(1,'width')    
    ratiototUncHisto.Draw('E3 same')
    
    if not process.startswith('MCSelfClosure'):
        ratiosystUncHisto.SetFillColor(9)
        #ratiosystUncHisto.SetLineColor(0)
        ratiosystUncHisto.SetFillStyle(3006)
        ratiosystUncHisto.SetMarkerStyle(0)
        #ratiosystUncHisto.Scale(1,'width')    
        ratiosystUncHisto.Draw('E3 same')
    '''
    
    png = outputName.split('.pdf')[0]+'.png'
    can.SaveAs(outputName)
    can.SaveAs(png)
    ROOT.gStyle.SetPadRightMargin(0.09)     ## reseating
    ROOT.gStyle.SetPadLeftMargin(0.12)

In [14]:
def draw2D( ivar, histo, varInfo, outputDir, outputLabel='data', addCorrelation=False, addCondition=False, addInvertedMatrix=False,ext='pdf' ):
    """docstring for draw2D"""

    if not os.path.exists(outputDir): os.makedirs(outputDir)
    outputName = outputDir+ivar+'_'+selection+'_'+outputLabel+'_'+version+'.'+ext


    ROOT.gStyle.SetPadRightMargin(0.15)
    can2D = ROOT.TCanvas(ivar+'can2D', ivar+'can2D', 750, 500 )
    histo.GetXaxis().SetTitle('Accepted Gen '+varInfo['label'])
    histo.GetYaxis().SetTitle('True Reco '+varInfo['label'])
    histo.GetYaxis().SetTitleOffset( 0.8 )
    #signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel]covHisto.GetYaxis().SetRange( variables[ivar]['bins'][0], variables[ivar]['bins'][-1] )
    histo.Draw("colz")
    CMS_lumi.extraText = "Preliminary"
    CMS_lumi.lumi_13TeV = "13 TeV, "+ ( '2017+2018' if year.startswith('all') else year )
    CMS_lumi.relPosX = 0.12
    CMS_lumi.CMS_lumi(can2D, 4, 0)

    textBox.SetTextSize(0.04)
    if addCorrelation:
        #print('|-----> Correlation: ', histo.GetCorrelationFactor())
        textBoxCorr = textBox.Clone()
        textBoxCorr.DrawLatex( 0.05, varInfo['bins'][-1]-( .05*(varInfo['bins'][-1]-varInfo['bins'][0]) ), '#color[8]{Corr. Factor = '+str(round(histo.GetCorrelationFactor(),2))+'}' )

    if addCondition:   ## based on https://gitlab.cern.ch/DasAnalysisSystem/InclusiveJet/-/blob/master/UnfoldingSampleND/bin/unfold.cc#L41
        Nx = histo.GetNbinsX()
        Ny = histo.GetNbinsY()
        RMx = histo.ProjectionX( 'RMx', 0, -1 )

        m = ROOT.TMatrixD( Ny, Nx )   ### need to swap the axes
        for ibin in range(1, Nx+1):
            normalization = RMx.GetBinContent(ibin)
            if (normalization>0):
                for jbin in range( 1, Ny+1 ):
                    m[jbin-1][ibin-1] = histo.GetBinContent(ibin,jbin) / normalization
        svd = ROOT.TDecompSVD(m)
        v = ROOT.TVectorD( svd.GetSig() )
        Min = v[0]
        Max = v[0]
        for ibin in range( 0, Nx ):
            if (abs(v[ibin]) < 1e-5 ): break
            Min = v[ibin]
        conditionNumber = str(round( Max/Min, 2 )) if Min > 0 else 'NaN'
        print('|-----> Condition Number: ', conditionNumber)
        textBoxCond = textBox.Clone()
        textBoxCond.DrawLatex( 0.05, varInfo['bins'][-1]-( .1*(varInfo['bins'][-1]-varInfo['bins'][0]) ), '#color[8]{Cond. Number = '+conditionNumber+'}' )

    can2D.SaveAs(outputName)
    if ext.startswith('pdf'):
        can2D.SaveAs( outputName.replace('pdf', 'png') )

    ROOT.gStyle.SetPadRightMargin(0.09)     ## reseating
    ROOT.gStyle.SetPadLeftMargin(0.12)



In [15]:
def getFiles(labelBegin='', year_list=['2017','2018','all']):
    Files={}
    for iy in year_list:
        for isam in dictSamples:
            if not checkDict( isam, dictSamples )[iy]['skimmerHisto'].endswith('root'): continue
            if isam.startswith(labelBegin):
                Files[isam] = [
                                ROOT.TFile.Open(inputFolder+checkDict( isam, dictSamples )[iy]['skimmerHisto'] ),
                                checkDict( isam, dictSamples )
                            ]
    return Files

In [16]:
def combinePlots( name, dictHistos, numBins, mainHistoLabel, otherHisto, otherHistoLabel, outputLabel, variables, ext, process, log, year, runMLU, version,  axisX='', outputDir='Plots/', ratioOnly=False):

    """docstring for combinePlots"""

    outputFileName = name+'_'+outputLabel+'_combinePlots_'+version+'.'+ext
    if log: outputFileName = outputFileName.replace('Plots','Plots_Log')
    print('Processing.......', outputFileName)

    legend=ROOT.TLegend(0.10,0.80,0.60,0.90)
    legend.SetNColumns(3 if runMLU else 2)
    legend.SetFillStyle(0)
    legend.SetTextSize(0.06)

    dictHistos['combData'] = ROOT.TH1F('combData', 'combData', numBins[-1], 0, numBins[-1])
    legend.AddEntry( dictHistos[ 'combData' ], mainHistoLabel, 'lep' )
    dictHistos['combUnfold'] = ROOT.TH1F('combUnfold', 'combUnfold', numBins[-1], 0, numBins[-1])
    legend.AddEntry( dictHistos[ 'combUnfold' ], otherHistoLabel, 'lep' )
    if runMLU:
        dictHistos['combMLU'] = dictHistos['combUnfold'].Clone()
        legend.AddEntry( dictHistos[ 'combMLU' ], 'MLU', 'lep' )

    tmpNbin = 0
    Xlabels = []
    for ivar,ih in dictHistos.items():
        if ivar.startswith('Jet') and not ivar.endswith(('21', '32')):
            Xlabels.append( '#'+variables[ivar]['label'].split('#')[1] )
            for ibin in range(1, ih['data'].GetNbinsX()+1):
                tmpNbin = tmpNbin+1
                dictHistos['combData'].SetBinContent( tmpNbin, ih[otherHisto].GetBinContent(ibin) )
                dictHistos['combData'].SetBinError( tmpNbin, ih[otherHisto].GetBinError(ibin) )
                dictHistos['combUnfold'].SetBinContent( tmpNbin, ih['unfold'].GetBinContent(ibin) )
                dictHistos['combUnfold'].SetBinError( tmpNbin, ih['unfold'].GetBinError(ibin) )
                if runMLU:
                    dictHistos['combMLU'].SetBinContent( tmpNbin, ih['MLU'].GetBinContent(ibin) )
                    dictHistos['combMLU'].SetBinError( tmpNbin, ih['MLU'].GetBinError(ibin) )


    if not ratioOnly:
        canvas[outputFileName] = ROOT.TCanvas('c1'+name, 'c1'+name, 1400, 750 )
        ROOT.gStyle.SetPadRightMargin(0.05)
        ROOT.gStyle.SetPadLeftMargin(0.08)
        ROOT.gStyle.SetPadTickX(0)
        pad1 = ROOT.TPad(ivar+'1', "Fit",0.,0.330,1.00,1.00,-1)
        pad2 = ROOT.TPad(ivar+'2', "Pull",0,0.00,1.00,0.40,-1);
        pad1.Draw()
        pad2.Draw()

        pad1.cd()
        #pad1.SetLogy()
        dictHistos['combData'].GetXaxis().SetNdivisions(100)
        dictHistos['combData'].GetYaxis().SetTitle( '#frac{1}{d#sigma} #frac{d#sigma}{d#tau_{X}}' )
        dictHistos['combData'].GetYaxis().SetTitleSize( 0.06 )
        dictHistos['combData'].GetYaxis().SetTitleOffset( 0.6 )
        dictHistos['combData'].SetMaximum( dictHistos['combUnfold'].GetMaximum()*1.2 )
        dictHistos['combData'].SetMinimum( 0.001 )
        dictHistos['combData'].SetLineColor( ROOT.kBlack )
        dictHistos['combData'].SetLineWidth( 2 )

        dictHistos['combUnfold'].SetLineColor( ROOT.kMagenta )
        dictHistos['combUnfold'].SetLineWidth( 2 )
        dictHistos['combData'].Draw('E')
        dictHistos[ 'combUnfold' ].Draw('E same')
        if runMLU:
            dictHistos['combMLU'].SetLineColor( 8 )
            dictHistos['combMLU'].SetLineWidth( 2 )
            dictHistos[ 'combMLU' ].Draw('E same')

        ### division lines
        lines = {}
        for i in numBins[1:-1]:
            lines[i] = ROOT.TGraph(2, array('d', [i,i]), array('d', [0, 200]) )
            lines[i].SetLineColor(ROOT.kGray)
            lines[i].Draw('same')

        CMS_lumi.lumiTextSize = 0.6
        CMS_lumi.relPosX = 0.07
        CMS_lumi.CMS_lumi( pad1, 4, 0)
        legend.Draw()

        pad2.cd()
        pad2.SetGridy()
        pad2.SetTopMargin(0)
        pad2.SetBottomMargin(0.2)

        tmppad= pad2.DrawFrame(0,0.2,numBins[-1],1.8)
        tmppad.GetYaxis().SetTitle( "Data/Unfold" )
        tmppad.GetXaxis().SetTitle(  axisX )
        tmppad.GetYaxis().SetTitleOffset( 0.4 )
        tmppad.GetYaxis().CenterTitle()
        tmppad.SetLabelSize(0., 'x')
        tmppad.SetTitleSize(0., 'x')
        tmppad.SetLabelSize(0.10, 'y')
        tmppad.SetTitleSize(0.10, 'y')
        tmppad.SetNdivisions(100, 'x')
        tmppad.SetNdivisions(505, 'y')
        pad2.Modified()
        hRatio = ROOT.TGraphAsymmErrors()
        hRatio.Divide( dictHistos['combUnfold'], dictHistos[ 'combData' ], 'pois' )
        hRatio.SetMarkerStyle(8)
        hRatio.Draw('P0')
        if runMLU:
            hRatioMLU = ROOT.TGraphAsymmErrors()
            hRatioMLU.Divide( dictHistos['combMLU'], dictHistos[ 'combData' ], 'pois' )
            hRatioMLU.SetMarkerStyle(8)
            hRatioMLU.SetMarkerColor( 8 )
            hRatioMLU.Draw('P0 same')
            hRatio.Draw('P0 same')

        for i in lines: lines[i].Draw('same')

        textBox.SetTextSize(0.10)
        textBox.SetTextAlign(12)
        textBoxList = {}
        
        for i in range(1, len(numBins)):
            textBoxList[i] = textBox.Clone()
            textBoxList[i].DrawLatex(numBins[i-1]+(numBins[i]-numBins[i-1])/2., 0., Xlabels[i-1] )
        textBox.SetTextSize(0.04)
    else:

        legend=ROOT.TLegend(0.60,0.80,0.90,0.90)
        legend.SetNColumns(3 if runMLU else 2)
        legend.SetFillStyle(0)
        legend.SetTextSize(0.06)

        ROOT.gStyle.SetPadRightMargin(0.05)
        ROOT.gStyle.SetPadLeftMargin(0.08)
        ROOT.gStyle.SetPadTickX(0)
        canvas[outputFileName] = ROOT.TCanvas('c1'+name, 'c1'+name, 1400, 500 )
        canvas[outputFileName].SetGridy()

        hRatio = ROOT.TGraphAsymmErrors()
        hRatio.Divide( dictHistos[ 'combData' ], dictHistos['combUnfold'], 'pois' )
        if process.startswith('MCCrossClosure'): labelLegend = 'MCSelfClosure Ind.Sample'
        elif process.startswith('MCClosure'): labelLegend = 'MCCrossClosure'
        else: labelLegend = process
        legend.AddEntry( hRatio, labelLegend, 'lep' )
        hRatio.SetMarkerStyle(8)

        hRatio.GetXaxis().SetNdivisions(100)
        hRatio.GetYaxis().SetTitle( 'Sim. / Data'+(' (MC)' if process.startswith('MC') else '') )
        hRatio.GetYaxis().SetTitleSize( 0.06 )
        hRatio.GetYaxis().SetTitleOffset( 0.6 )
        hRatio.GetXaxis().SetLimits( 0., numBins[-1] )
        hRatio.SetMaximum( 2. )
        hRatio.SetMinimum( 0. )

        hRatio.Draw('AP')

        ### division lines
        lines = {}
        for i in numBins[1:-1]:
            lines[i] = ROOT.TGraph(2, array('d', [i,i]), array('d', [0, 200]) )
            lines[i].SetLineColor(ROOT.kGray)
            lines[i].Draw('same')

        CMS_lumi.lumiTextSize = 0.6
        CMS_lumi.relPosX = 0.07
        CMS_lumi.CMS_lumi( canvas[outputFileName], 4, 0)
        legend.Draw()

        aBox = textBox.Clone()
        aBox.SetTextSize(0.06)
        #aBox.DrawLatex( 5, 1.80, '#bf{#splitline{'+('Central Jet' if name.startswith('recoJet2') else 'Outer Jet')+"}{Dijet Selection}}"  )
        if 'WSel' in selection: aBox.DrawLatex( 5, 1.80, '#bf{#splitline{'+('Leading jet')+"}{Boosted W selection}}"  )
        elif 'topSel'in selection: aBox.DrawLatex( 5, 1.80, '#bf{#splitline{'+('Leading jet')+"}{Boosted top selection}}"  )
        textBox.SetTextAlign(12)
        textBoxList = {}
        for i in range(1, len(numBins)):
            textBoxList[i] = textBox.Clone()
            textBoxList[i].DrawLatex(numBins[i-1]+(numBins[i]-numBins[i-1])/2., -0.1, Xlabels[i-1] )

    canvas[outputFileName].SaveAs( outputDir+'/'+outputFileName )
    if ext.startswith('pdf'):
        canvas[outputFileName].SaveAs( outputDir+'/'+outputFileName.replace('pdf', 'png') )
    del canvas[outputFileName]
    ROOT.gStyle.SetPadTickX(1)

In [17]:
def combineRatioPlots( name, ratioDicts, numBins, outputLabel,process, ext, log, version, selection, axisX='', outputDir='Plots/'):
    """docstring for combineRatioPlots"""

    outputFileName = name+'_'+outputLabel+'_combineBLTPlots_'+version+'.'+ext
    if log: outputFileName = outputFileName.replace('Plots','Plots_Log')
    print('Processing.......', outputFileName)

    legend=ROOT.TLegend(0.5,0.8,0.8,0.90)
    legend.SetFillStyle(0)
    legend.SetTextSize(0.055)
    legend.SetBorderSize(0)
    
    tmpNbin = 0
    Xlabels = []
    yvaluesGen = np.array( [0]*numBins[-1], 'd' )
    yErrLowValuesGen = np.array( [0]*numBins[-1], 'd' )
    yErrHighValuesGen = np.array( [0]*numBins[-1], 'd' )
    yvaluesReco = np.array( [0]*numBins[-1], 'd' )
    yErrLowValuesReco = np.array( [0]*numBins[-1], 'd' )
    yErrHighValuesReco = np.array( [0]*numBins[-1], 'd' )
    for ivar,ih in ratioDicts.items():
        if ivar.startswith('Jet') and not ivar.endswith(('21', '32')):
            Xlabels.append( '#'+variables[ivar]['label'].split('#')[1] )
            for ibin in range( ih[0].GetN() ):
                a = ctypes.c_double(0.)
                b = ctypes.c_double(0.)
                ih[0].GetPoint(ibin, a, b)
                yvaluesGen[tmpNbin] = b.value
                yErrLowValuesGen[tmpNbin] = ih[0].GetErrorYlow(ibin)
                yErrHighValuesGen[tmpNbin] = ih[0].GetErrorYhigh(ibin)
                c = ctypes.c_double(0.)
                d = ctypes.c_double(0.)
                ih[1].GetPoint(ibin, c, d )
                yvaluesReco[tmpNbin] = d.value
                yErrLowValuesReco[tmpNbin] = ih[1].GetErrorYlow(ibin)
                yErrHighValuesReco[tmpNbin] = ih[1].GetErrorYhigh(ibin)
                tmpNbin = tmpNbin+1

    xvalues = np.array( range(1,numBins[-1]+1), 'd' )
    xvalues = xvalues - 0.5

    dictHistos = {}
    dictHistos['combRecoRatio'] = ROOT.TGraphAsymmErrors(len(xvalues), np.array(xvalues, 'd'), yvaluesReco, np.array([0.5]*len(xvalues), 'd' ), np.array([0.5]*len(xvalues), 'd' ), yErrLowValuesReco, yErrHighValuesReco )
    legend.AddEntry( dictHistos[ 'combRecoRatio' ], 'detector level (stat. unc. only)', 'lep' )
    dictHistos['combGenRatio'] = ROOT.TGraphAsymmErrors(len(xvalues), np.array(xvalues, 'd'), yvaluesGen, np.array([0]*len(xvalues), 'd' ), np.array([0]*len(xvalues), 'd' ), yErrLowValuesGen, yErrHighValuesGen )
    legend.AddEntry( dictHistos[ 'combGenRatio' ], 'hadron level (all uncorr. unc.)', 'lep' )


    canvas[outputFileName] = ROOT.TCanvas('c1'+name, 'c1'+name, 1400, 500 )
    canvas[outputFileName].SetGridy()
    ROOT.gStyle.SetPadRightMargin(0.05)
    ROOT.gStyle.SetPadLeftMargin(0.08)
    ROOT.gStyle.SetPadTickX(0)
    dictHistos['combRecoRatio'].SetLineColor( ROOT.kBlack )
    dictHistos['combRecoRatio'].SetMarkerColor( ROOT.kBlack )
    dictHistos['combRecoRatio'].SetLineWidth( 1 )

    dictHistos['combGenRatio'].SetLineColor( ROOT.kMagenta )
    dictHistos['combGenRatio'].SetMarkerColor( ROOT.kMagenta )
    dictHistos['combGenRatio'].SetLineWidth( 1 )

    multiGraph = ROOT.TMultiGraph()
    multiGraph.Add( dictHistos['combRecoRatio'] )
    multiGraph.Add( dictHistos['combGenRatio'] )

    multiGraph.GetXaxis().SetNdivisions(100)
    multiGraph.GetYaxis().SetTitle( 'Sim. / Data'+(' (MC)' if process.startswith('MC') else '') )
    multiGraph.GetYaxis().SetTitleSize( 0.06 )
    multiGraph.GetYaxis().SetTitleOffset( 0.6 )
    multiGraph.GetXaxis().SetLimits( 0., xvalues[-1]+1 )
    multiGraph.SetMaximum( 4.5 )
    multiGraph.SetMinimum( 0.5)
    multiGraph.Draw('AP')

    aBox = textBox.Clone()
    aBox.SetTextSize(0.06)
    #aBox.DrawLatex( 5, 1.80, '#bf{#splitline{'+('Central Jet' if name.startswith('recoJet2') else 'Outer Jet')+"}{Dijet Selection}}"  )
    if 'WSel' in selection: aBox.DrawLatex( 5, 4.10, '#bf{Boosted W selection}'  )
    elif 'topSel'in selection: aBox.DrawLatex( 5, 4.10, '#bf{Boosted top selection}'  )

    ### division lines
    lines = {}
    for i in numBins[1:-1]:
        lines[i] = ROOT.TGraph(2, array('d', [i,i]), array('d', [0, 200]) )
        lines[i].SetLineColor(ROOT.kGray)
        lines[i].Draw('same')

    CMS_lumi.lumiTextSize = 0.6
    CMS_lumi.relPosX = 0.07
    CMS_lumi.CMS_lumi( canvas[outputFileName], 4, 0)
    legend.Draw()

    textBox.SetTextAlign(12)
    textBoxList = {}
    
    print (len(numBins),len(Xlabels), numBins, Xlabels)

    for i in range(1, len(numBins)):
        textBoxList[i] = textBox.Clone()
        textBoxList[i].DrawLatex(numBins[i-1]+(numBins[i]-numBins[i-1])/2., -0.1, Xlabels[i-1] )
    
    canvas[outputFileName].SaveAs( outputDir+'/'+outputFileName )
    if ext.startswith('pdf'):
        canvas[outputFileName].SaveAs( outputDir+'/'+outputFileName.replace('pdf', 'png') )
    del canvas[outputFileName]
    ROOT.gStyle.SetPadTickX(1)

In [18]:
def bottomLineTest( ivar, dataHisto, mainHistoLabel, datarecoHisto, recoHisto, genHisto, datacovMatrix, hadcovMatrix, varInfo, outputLabel, outputDir, runMLU=False, ext='pdf' ):
    """based on https://gitlab.cern.ch/DasAnalysisSystem/InclusiveJet/-/blob/master/UnfoldingSampleND/bin/unfold.cc#L74"""

    outputDir=outputDir+'/'+ivar+'/'+process+'/'
    if not os.path.exists(outputDir): os.makedirs(outputDir)

    #recoHisto.Rebin( 2 )  ### because data and covMatrix have less number of bins
    #datarecoHisto.Rebin(2)
    #recoHisto.Scale( dataHisto.Integral()/recoHisto.Integral() )
    
    #genHisto.Scale( dataHisto.Integral()/genHisto.Integral() )

    #dataHisto.Scale(datarecoHisto.Integral()/dataHisto.Integral())

    #datarecoHisto.Scale( 1 )
    
    
    ##### computing chi2 and inverted matrix
    vector = []
    ndf = 0
    for ibin in range(1, datacovMatrix.GetNbinsX()+1):
        if (datacovMatrix.GetBinContent(ibin, ibin) > 0.):
            ndf = ndf + 1
            vector.append( datarecoHisto.GetBinContent( ibin ) - recoHisto.GetBinContent( ibin ) )
            
    print (ndf,datacovMatrix.GetNbinsX(),datacovMatrix.GetNbinsY())
    #assert ndf==covMatrix.GetNbinsX()
    matrix = np.eye( ndf, ndf )
    
    for ibin in range(1, datacovMatrix.GetNbinsX()+1):
        if (datacovMatrix.GetBinContent(ibin, ibin) > 0.):
            for jbin in range(1, datacovMatrix.GetNbinsY()+1):
                matrix[ibin-1][jbin-1] = datacovMatrix.GetBinContent( ibin, jbin )
    
    vector = np.array( vector )
    invMatrix = np.linalg.inv( matrix )
    chi2 = np.dot( vector, np.dot( invMatrix, vector ) )
    print('Detector level: chi2, ndf, chi2/ndf = ', chi2, ndf, chi2/ndf)
    
    
    vector = []
    ndf = 0
    for ibin in range(1, hadcovMatrix.GetNbinsX()+1):
        if (hadcovMatrix.GetBinContent(ibin, ibin) > 0.):
            ndf = ndf + 1
            vector.append( dataHisto.GetBinContent( ibin ) - genHisto.GetBinContent( ibin ) )
            
    print (ndf,hadcovMatrix.GetNbinsX(),hadcovMatrix.GetNbinsY())
    
    matrix = np.eye( ndf, ndf)
    
    for ibin in range(1, hadcovMatrix.GetNbinsX()+1):
        if (hadcovMatrix.GetBinContent(ibin, ibin) > 0.):
            for jbin in range(1, hadcovMatrix.GetNbinsY()+1):
                matrix[ibin-1][jbin-1] = hadcovMatrix.GetBinContent( ibin, jbin )

    #assert ndf==covMatrix.GetNbinsX()
    vector = np.array( vector )
    invMatrix = np.linalg.inv( matrix )
    chi2 = np.dot( vector, np.dot( invMatrix, vector ) )
    print('Hadron level: chi2, ndf, chi2/ndf = ', chi2, ndf, chi2/ndf)
    
    


    #### plotting inverted matrix
    invertedMatrix = hadcovMatrix.Clone()
    invertedMatrix.Reset()
    for ibin in range(1, hadcovMatrix.GetNbinsX()):
        for jbin in range(1, hadcovMatrix.GetNbinsY()):
            invertedMatrix.SetBinContent( ibin, jbin, invMatrix[ibin-1][jbin-1]  )
    draw2D( ivar, invertedMatrix, varInfo, outputLabel=outputLabel+'_invertedMatrix', outputDir=outputDir.split(ivar)[0] )

    ##### plotting ratios together
    outputName = outputDir+ivar+'_'+selection+'_'+outputLabel+'_bottomLineTest_'+version+'.'+ext

    canRatio = ROOT.TCanvas('canRatio'+ivar, 'canRatio'+ivar,  10, 10, 750, 500 )

    genRatio = ROOT.TGraphAsymmErrors()
    genRatio.Divide( dataHisto, genHisto, 'pois' )
    recoRatio = ROOT.TGraphAsymmErrors()
    recoRatio.Divide( datarecoHisto, recoHisto, 'pois' )

    legend=ROOT.TLegend(0.15,0.70,0.40,0.90)
    legend.SetFillStyle(0)
    legend.SetTextSize(0.03)
    legend.AddEntry( genRatio, 'Hadron level (w/ stat + unf. unc.)', 'pl' )
    legend.AddEntry( recoRatio, 'Detector level (stat unc.)', 'pl' )
    legend.SetBorderSize(0)
    
    genRatio.SetLineWidth(2)
    genRatio.GetXaxis().SetTitle(varInfo['label'])
    genRatio.GetXaxis().SetLimits( varInfo['bins'][0], varInfo['bins'][-1] )
    genRatio.GetYaxis().SetTitle('Data / Simulation')
    genRatio.GetYaxis().SetTitleOffset( 0.8 )
    genRatio.SetMarkerStyle(8)
    genRatio.GetYaxis().SetRangeUser(-5.,10.)
    genRatio.Draw('AP0')
    recoRatio.SetLineColor(ROOT.kRed)
    recoRatio.SetLineWidth(2)
    recoRatio.SetMarkerStyle(4)
    recoRatio.Draw('P0 same')

    lineOne = ROOT.TGraph(2, array('d', [0, 1]), array('d', [1, 1]))
    lineOne.Draw('same')

    legend.Draw()
    CMS_lumi.extraText = " Preliminary"
    CMS_lumi.lumi_13TeV = "13 TeV, "+ ( '2017+2018' if year.startswith('all') else year )
    CMS_lumi.relPosX = 0.11
    CMS_lumi.CMS_lumi(canRatio, 4, 0)
    canRatio.SaveAs(outputName)

    return [genRatio, recoRatio]

In [19]:
print (np.max([1,2,3,4]))

4


In [20]:
def makeJacobian(aTH1, aJac):
    N = aTH1.Integral(0,aTH1.GetNbinsX())
    for i in range(0,aTH1.GetNbinsX()):
        for j in range(0,aTH1.GetNbinsX()):
            if i==j: aJac[i][j]=1.*(N-aTH1.GetBinContent(i))/N**2 
            else: aJac[i][j]=(-1.*aTH1.GetBinContent(i))/N**2 
                

In [21]:
#Taken from Christine/Ashley: 
#https://gitlab.cern.ch/asparker/QJetMass/-/blob/master/unfold/cppImplementation/do2DTUnfolding_Dec15lep.py#L1790
def tmatrixdsparse_to_ndarray(matrix):
    ndarr = np.zeros(shape=(matrix.GetNrows(), matrix.GetNcols()))

    rows_A = matrix.GetRowIndexArray()
    cols_A = matrix.GetColIndexArray()
    data_A = matrix.GetMatrixArray()
    for iy in range(matrix.GetNrows()):
        for indexA in range(rows_A[iy], rows_A[iy+1]):
            ix = cols_A[indexA]
            # print([x for x in self.GetXToHist()])
            # TODO: care about orientation?
            ndarr[iy, ix] = data_A[indexA]
    return ndarr
def GetNormalizedTMatrixandTH2( ath2, matrixname , aunfoldedth1 ):
        # should use matrixname  to give uique names to histograms created in loop

        J = ROOT.TMatrixF( aunfoldedth1.GetNbinsX(), aunfoldedth1.GetNbinsX() )
        makeJacobian(aunfoldedth1 , J)

        cov_m,_ = th2_to_ndarray(ath2.Clone())
        covnormth2,_ = th2_to_ndarray(ath2.Clone())
        J = ROOT.TH2F(J.Clone())
        J, _ = th2_to_ndarray(J.Clone())
        
        covnorm = J@cov_m@J.T
        covnormth2 = ndarray_to_th2(covnorm)

        covnorm = ndarray_to_th2(covnorm)
        covnorm = th2_to_tmatrixd(covnorm)
        #covnorm_temp = ROOT.TMatrixD( cov_m, ROOT.TMatrixD.kMultTranspose, J)
        #print ("Transform total error matrix to normalized space using Jacobian ")
        #covnorm = ROOT.TMatrixD(J, ROOT.TMatrix.kMult, covnorm_temp )
        #print ("fill normalized th2 for later use...")
        
        #for xbin in range(0, ath2.GetNbinsX() +1):
        #    for ybin in range(0,ath2.GetNbinsY() +1  ):
        #        covnormth2.SetBinContent(xbin, ybin , covnorm[xbin][ybin])  
        #ErrorMatrixToHist(covnorm)
        #print ("th2 -> (TMatrixD ->normalized ->th2)-> [ tmatrix, th2 ]")
        #print (covnormth2)
        #print (matrixname)

        return [ covnorm.Clone() , covnormth2.Clone()  ]
    
#https://gitlab.cern.ch/asparker/QJetMass/-/blob/master/unfold/cppImplementation/do2DTUnfolding_Mar15_BottomLine.py#L119
def ConvertTH2toTMatrix( someth2 ):
    acov_m = ROOT.TMatrixD( someth2.GetNbinsX()+1, someth2.GetNbinsY()+1 )

    for xbin in range(0, someth2.GetNbinsX()+1 ):
        for ybin in range(0,someth2.GetNbinsY()+1  ):
            if xbin > someth2.GetNbinsX() :
                print (xbin)
                print (ybin)
            acov_m[xbin][ybin] = someth2.GetBinContent(  xbin, ybin)
    print (" finished filling TMatrixD from TH2 "  )
    return acov_m

def ConvertTH1toTMatrix(  someth2 ):
    acov_m1 = ROOT.TVectorD( someth2.GetNbinsX()+1 )

    for xbin in range(0, someth2.GetNbinsX()+1 ):
            #for ybin in range(0,someth2.GetNbinsY()+1  ):
            if xbin > someth2.GetNbinsX() :
                print (xbin)
                #print ybin
            acov_m1[xbin] = someth2.GetBinContent(  xbin)
    print (" finished filling TVectorD from TH1 "  )
    return acov_m1


def NormYourHisto(hist = None ) :
    ### Make a new empty TH1 so the OFL and UFL will be zero
    name = hist.GetTitle()+'_normed'
    histn = hist.Clone(name)
    integral=0
    histn.Reset()
    
    for h in range(0,hist.GetNbinsX()+1) :
        bc = hist.GetBinContent(h) 
        be = hist.GetBinError(h)
        histn.SetBinContent(h ,bc)    
        histn.SetBinError(h, be)  
        integral+=bc
    
    for h in range(0,histn.GetNbinsX()+1) :
        bc = histn.GetBinContent(h) 
        be = histn.GetBinError(h)
        #print bw
        if integral > 0. :
            bc = bc/integral
            be = be/integral            
        histn.SetBinContent(h , bc)    
        histn.SetBinError(h, be)  
    
    return histn

def normalise_hist(h):
    if h.Integral() > 0:
        h.Scale(1./h.Integral())
    return h
def hist_divide_bin_width(h):
    """Create copy of hist, but each bin's contents is divide by the bin width"""
    h_new = h.Clone(h.GetName()+"DivideBinWidth")
    h_new.Scale(1., 'width')
    # if any bin has 0 entries before, it will now have nan, so we need to manually fix that
    # arghhhhhhhhhhhhhhhhhh
    for i in range(1, h_new.GetNbinsX()+1):
        if np.isnan(h_new.GetBinContent(i)):
            h_new.SetBinContent(i, 0)
            h_new.SetBinError(i, 0)
    h_new.SetEntries(h.GetEntries())  # needed as the default is to replace with integral
    return h_new

def normalise_hist_divide_bin_width(h):
    h_new = h.Clone(h.GetName()+"DivideBinWidth")
    normalise_hist(h_new)
    h_new = hist_divide_bin_width(h_new)
    return h_new

def get_syst_shifted_hist(syst_shift, unfolded=None):
    """Get histogram with systematic shift applied to bin contents
    Can specify starting hist, otherwise assumes unfolded w/no error
    """
    # TODO: syst_label -> ExpSystematic obj
    hist_shift = syst_shift.Clone(syst_shift.GetTitle()+'_shiftedbyNom')
    hist_shift.Add(unfolded)  # TODO what about errors?
    return hist_shift

def get_syst_error_hist(syst_shift, unfolded=None):
    """Get histogram with systematic shift as error bars
    Can specify starting hist, otherwise assumes unfolded w/no error
    """
    this_syst = self.get_exp_syst(syst_label)
    if this_syst.syst_error_bar is None:
        ref = unfolded or self.get_unfolded_with_no_errors()
        new_hist = self.convert_error_shift_to_error_bars(ref, self.get_syst_shift(syst_label))
        this_syst.syst_error_bar = new_hist
    return this_syst.syst_error_bar


def convert_error_bars_to_error_shift(h):
        """Create histogram with bin contents equal to error bar on h,
        and 0 error bars"""
        h_new = h.Clone(get_unique_str())
        for i in range(1, h.GetNbinsX()+1):
            h_new.SetBinContent(i, h.GetBinError(i))
            h_new.SetBinError(i, 0)
        return h_new


def convert_error_shift_to_error_bars(h_nominal, h_shift):
    """Create histogram with bin contents from h_nominal,
    and error bars from bin values of h_shift"""
    h = h_nominal.Clone(get_unique_str())
    for i in range(1, h_nominal.GetNbinsX()+1):
        h.SetBinError(i, h_shift.GetBinContent(i))
    return h

def convert_syst_shift_to_error_ratio_hist(h_syst, h_nominal):
    """Create h_syst / h_nominal without error bars"""
    h_new = h_syst.Clone(h_syst.GetName() + get_unique_str())
    h_new.Divide(h_nominal)
    for ix in range(1, h_new.GetNbinsX()+1):
        if h_nominal.GetBinContent(ix) == 0:
            h_new.SetBinContent(ix, 1)
        if h_syst.GetBinContent(ix) < 0:
            h_new.SetBinContent(ix, 1)
            print("Warning: _convert_syst_shift_to_error_ratio_hist bin", ix, "of h_syst < 0", h_syst.GetName(),h_syst.GetBinContent(ix))
        h_new.SetBinError(ix, 0)
    return h_new
        
def convert_error_bars_to_error_ratio_hist(h, direction=1):
    """Create hist with bin content = (bin value ± bin error) / bin value, 0 error"""
    h_new = h.Clone(h.GetName() + get_unique_str())
    for ix in range(1, h_new.GetNbinsX()+1):
        if h.GetBinContent(ix) > 0:
            h_new.SetBinContent(ix, 1+(direction*(h.GetBinError(ix) / h.GetBinContent(ix))))
        else:
            if h.GetBinContent(ix) < 0:
                h_new.SetBinContent(ix, 1+(direction*(h.GetBinError(ix) / h.GetBinContent(ix))))
                print("_convert_error_bars_to_error_ratio_hist() warning: bin %d content < 0!" % (ix))
            else:
                h_new.SetBinContent(ix, 1)
        h_new.SetBinError(ix, 0)
    return h_new

In [22]:
#Taken from Robin: https://github.com/raggleton/QGAnalysisPlotting/blob/26bb66e690a4a052b9b1acc328059a372fd25c6b/my_unfolder.py#L2358
def get_th1_bin_centers(h):
    # TODO maintain same shape(1, n) as in th1_to_array?
    centers = np.array([h.GetBinLowEdge(i) + 0.5*h.GetBinWidth(i) for i in range(1, h.GetNbinsX()+1)])
    return centers

def scale_th2_bin_widths(h2d, bins):
    """Scale bins of a square TH2 by bin widths
    bins is a list of bin edges, must have 1 more value than the number of bins in h2d
    """
    if len(bins) != h2d.GetNbinsX()+1:
        print(bins)
        print(h2d.GetNbinsX())
        raise ValueError("Wrong number of bins to scale x axis")
    if len(bins) != h2d.GetNbinsY()+1:
        raise ValueError("Wrong number of bins to scale y axis")
    for ix, (binx_low, binx_high) in enumerate(zip(bins[:-1], bins[1:]), 1):
        for iy, (biny_low, biny_high) in enumerate(zip(bins[:-1], bins[1:]), 1):
            width_x = binx_high - binx_low
            width_y = biny_high - biny_low
            scale = width_x * width_y
            value = h2d.GetBinContent(ix, iy)
            err = h2d.GetBinError(ix, iy)
            h2d.SetBinContent(ix, iy, value / scale)
            h2d.SetBinError(ix, iy, err / scale)
                
def get_th1_bin_widths(h):
    # TODO maintain same shape(1, n) as in th1_to_array?
    widths = np.array([h.GetBinWidth(i) for i in range(1, h.GetNbinsX()+1)])
    return widths
def get_unique_str():
    return ROOT.TUUID().AsString()
def ndarray_to_th1(nd_array, has_oflow_x=False, offset=0.5, bins=None):
    """Convert numpy ndarray row vector to TH1, with shape (1, nbins)
    Use has_oflow_x to include the under/overflow bins
    """
    nbinsx = nd_array.shape[1]
    nbins_hist = nbinsx
    if has_oflow_x:
        nbins_hist -= 2

    # need the 0.5 offset to match TUnfold
    if bins == None:
        h = ROOT.TH1F(get_unique_str(), "", nbins_hist, offset, nbins_hist+offset)
    else:
        if len(bins) != nbinsx+1:
            raise IndexError("len(bins) != nbinsx + 1")
        h = ROOT.TH1F(get_unique_str(), "", nbins_hist, bins)

    x_start = 1
    x_end = nbins_hist

    if has_oflow_x:
        x_start = 0
        x_end = nbins_hist+1

    for x_ind, ix in enumerate(range(x_start, x_end+1)):
        h.SetBinContent(ix, nd_array[0][x_ind])
        h.SetBinError(ix, math.sqrt(abs(nd_array[0][x_ind])))
        #FIXME how to do errors
    return h

def th1_to_ndarray(hist_A, oflow_x=False):
    """Convert TH1 to numpy ndarray"""
    ncol = hist_A.GetNbinsX()
    if oflow_x:
        ncol += 2

    # makes column vectors
    contents = np.zeros(shape=(1, ncol), dtype=np.float64)
    errors = np.zeros(shape=(1, ncol), dtype=np.float64)

    # Get ROOT indices to loop over
    x_start = 0 if oflow_x else 1
    x_end = hist_A.GetNbinsX()
    if oflow_x:
        x_end += 1

    # x_ind for numpy as always starts at 0
    # ix for ROOT
    for x_ind, ix in enumerate(range(x_start, x_end+1)):
        contents[0][x_ind] = hist_A.GetBinContent(ix)
        errors[0][x_ind] = hist_A.GetBinError(ix)

    # check sparsity
    return contents, errors

def th2_to_tmatrixd(hist, include_uflow=False, include_oflow=False):
    n_rows = hist.GetNbinsY()
    n_cols = hist.GetNbinsX()

    # ignore for now as too complicated
    # if include_uflow:
    #     n_rows += 1
    #     n_cols += 1
    # if include_oflow:
    #     n_rows += 1
    #     n_cols += 1

    # taken from https://root.cern.ch/doc/master/TH2_8cxx_source.html#l03739
    m = ROOT.TMatrixD(n_rows, n_cols)
    ilow = m.GetRowLwb()
    iup  = m.GetRowUpb()
    jlow = m.GetColLwb()
    jup  = m.GetColUpb()
    for i in range(ilow, iup+1):
        for j in range(jlow, jup+1):
            m[i,j] = hist.GetBinContent(j-jlow+1,i-ilow+1)
    return m

def th2_to_ndarray(hist_A, oflow_x=False, oflow_y=False):
    """Convert TH2 to numpy ndarray
    Don't use verison in common_utils - wrong axes?
    """
    ncol = hist_A.GetNbinsX()
    if oflow_x:
        ncol += 2
    nrow = hist_A.GetNbinsY()
    if oflow_y:
        nrow += 2

    contents = np.zeros(shape=(nrow, ncol), dtype=np.float64)
    errors = np.zeros(shape=(nrow, ncol), dtype=np.float64)
    # access via contents[irow][icol]

    # Get ROOT indices to loop over
    y_start = 0 if oflow_y else 1
    y_end = hist_A.GetNbinsY()
    if oflow_y:
        y_end += 1

    x_start = 0 if oflow_x else 1
    x_end = hist_A.GetNbinsX()
    if oflow_x:
        x_end += 1

    # y_ind, x_ind for numpy as always starts at 0
    # iy, ix for ROOT
    for y_ind, iy in enumerate(range(y_start, y_end+1)):
        for x_ind, ix in enumerate(range(x_start, x_end+1)):
            contents[y_ind][x_ind] = hist_A.GetBinContent(ix, iy)
            errors[y_ind][x_ind] = hist_A.GetBinError(ix, iy)

    return contents, errors


def ndarray_to_th2(data, offset=0, binsx=None, binsy=None):
    nbinsy, nbinsx = data.shape
    bins_x = array('d', [x+offset for x in range(1, nbinsx+2)]) # e.g. offset = -0.5 for TUnfold
    bins_y = array('d', [x+offset for x in range(1, nbinsy+2)])
    if binsx is not None:
        if len(binsx) != nbinsx+1:
            raise IndexError("binsx wrong size")
        bins_x = binsx
    if binsy is not None:
        if len(binsy) != nbinsy+1:
            raise IndexError("binsy wrong size")
        bins_y = binsy
    h = ROOT.TH2D(get_unique_str(), "", nbinsx, bins_x, nbinsy, bins_y)
    for ix in range(nbinsx):
        for iy in range(nbinsy):
            h.SetBinContent(ix+1, iy+1, data[iy,ix])
            h.SetBinError(ix+1, iy+1, 0)
    return h

def make_hist_from_diagonal_errors(h2d, do_sqrt=True, set_errors=True, offset=0.):
    """Make 1D hist, with errors or contents set to diagonal elements from h2d
    Can be TH2 or numpy.ndarray, cos we have to use both
    Yes that is majorly wack
    set_errors: True to set TH1 bin errors, otherwise sets bin contents
    offset is on bin edge from 0 (TUnfold is 0.5)
    """
    if isinstance(h2d, ROOT.TH2):
        nbins = h2d.GetNbinsX()
        hnew = ROOT.TH1D("h_diag" + get_unique_str(), "", nbins, offset, nbins+offset)
        for i in range(1, nbins+1):
            err = h2d.GetBinContent(i, i)
            if do_sqrt and err > 0:
                err = math.sqrt(err)
            if set_errors:
                hnew.SetBinContent(i, 0)
                hnew.SetBinError(i, err)
            else:
                hnew.SetBinContent(i, err)
                hnew.SetBinError(i, 0)
        return hnew
    elif isinstance(h2d, np.ndarray):
        nbins = h2d.shape[0]
        hnew = ROOT.TH1D("h_diag" + get_unique_str(), "", nbins, offset, nbins+offset)
        for i in range(1, nbins+1):
            err = h2d[i-1, i-1]
            if do_sqrt and err > 0:
                err = math.sqrt(err)
            if set_errors:
                hnew.SetBinContent(i, 0)
                hnew.SetBinError(i, err)
            else:
                hnew.SetBinContent(i, err)
                hnew.SetBinError(i, 0)
        return hnew

def update_hist_bin_error(h_orig, h_to_be_updated):
    """Change the errors in h_to_be_updated to those from h_orig"""
    if h_orig.GetNbinsX() != h_to_be_updated.GetNbinsX():
        raise RuntimeError("Need same # x bins, %d vs %s" % (h_orig.GetNbinsX(), h_to_be_updated.GetNbinsX()))
    for i in range(0, h_orig.GetNbinsX()+2):
        h_to_be_updated.SetBinError(i, h_orig.GetBinError(i))

def get_folded_unfolded(folded, unfolded, cov_tot, probaM):
    # don't use getfoldedoutput, because it doesn't have the updated errors from the total error matrix
    # so we'll have to do it ourselves
    # 1. Make unfolded hist into TVector/TMatrix

    # 2. Make response 2d hist into matrix

    # 3. Multiply the two, convert to TH1

    # Get the TUnfold one for reference, although its errors will be wrong
    
    probaM, _ = th2_to_ndarray(probaM)
    
    folded_unfolded_tunfold = folded

    oflow = False

    # Get unfolded results as array
    unfolded_vector, _ = th1_to_ndarray(unfolded, oflow)

    # Multiply
    # Note that we need to transpose from row vec to column vec
    folded_vec = probaM.dot(unfolded_vector.T)

    # Convert vector to TH1
    folded_unfolded = ndarray_to_th1(folded_vec.T, has_oflow_x=oflow, offset=0.)

    # Error propagation: if y = Ax, with covariance matrices Vyy and Vxx,
    # respectively, then Vyy = (A*Vxx)*A^T
    unfolded_covariance_matrix, _ = th2_to_ndarray(cov_tot , oflow_x=oflow, oflow_y=oflow)
    result = probaM.dot(unfolded_covariance_matrix)
    folded_covariance = result.dot(probaM.T)
    folded_errors = make_hist_from_diagonal_errors(folded_covariance)
    update_hist_bin_error(h_orig=folded_errors, h_to_be_updated=folded_unfolded)

    return folded_unfolded

In [23]:
def drawUnfold( ivar, selection, process, year, dataJetHisto, genJetHisto, unfoldHisto, unfoldHistowoUnc, altMCHisto,
               foldHisto, recoJetHisto, cov_tot, cov_datastat_tot, labelX, maxX, tlegendAlignment, outputName ):
    """docstring for drawUnfold"""
    #print ("Drawing unfolding")
    ROOT.gStyle.SetPadRightMargin(0.05)
    ROOT.gStyle.SetPadLeftMargin(0.15)
    can = ROOT.TCanvas('can'+ivar, 'can'+ivar,  10, 10, 1500, 1500 )
    pad1 = ROOT.TPad("pad1"+ivar, "Main",0,0.3,1.00,1.00,-1)
    pad1.Draw()

    pad1.cd()
    pad1.SetTopMargin(0.08)
    pad1.SetBottomMargin(0.02)
    
    if tlegendAlignment.startswith('right'): legend=ROOT.TLegend(0.65,0.67,0.90,0.9)

    else: legend=ROOT.TLegend(0.20,0.67,0.40,0.9)
    legend.SetFillStyle(0)
    legend.SetTextSize(0.035)
    legend.SetBorderSize(0)
    
    bins = variables[ivar]['bins']

    unfoldHistoTot = unfoldHisto.Clone()
    #print (unfoldHisto)
    #use unnormed unfold histo to build the jacobian for the correct propagation of errors
    #via the covariance matrix, from the normalise -> the unnormalised space
    normed_cov_tot_matrix, normed_cov_tot = GetNormalizedTMatrixandTH2(cov_tot.Clone(),"normed_cov_tot", unfoldHisto.Clone())
    
    normed_cov_datastat_tot_matrix, normed_cov_datastat_tot = GetNormalizedTMatrixandTH2(cov_datastat_tot.Clone(),"normed_cov_dastat_tot", unfoldHisto.Clone())
    '''
    normed_cov_bkgsub_tot_matrix, normed_cov_bkgsub_tot = GetNormalizedTMatrixandTH2(cov_bkg_tot.Clone(),
                                                                                     "normed_cov_tot",
                                                                                     unfoldHistoTotUnc)
    
    normed_cov_rmstat_tot_matrix, normed_cov_rmstat_tot = GetNormalizedTMatrixandTH2(cov_rmstat_tot.Clone(),
                                                                                     "normed_cov_rmstat_tot", 
                                                                                     unfoldHistoTotUnc)
    '''
    
    #print (unfoldHisto)

    
    unfoldHistoDataStatErr = normalise_hist(unfoldHisto.Clone())    
    unfoldHisto = normalise_hist(unfoldHisto.Clone())    
    dataJetHisto = normalise_hist(dataJetHisto.Clone())
    genJetHisto = normalise_hist(genJetHisto.Clone())
    unfoldHistowoUnc = normalise_hist_divide_bin_width(unfoldHistowoUnc.Clone())
    altMCHisto = normalise_hist(altMCHisto.Clone())
    foldHisto = normalise_hist(foldHisto.Clone())
    recoJetHisto = normalise_hist(recoJetHisto.Clone())
    #print (unfoldHisto)

    #norm = unfoldHistoTot.Integral("width")/unfoldHisto.Integral("width")
    
    #normed_cov_tot = cov_tot.Clone()
    #normed_cov_tot.Scale(1./(norm*norm))
    #scale_th2_bin_widths(normed_cov_tot, variables[ivar]['bins'])
    #normed_cov_datastat_tot = cov_datastat_tot.Clone()
    #normed_cov_datastat_tot.Scale(1./(norm*norm))
    #scale_th2_bin_widths(normed_cov_datastat_tot, variables[ivar]['bins'])   
                                                         
    
    
    for ibin in range(1, unfoldHisto.GetNbinsX()+1):
        tot_err = normed_cov_tot.GetBinContent(ibin,ibin)
        tot_datastaterr = normed_cov_datastat_tot.GetBinContent(ibin,ibin)
        
        if tot_err<=0.: tot_err=0.
        else: tot_err = np.sqrt(tot_err)
        
        if tot_datastaterr<=0.: tot_datastaterr=0.
        else: tot_datastaterr = np.sqrt(tot_datastaterr)    
        
        unfoldHisto.SetBinError(ibin,tot_err)
        unfoldHistoDataStatErr.SetBinError(ibin,tot_datastaterr)
            
        
    unfoldHistoDataStatErr.Scale(1,'width')
    #dataIntegral = dataJetHisto.Integral()
    #unfoldIntegral = unfoldHisto.Integral()
    #tmpMax = float(unfoldHisto.GetMaximum())
    
    unfoldHisto.Scale(1, 'width')  ### divide by bin width
    #unfoldHisto.Scale(1/unfoldHisto.Integral(), 'width')  ### divide by bin width
    unfoldHisto.SetMarkerStyle(8)
    unfoldHisto.SetMarkerSize(2)
    unfoldHisto.SetMarkerColor(ROOT.kBlack)
    unfoldHisto.SetLineColor(ROOT.kBlack)
    legend.AddEntry( unfoldHisto, 'Data', 'pe' )
    
    genJetHisto.Scale(1, 'width')
    #genJetHisto.Scale(scaleFactor)
    #genJetHisto.Scale(1/genJetHisto.Integral(), 'width')  ### divide by bin width
    genJetHisto.SetLineWidth(2)
    genJetHisto.SetLineColor(ROOT.kRed)
    genJetHisto.SetMarkerColor(ROOT.kRed)
    genJetHisto.SetMarkerStyle(25)
    legend.AddEntry( genJetHisto, 'MG5+Pythia8', 'lp' )

   

    unfoldHisto.GetYaxis().SetTitle( '#frac{1}{d#sigma} #frac{d#sigma}{d#'+labelX.split('#')[1]+'}' )
    #unfoldHisto.GetYaxis().SetTitleOffset(0.95)
    unfoldHisto.GetYaxis().SetTitleSize(0.05)
    unfoldHisto.SetMaximum( 1.6*max([ genJetHisto.GetMaximum(), unfoldHisto.GetMaximum()] )  )
    unfoldHisto.SetMinimum(0.)
    #pad1.GetYaxis().SetRangeUser(0,1.5*max([ genJetHisto.GetMaximum(), unfoldHisto.GetMaximum()] ) )

    unfoldHisto.Draw( "E")
    genJetHisto.Draw( "histe same")

    altMCHisto.Scale(1, 'width')  ### divide by bin width
    altMCHisto.SetLineWidth(2)
    altMCHisto.SetLineColor(ROOT.kBlue)
    altMCHisto.SetMarkerColor(ROOT.kBlue)
    altMCHisto.SetMarkerStyle(25)
    legend.AddEntry( altMCHisto, 'Herwig7', 'lp' )
    altMCHisto.Draw("histe same")
    #unfoldHistowoUnc.Draw( "e1 same")
    #foldHisto.Draw( "histe same")
    #if selfClosure: foldHisto.Draw( "histe same")
    #dataJetHisto.Draw( "histe same")
    #recoJetHisto.Draw( "histe same")
    #if process.startswith('data'): recoJetHisto.Draw( "hist same")
    
    selText = textBox.Clone()
    selText.SetTextFont(42)
    selText.SetTextSize(0.045)

    selText.SetNDC()

    if selection.startswith("_dijet"): seltext = ( 'Central' if 'Central' in labelX  else 'Outer' )+' dijet region'
    elif selection.startswith("_W"): seltext = 'Boosted W region'
    elif selection.startswith("_top"): seltext = 'Boosted top region'
    selText.DrawLatex( ( 0.21 if tlegendAlignment.startswith('right') else 0.55 ), 0.87, seltext )

    selText = textBox.Clone()
    selText.SetTextFont(42)
    selText.SetTextSize(0.042)

    selText.SetNDC()
    
    if selection.startswith("_dijet"): seltext = 'p_{T}>200 GeV' 
    elif selection.startswith("_W"): seltext = 'p_{T}>200 GeV, 65#leqm_{SD}<115 GeV' 
    elif selection.startswith("_top"): seltext = 'p_{T}>350 GeV, 140#leqm_{SD}<220 GeV'
    selText.DrawLatex( ( 0.21 if tlegendAlignment.startswith('right') else 0.55 ), 0.78, seltext )

    
    legend.Draw()
    if process.startswith('data'):
        CMS_lumi.extraText = "Preliminary"
        CMS_lumi.lumi_13TeV = ('#leq' if selection.startswith('dijet') else '')+str( round( (lumi/1000.), 2 ) )+" fb^{-1}, 13 TeV"+('' if year.startswith('all') else ", "+( '2017+2018' if year.startswith('all') else year ) )
    else:
        CMS_lumi.extraText = "Simulation Preliminary"
        CMS_lumi.lumi_13TeV = "13 TeV, "+ ( '2017+2018' if year.startswith('all') else year )
    CMS_lumi.relPosX = 0.12
    CMS_lumi.CMS_lumi(pad1, 4, 0)
    
    
    can.cd()
    pad2 = ROOT.TPad("pad2"+ivar, "Ratio",0,0.00,1.00,0.30,-1);
    ROOT.gStyle.SetOptFit(1)
    pad2.SetGrid()
    pad2.SetTopMargin(0.)
    pad2.SetBottomMargin(0.3)
    pad2.Draw()
    pad2.cd()
    
    ratio_datastatUnc = unfoldHistowoUnc.Clone()
    ratio_datastatUnc.Divide(unfoldHistoDataStatErr)
    #ratio_datastatUnc.Reset()
    ratio_totalUnc = unfoldHistowoUnc.Clone()
    ratio_totalUnc.Divide(unfoldHisto)
    #ratio_totalUnc.Reset()
    '''
    for ibin in range(0, unfoldHisto.GetNbinsX()):
        
        tot_err = unfoldHisto.GetBinError(ibin)
        tot_datastaterr = unfoldHistoDataStatErr.GetBinError(ibin)
        bc = unfoldHisto.GetBinContent(ibin)
        
        ratio_datastatUnc.SetBinContent(ibin,1.)
        ratio_totalUnc.SetBinContent(ibin,1.)
                                         
        if bc>0.:
            ratio_datastatUnc.SetBinError(ibin,tot_datastaterr/bc)
            ratio_totalUnc.SetBinError(ibin,tot_err/bc)
   
    '''
    tmpPad2= pad2.DrawFrame( 0, 0., maxX, 1.9 )
    print (labelX)
    #tmpPad2.GetXaxis().SetTitle( labelX )
    tmpPad2.GetYaxis().SetTitle( "Sim./Data" )
    tmpPad2.GetYaxis().SetTitleOffset( 0.5 )
    tmpPad2.GetYaxis().SetRangeUser(-1., 3. )
    tmpPad2.GetYaxis().CenterTitle()
    tmpPad2.SetLabelSize(0.12, 'x')
    tmpPad2.SetTitleSize(0.12, 'x')
    tmpPad2.SetLabelSize(0.12, 'y')
    tmpPad2.SetTitleSize(0.12, 'y')
    tmpPad2.SetNdivisions(505, 'x')
    tmpPad2.SetNdivisions(505, 'y')
    pad2.Modified()
    pad2.Update()
    pad2.Draw()
    can.Update()
    
    #hRatioDown.Draw('P same')
    ratio_datastatUnc.SetFillColor(ROOT.kAzure+7)
    ratio_datastatUnc.SetLineColor(0)
    ratio_datastatUnc.SetLineWidth(0)
    ratio_datastatUnc.SetFillStyle(3245)
    ratio_datastatUnc.GetXaxis().SetTitle( '#'+labelX.split('#')[1] )
    ratio_datastatUnc.GetYaxis().SetTitle( "Sim./Data" )
    ratio_datastatUnc.GetYaxis().SetTitleOffset( 0.5 )
    ratio_datastatUnc.GetYaxis().SetRangeUser(-1., 3. )
    ratio_datastatUnc.GetYaxis().CenterTitle()
    ratio_datastatUnc.GetXaxis().SetLabelSize(0.12)
    ratio_datastatUnc.GetXaxis().SetTitleSize(0.12)
    ratio_datastatUnc.GetYaxis().SetLabelSize(0.12)
    ratio_datastatUnc.GetYaxis().SetTitleSize(0.12)
    ratio_datastatUnc.GetXaxis().SetNdivisions(505)
    ratio_datastatUnc.GetYaxis().SetNdivisions(505)
    ratio_datastatUnc.SetMarkerStyle(0)
    ratio_datastatUnc.SetMarkerSize(0)
    #ratio_datastatUnc.Scale(1,'width')
    ratio_datastatUnc.Draw('E5')

    ratio_totalUnc.SetFillColor(ROOT.kGray+3)
    ratio_totalUnc.SetLineColor(0)
    ratio_totalUnc.SetLineWidth(0)
    ratio_totalUnc.SetFillStyle(3254)
    ratio_totalUnc.SetMarkerStyle(0)
    ratio_totalUnc.SetMarkerSize(0)
    #ratio_totalUnc.Scale(1,'width')    
    ratio_totalUnc.Draw('E5 SAME')
    
    #ratiosystUncHisto.SetFillColor(9)
    #ratiosystUncHisto.SetLineColor(0)
    #ratiosystUncHisto.SetFillStyle(3006)
    #ratiosystUncHisto.SetMarkerStyle(0)
    #ratiosystUncHisto.Scale(1,'width')    
    #ratiosystUncHisto.Draw('E3 same')

    hRatioUp = ROOT.TGraphAsymmErrors()
    hRatioUp.Divide( genJetHisto, unfoldHisto, 'pois' )
    hRatioUp.SetLineColor(ROOT.kRed)
    hRatioUp.SetMarkerColor(ROOT.kRed)
    #hRatioUp.SetLineWidth(2)
    hRatioUp.SetMarkerStyle(25)
    hRatioUp.Draw('P0 same')
    
    hRatioUp2 = ROOT.TGraphAsymmErrors()
    hRatioUp2.Divide( altMCHisto, unfoldHisto, 'pois' )
    hRatioUp2.SetLineColor(ROOT.kBlue)
    hRatioUp2.SetMarkerColor(ROOT.kBlue)
    #hRatioUp.SetLineWidth(2)
    hRatioUp2.SetMarkerStyle(25)
    hRatioUp2.Draw('P0 same')
    
    ratioLegend=ROOT.TLegend(0.20,0.85,0.80,0.95)
    ratioLegend.SetTextSize(0.095)
    ratioLegend.SetNColumns(3)
    ratioLegend.SetFillColorAlpha(10,0.6)
    ratioLegend.SetBorderSize(0)
    #ratioLegend.SetTextSize(0.1)
    ratioLegend.AddEntry( ratio_totalUnc, 'Data total unc.', 'f' )
    ratioLegend.AddEntry( ratio_datastatUnc, 'Data stat. unc.', 'f' )
    #ratioLegend.AddEntry( ratiosystUncHisto, 'Syst.', 'f' )
    ratioLegend.Draw()
    png = outputName.split('.pdf')[0]+'.png'
    can.SaveAs(outputName)
    can.SaveAs(png)
    ROOT.gStyle.SetPadRightMargin(0.09)     ## reseating
    ROOT.gStyle.SetPadLeftMargin(0.12)

In [24]:
def normaliseUncs(systs):
    return 1

In [25]:
def drawUncertainties(ivar, unfoldHistoTotUnc,
                      uncerUnfoldHisto, cov_tot, cov_datastat_tot, cov_rmstat_tot, cov_bkg_tot,
                      labelX, tlegendAlignment, outputName,year,unftot ):
    """docstring for drawUncUncertainties"""
    
    #Draw fractional uncertainties for all sources of systematics and statical errors
    #Systematics are obtained from the total of up/down shifts normalized per bin by the nominal unfolded 
    #histos respective bins'contents, this is with the exception of the bkg_tot_err and RM_staterr which are obtained 
    #from the variances (diagonal of the respective cov. matrix) and then normalized
    #Stat errors are obtained from the diagonals of the respective covariance matrices provided by TUnfold and normalized
    
    normed_cov_tot_matrix, normed_cov_tot = GetNormalizedTMatrixandTH2(cov_tot.Clone(),"normed_cov_tot", 
                                                                       unfoldHistoTotUnc.Clone())
    
    normed_cov_datastat_tot_matrix, normed_cov_datastat_tot = GetNormalizedTMatrixandTH2(cov_datastat_tot.Clone(),
                                                                                         "normed_cov_dastat_tot", 
                                                                                          unfoldHistoTotUnc.Clone())
   
    normed_cov_bkgsub_tot_matrix, normed_cov_bkgsub_tot = GetNormalizedTMatrixandTH2(cov_bkg_tot.Clone(),
                                                                                     "normed_cov_tot",
                                                                                     unfoldHistoTotUnc.Clone())
    
    normed_cov_rmstat_tot_matrix, normed_cov_rmstat_tot = GetNormalizedTMatrixandTH2(cov_rmstat_tot.Clone(),
                                                                                     "normed_cov_rmstat_tot", 
                                                                                     unfoldHistoTotUnc.Clone())
   
    
    unfoldHistoNoNorm=unfoldHistoTotUnc.Clone()
    
    unfoldHistoDataStatUnc=unfoldHistoTotUnc.Clone()
    unfoldHistoRMStatUnc=unfoldHistoTotUnc.Clone()
    unfoldHistoBkgSubUnc=unfoldHistoTotUnc.Clone()
    
    unfoldHistoTotUnc = normalise_hist_divide_bin_width(unfoldHistoTotUnc.Clone())
    unfoldHistoDataStatUnc = normalise_hist_divide_bin_width(unfoldHistoDataStatUnc.Clone())
    unfoldHistoRMStatUnc = normalise_hist_divide_bin_width(unfoldHistoRMStatUnc.Clone())
    unfoldHistoBkgSubUnc = normalise_hist_divide_bin_width(unfoldHistoBkgSubUnc.Clone())
    
    scale_th2_bin_widths(normed_cov_tot_matrix)
    scale_th2_bin_widths(normed_cov_datastat_tot_matrix)
    scale_th2_bin_widths(normed_cov_bkgsub_tot_matrix)
    scale_th2_bin_widths(normed_cov_rmstat_tot_matrix)
    
    for ibin in range(1, unfoldHistoNoNorm.GetNbinsX()+1):
        tot_err = normed_cov_tot.GetBinContent(ibin,ibin)
        tot_datastaterr = normed_cov_datastat_tot.GetBinContent(ibin,ibin)
        tot_rmstaterr = normed_cov_rmstat_tot.GetBinContent(ibin,ibin)
        tot_bkgsuberr = normed_cov_bkgsub_tot.GetBinContent(ibin,ibin)
        
        if tot_err<=0.: tot_err=0.
        else: tot_err = np.sqrt(tot_err)
        
        if tot_datastaterr<=0.: tot_datastaterr=0.
        else: tot_datastaterr = np.sqrt(tot_datastaterr)    
     
        if tot_rmstaterr<=0.: tot_rmstaterr=0.
        else: tot_rmstaterr = np.sqrt(tot_rmstaterr)
        
        if tot_bkgsuberr<=0.: tot_bkgsuberr=0.
        else: tot_bkgsuberr = np.sqrt(tot_bkgsuberr)
        
        unfoldHistoTotUnc.SetBinError(ibin,tot_err)
        unfoldHistoDataStatUnc.SetBinError(ibin,tot_datastaterr)
        unfoldHistoRMStatUnc.SetBinError(ibin,tot_datastaterr)
        unfoldHistoBkgSubUnc.SetBinError(ibin,tot_bkgsuberr)
        
        
    #unfoldHistoNoNorm.Scale(1,'width')
    #unfoldHistoTotUnc.Scale(1,'width')
    #unfoldHistoDataStatUnc.Scale(1,'width')
    #unfoldHistoRMStatUnc.Scale(1,'width')
    #unfoldHistoBkgSubUnc.Scale(1,'width')
    
    colors = [ 2, 3, 4, 6, 7, 8, 9, 50, 205, 225, 94, 221, 92, 16, 28, 219, 225, 128,]
    ROOT.gStyle.SetPadRightMargin(0.05)
    ROOT.gStyle.SetPadLeftMargin(0.15)
    canUnc = ROOT.TCanvas('canUnc'+ivar, 'canUnc'+ivar,  10, 10, 750, 500 )
    
    if tlegendAlignment.startswith('right'): legend=ROOT.TLegend(0.65,0.7,0.90,0.92)
    else: legend=ROOT.TLegend(0.20,0.7,0.40,0.92)
    legend.SetFillStyle(0)
    legend.SetNColumns(2)
    legend.SetTextSize(0.02)
    legend.SetBorderSize(0)
    
    totalErrHist = unfoldHistoTotUnc.Clone()
    totalErrHist.Reset()
    dataStatErrHist = unfoldHistoDataStatUnc.Clone()
    dataStatErrHist.Reset()
    rmStatErrHist = unfoldHistoRMStatUnc.Clone()
    rmStatErrHist.Reset()
    bkgSubErrHist = unfoldHistoTotUnc.Clone()
    bkgSubErrHist.Reset()
    
    
    
    #print (uncerUnfoldHisto)
    
    #print (uncerUnfoldHisto.keys())
    normeduncerUnfoldHisto = OrderedDict()
    for k in uncerUnfoldHisto:
        if ('Total'in k ) and not k.endswith(('TotalUnc', 'SystTotal', 'StatTotal')) and not 'CM' in k:
            
            normeduncerUnfoldHisto[k]=uncerUnfoldHisto[k].Clone()
            #normeduncerUnfoldHisto[k].Scale(1,'width')
            #normeduncerUnfoldHisto[k].Divide(unfoldHistoTotUnc)
            for i in range(1,normeduncerUnfoldHisto[k].GetNbinsX()+1):
                if unfoldHistoNoNorm.GetBinContent(i)>0.:
                    if unfoldHistoTotUnc.GetBinContent(i)>0: 
                        perbin_scale = 1.0/(unfoldHistoNoNorm.GetBinContent(i)/unfoldHistoTotUnc.GetBinContent(i))
                    else: perbin_scale = 0
                    normeduncerUnfoldHisto[k].SetBinContent(i, 
                                                            normeduncerUnfoldHisto[k].GetBinContent(i)*perbin_scale)

    
            
            text = k.split('_')[-1].split('Total')[0].replace('TOTAL', '').replace('WEIGHT', '')
            if text.startswith(('ISR', 'FSR', 'JER', 'PU', 'PDF', 'Bkg')):
                uncerUnfoldHisto[k].SetLineStyle(2)
            uncerUnfoldHisto[k].SetLineColor(colors[dummy])
            uncerUnfoldHisto[k].SetLineWidth(2)
            #uncerUnfoldHisto[k].Scale( uncScaleFactor )
            uncerUnfoldHisto[k].Draw("hist same")
            if not 'damp' in k: legend.AddEntry( uncerUnfoldHisto[k], k.split('_')[-1].split('Total')[0].replace('TOTAL', '').replace('WEIGHT', ''), 'l' )
            else: legend.AddEntry( uncerUnfoldHisto[k], 'h_{damp}', 'l' )
            dummy=dummy+1
            
        
    #get fractionals for stat and total errors
    for i in range(1,dataStatErrHist.GetNbinsX()+1):
    
        if unfoldHistoTotUnc.GetBinContent(i)>0.:
            dataStatErrHist.SetBinContent(i,unfoldHistoDataStatUnc.GetBinError(i)/unfoldHistoTotUnc.GetBinContent(i))
            rmStatErrHist.SetBinContent(i,unfoldHistoRMStatUnc.GetBinError(i)/unfoldHistoTotUnc.GetBinContent(i))
            bkgSubErrHist.SetBinContent(i,unfoldHistoBkgSubUnc.GetBinError(i)/unfoldHistoTotUnc.GetBinContent(i))
            totalErrHist.SetBinContent(i,unfoldHistoTotUnc.GetBinError(i)/unfoldHistoTotUnc.GetBinContent(i))
        else:
            dataStatErrHist.SetBinContent(i,0)
            rmStatErrHist.SetBinContent(i,0)
            bkgSubErrHist.SetBinContent(i,0)
            totalErrHist.SetBinContent(i,0)
            
        dataStatErrHist.SetBinError(i,0)
        rmStatErrHist.SetBinError(i,0)
        bkgSubErrHist.SetBinError(i,0)
        totalErrHist.SetBinError(i,0)
            
    
    
    dataStatErrHist.SetLineWidth(2)
    dataStatErrHist.SetLineStyle(3)
    #dataStatErrHist.Scale( uncScaleFactor )
    dataStatErrHist.GetXaxis().SetTitle(labelX)
    dataStatErrHist.GetYaxis().SetTitle('Relative Uncertainty')
    dataStatErrHist.SetMaximum(5)
    dataStatErrHist.GetYaxis().SetRangeUser(5*(10**(-5)),15)
    dataStatErrHist.SetLineColor(88)
    dataStatErrHist.Draw('hist ')
    
    rmStatErrHist.SetLineWidth(2)
    rmStatErrHist.SetLineStyle(3)
    #dataStatErrHist.Scale( uncScaleFactor )
    #rmStatErrHist.GetXaxis().SetTitle(labelX)
    #rmStatErrHist.GetYaxis().SetTitle('Relative Uncertainty')
    #rmStatErrHist.SetMaximum(5)
    #rmStatErrHist.GetYaxis().SetRangeUser(5*(10**(-4)),8)
    rmStatErrHist.SetLineColor(209)
    rmStatErrHist.Draw('hist same ')
    
    bkgSubErrHist.SetLineWidth(2)
    bkgSubErrHist.SetLineStyle(3)
    #dataStatErrHist.Scale( uncScaleFactor )
    #rmStatErrHist.GetXaxis().SetTitle(labelX)
    #rmStatErrHist.GetYaxis().SetTitle('Relative Uncertainty')
    #rmStatErrHist.SetMaximum(5)
    #rmStatErrHist.GetYaxis().SetRangeUser(5*(10**(-4)),8)
    bkgSubErrHist.SetLineColor(ROOT.kMagenta-4)
    bkgSubErrHist.Draw('hist same ')
    
    
    dummy=0
    #print (uncerUnfoldHisto.keys())
    
    for k in normeduncerUnfoldHisto:
        if ('Total'in k ) and not k.endswith(('TotalUnc', 'SystTotal', 'StatTotal')) and not 'Bkg' in k and not 'CM' in k and not 'jes' in k and not 'JES' in k:
            text = k.split('_')[-1].split('Total')[0].replace('TOTAL', '').replace('WEIGHT', '')
            if text.startswith(('ISR', 'FSR', 'JER', 'PU', 'PDF', 'Bkg')):
                normeduncerUnfoldHisto[k].SetLineStyle(2)
            normeduncerUnfoldHisto[k].SetLineColor(colors[dummy])
            normeduncerUnfoldHisto[k].SetLineWidth(2)
            #uncerUnfoldHisto[k].Scale( uncScaleFactor )
            normeduncerUnfoldHisto[k].Draw("hist same")
            if not 'damp' in k: legend.AddEntry( normeduncerUnfoldHisto[k], k.split('_')[-1].split('Total')[0].replace('TOTAL', '').replace('WEIGHT', ''), 'l' )
            else: legend.AddEntry( normeduncerUnfoldHisto[k], 'h_{damp}', 'l' )
            dummy=dummy+1
    #print ("adding jeshisto values")
    
    
    jesHisto.SetLineStyle(5)
    jesHisto.SetLineColor(colors[dummy])
    jesHisto.SetLineWidth(2)
    #jesHisto.Scale( uncScaleFactor )
    legend.AddEntry(jesHisto, 'JESMerged','l')
    jesHisto.Draw("hist same")
    
    
    '''
    #uncScaleFactor = 1./totalErrHist.Integral()
    for k in uncerUnfoldHisto:
        for i in range(0,unfoldHistoTotUnc.GetNbinsX()+1):
            if ('Total' in k) and unfoldHistoTotUnc.GetBinContent(i)>0.0000000000000000000000000001:
                uncerUnfoldHisto[k].SetBinContent(i, uncerUnfoldHisto[k].GetBinContent(i)/unfoldHistoTotUnc.GetBinContent(i) )
    #print ("unc. scale factor", uncScaleFactor)

    '''
    
    
    
    
    
    
    
    totalErrHist.SetLineWidth(3)
    totalErrHist.SetLineStyle(2)
    #totalErrHist.Scale( uncScaleFactor )
    #totalErrHist.GetXaxis().SetTitle(labelX)
    #totalErrHist.GetYaxis().SetTitle('Fractional Uncertainty')
    totalErrHist.SetMarkerStyle(4)
    totalErrHist.SetLineColor(1)
    #totalErrHist.GetYaxis().SetRangeUser(5*(10**(-4)),5)
    legend.AddEntry( rmStatErrHist, 'Bkg. Sub. Unc.', 'l' )    
    legend.AddEntry( dataStatErrHist, 'Data Stat. Unc.', 'l' )    
    legend.AddEntry( rmStatErrHist, 'RM Stat. Unc.', 'l' )    
    
    legend.AddEntry( totalErrHist, 'Total Unc.', 'l' )   
    
    totalErrHist.Draw('hist same')
    
    
    
    #uncerUnfoldHisto[ivar+'_SystTotal'].SetLineWidth(2)
    #uncerUnfoldHisto[ivar+'_SystTotal'].SetLineStyle(2)
    #uncerUnfoldHisto[ivar+'_SystTotal'].Scale( uncScaleFactor )
    #uncerUnfoldHisto[ivar+'_SystTotal'].SetLineColor(209)
    #legend.AddEntry( uncerUnfoldHisto[ivar+'_SystTotal'], 'Syst. Tot.', 'l' )    
    #uncerUnfoldHisto[ivar+'_SystTotal'].Draw('hist same')
    
    
    
    legend.Draw()
    CMS_lumi.extraText = "Preliminary"
    CMS_lumi.lumi_13TeV = "13 TeV, "+ ( '2017+2018' if year.startswith('all') else year )
    CMS_lumi.relPosX = 0.11
    CMS_lumi.CMS_lumi(canUnc, 4, 0)
    canUnc.SetLogy()
    canUnc.Update()

    canUnc.SaveAs(outputName)
    
    

In [26]:
def drawUncertainties_normalizedshifts(ivar, unfoldHistoTotUnc, unfoldHistowoUnc,
                      uncerUnfoldHisto, cov_tot, cov_datastat_tot, cov_rmstat_tot, cov_bkg_tot,
                      labelX, tlegendAlignment, outputName,year,unftot ):
    """docstring for drawUncUncertainties"""
    #outputRoot = ROOT.TFile.Open( 'draw_unc'+ivar+'.root', 'recreate' )

    #Absolute shifts on the sbolute unfolded distribution are first created
    #this distribtuion is normalized taking into account the bin widths as for the nominal 
   
    colors = [ 95, 38, 6, 7, 8, 42, 50, 218, 225, 30, 16, 198, 190, 83, 167, 207, 209, 212, 216, 51, 61, 67, 89, 133, 142, 208, 36, 2, 144, 225, 227, 150]
    ROOT.gStyle.SetPadRightMargin(0.05)
    ROOT.gStyle.SetPadLeftMargin(0.15)
    canUnc = ROOT.TCanvas('canUnc'+ivar, 'canUnc'+ivar,  10, 10, 1500, 1000 )
    canUnc.SetTopMargin(0.08)
    #canUnc.SetBottomMargin(0.02)
    
    
    if tlegendAlignment.startswith('right'): legend=ROOT.TLegend(0.20,0.65,0.55,0.9)
    else: legend=ROOT.TLegend(0.55,0.65,0.9,0.9)
    legend.SetFillStyle(0)
    legend.SetNColumns(2)
    legend.SetTextSize(0.03)
    legend.SetBorderSize(0)
    
    unfoldHistoNoNorm=unfoldHistoTotUnc.Clone()
    unfoldHistoDataStatUnc=unfoldHistoTotUnc.Clone()
    unfoldHistoRMStatUnc=unfoldHistoTotUnc.Clone()
    unfoldHistoBkgSubUnc=unfoldHistoTotUnc.Clone()
    
    unfoldHistowoUnc = normalise_hist(unfoldHistoNoNorm.Clone())
    unfoldHistoTotUnc = normalise_hist(unfoldHistoNoNorm.Clone())
    unfoldHistoDataStatUnc = normalise_hist(unfoldHistoDataStatUnc.Clone())
    unfoldHistoRMStatUnc = normalise_hist(unfoldHistoRMStatUnc.Clone())
    unfoldHistoBkgSubUnc = normalise_hist(unfoldHistoBkgSubUnc.Clone())

    unfoldHistoNoNorm.Sumw2()
    unfoldHistoTotUnc.Sumw2()
    unfoldHistoDataStatUnc.Sumw2()
    unfoldHistoRMStatUnc.Sumw2()
    unfoldHistoBkgSubUnc.Sumw2()
    unfoldHistowoUnc.Sumw2()
    
    cov_tot.Sumw2()
    cov_datastat_tot.Sumw2()
    cov_bkg_tot.Sumw2()
    cov_rmstat_tot.Sumw2()
    
    normed_cov_tot_matrix, normed_cov_tot = GetNormalizedTMatrixandTH2(cov_tot.Clone(),"normed_cov_tot", 
                                                                       unfoldHistoNoNorm.Clone())
    
    normed_cov_datastat_tot_matrix, normed_cov_datastat_tot = GetNormalizedTMatrixandTH2(cov_datastat_tot.Clone(),
                                                                                         "normed_cov_dastat_tot", 
                                                                                          unfoldHistoNoNorm.Clone())
   
    normed_cov_bkgsub_tot_matrix, normed_cov_bkgsub_tot = GetNormalizedTMatrixandTH2(cov_bkg_tot.Clone(),
                                                                                     "normed_cov_tot",
                                                                                     unfoldHistoNoNorm.Clone())
    
    normed_cov_rmstat_tot_matrix, normed_cov_rmstat_tot = GetNormalizedTMatrixandTH2(cov_rmstat_tot.Clone(),
                                                                                     "normed_cov_rmstat_tot", 
                                                                                     unfoldHistoNoNorm.Clone())
    #add errors now to unf. histo without dealing with bins divided by width
    #then ask root to handle that part of it for you
    
     
    for ibin in range(1, unfoldHistoNoNorm.GetNbinsX()+1):
        tot_err = normed_cov_tot.GetBinContent(ibin,ibin)
        tot_datastaterr = normed_cov_datastat_tot.GetBinContent(ibin,ibin)
        tot_rmstaterr = normed_cov_rmstat_tot.GetBinContent(ibin,ibin)
        tot_bkgsuberr = normed_cov_bkgsub_tot.GetBinContent(ibin,ibin)
        
        if tot_err<=0.: tot_err=0.
        else: tot_err = np.sqrt(tot_err)
        
        if tot_datastaterr<=0.: tot_datastaterr=0.
        else: tot_datastaterr = np.sqrt(tot_datastaterr)    
     
        if tot_rmstaterr<=0.: tot_rmstaterr=0.
        else: tot_rmstaterr = np.sqrt(tot_rmstaterr)
        
        if tot_bkgsuberr<=0.: tot_bkgsuberr=0.
        else: tot_bkgsuberr = np.sqrt(tot_bkgsuberr)
        
        unfoldHistoTotUnc.SetBinError(ibin,tot_err)
        unfoldHistoDataStatUnc.SetBinError(ibin,tot_datastaterr)
        unfoldHistoRMStatUnc.SetBinError(ibin,tot_rmstaterr)
        unfoldHistoBkgSubUnc.SetBinError(ibin,tot_bkgsuberr)
    
    unfoldHistowoUnc.Scale(1, 'width')
    unfoldHistoNoNorm.Scale(1,'width')
    unfoldHistoTotUnc.Scale(1,'width')
    unfoldHistoDataStatUnc.Scale(1,'width')
    unfoldHistoRMStatUnc.Scale(1,'width')
    unfoldHistoBkgSubUnc.Scale(1,'width')
    
    dummy=0
    dummy_jes=0
    
    normeduncerUnfoldHistoshiftsUp = OrderedDict()
    normeduncerUnfoldHistoshiftsDown = OrderedDict()
    otherUncs = OrderedDict()
    
    up_counter=0
    down_counter=0
    
    upstyles=[20,22,21,23,29,34,47,33,43,39,41,]
    downstyles=[24,26,25,32,30,28,46,27,42,37,40]
    
    
    jesHistoUpMax = unfoldHistoTotUnc.Clone()
    jesHistoUpMax.Reset()
    jesHistoDownMax = unfoldHistoTotUnc.Clone()
    jesHistoDownMax.Reset()
    
    jesHistoUpMax.Sumw2()
    jesHistoDownMax.Sumw2()
    
    for k in uncerUnfoldHisto:
        text = (k.split('_shifthist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
        text=text.upper()
        if 'crtotal' in text.lower() or 'model' in text.lower(): continue
        if ('_shifthist'in k.lower() and 'up' in k.lower()):# and not k.endswith(('TotalUnc', 'SystTotal', 'StatTotal')) and not 'CM' in k:

            normeduncerUnfoldHistoshiftsUp[k] = uncerUnfoldHisto[k].Clone()
            normeduncerUnfoldHistoshiftsUp[k].Sumw2()
            normeduncerUnfoldHistoshiftsUp[k] = normalise_hist(normeduncerUnfoldHistoshiftsUp[k].Clone())
            normeduncerUnfoldHistoshiftsUp[k].Scale(1,'width')
            normeduncerUnfoldHistoshiftsUp[k] = convert_syst_shift_to_error_ratio_hist(normeduncerUnfoldHistoshiftsUp[k].Clone(),                            
                                                                                       unfoldHistoTotUnc.Clone())
            
            if 'ISR' in text or 'FSR' in text or 'JER' in text or ('PU' in text and 'DAMP' not in text) or 'PDF' in text:
                normeduncerUnfoldHistoshiftsUp[k].SetLineStyle(2)
                normeduncerUnfoldHistoshiftsUp[k].SetLineColor(colors[dummy])
                normeduncerUnfoldHistoshiftsUp[k].SetMarkerColor(colors[dummy])
                normeduncerUnfoldHistoshiftsUp[k].SetMarkerSize(2)
                normeduncerUnfoldHistoshiftsUp[k].SetMarkerStyle(upstyles[up_counter])
                #print (k,text, upstyles[up_counter], up_counter, dummy)
                dummy=dummy+1    
                up_counter=up_counter+1
            elif 'DAMP' in text or 'MTOP' in text:
                normeduncerUnfoldHistoshiftsUp[k].SetLineStyle(3)
                normeduncerUnfoldHistoshiftsUp[k].SetLineColor(colors[dummy])
                normeduncerUnfoldHistoshiftsUp[k].SetMarkerColor(colors[dummy])
                normeduncerUnfoldHistoshiftsUp[k].SetMarkerSize(2)
                normeduncerUnfoldHistoshiftsUp[k].SetMarkerStyle(upstyles[up_counter])
                #print (k,text, upstyles[up_counter], up_counter, dummy)
                dummy=dummy+1    
                up_counter=up_counter+1
    dummy=0
    
    for k in uncerUnfoldHisto:
        text = (k.split('_shifthist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
        text=text.upper()
        if 'crtotal' in text.lower() or 'model' in text.lower(): continue
        if ('_shifthist' in k.lower() and 'down' in k.lower()):
            
            normeduncerUnfoldHistoshiftsDown[k] = uncerUnfoldHisto[k].Clone()
            normeduncerUnfoldHistoshiftsDown[k].Sumw2()
            normeduncerUnfoldHistoshiftsDown[k] = normalise_hist(normeduncerUnfoldHistoshiftsDown[k].Clone())
            normeduncerUnfoldHistoshiftsDown[k].Scale(1,'width')
            normeduncerUnfoldHistoshiftsDown[k] = convert_syst_shift_to_error_ratio_hist(normeduncerUnfoldHistoshiftsDown[k].Clone(),
                                                                                         unfoldHistoTotUnc.Clone())
              
            if 'ISR' in text or 'FSR' in text or 'JER' in text or ('PU' in text and 'DAMP' not in text) or 'PDF' in text:
                normeduncerUnfoldHistoshiftsDown[k].SetLineStyle(2)
                normeduncerUnfoldHistoshiftsDown[k].SetLineColor(colors[dummy])
                normeduncerUnfoldHistoshiftsDown[k].SetMarkerColor(colors[dummy])
                normeduncerUnfoldHistoshiftsDown[k].SetMarkerSize(2)
                normeduncerUnfoldHistoshiftsDown[k].SetMarkerStyle(downstyles[down_counter])
                #print (k,text, downstyles[down_counter], down_counter, dummy)
                down_counter=down_counter+1
                dummy=dummy+1 
            elif 'DAMP' in text or 'MTOP' in text:
                normeduncerUnfoldHistoshiftsDown[k].SetLineStyle(3)
                normeduncerUnfoldHistoshiftsDown[k].SetLineColor(colors[dummy])
                normeduncerUnfoldHistoshiftsDown[k].SetMarkerColor(colors[dummy])
                normeduncerUnfoldHistoshiftsDown[k].SetMarkerSize(2)
                normeduncerUnfoldHistoshiftsDown[k].SetMarkerStyle(downstyles[down_counter])
                #print (k,text, downstyles[down_counter], down_counter, dummy)
                down_counter=down_counter+1
                dummy=dummy+1 

    dummy = dummy+2
    modelkey = 0
    '''
    cr_maxup = unfoldHistoTotUnc.Clone()
    cr_maxup.Reset()
    cr_maxdown = unfoldHistoTotUnc.Clone()
    cr_maxdown.Reset()
    
    cr_histos = OrderedDict()
    
    for k in uncerUnfoldHisto:
        text = (k.split('_shifthist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
        #print (text, dummy)
        if ('cr1' in text.lower() or 'cr2' in text.lower() or 'erd' in text.lower()) and '_shifthist' in k.lower():
            #print (text, dummy, k)
            cr_histos[k] = uncerUnfoldHisto[k].Clone()
            cr_histos[k].Sumw2()
            cr_histos[k] = normalise_hist(cr_histos[k].Clone())
            cr_histos[k].Scale(1,'width')
            cr_histos[k] = convert_syst_shift_to_error_ratio_hist(cr_histos[k].Clone(),
                                                                  unfoldHistoTotUnc.Clone())
    '''
    
    for ibin in range(1,unfoldHistoTotUnc.GetNbinsX()+1):
        #cr_maxup.SetBinContent(ibin,1.)
        #cr_maxdown.SetBinContent(ibin,1.)
        #upmax_ibin = 1
        #downmax_ibin = 1
        
        for k in uncerUnfoldHisto:
            text = (k.split('_shifthist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
            #print (text, dummy)
            if 'model'in k.lower(): modelkey=k
            '''
            if ('cr1' in text.lower() or 'cr2' in text.lower() or 'erd' in text.lower()) and '_shifthist' in k.lower():
                #print (text, dummy, k)
                
                if upmax_ibin<cr_histos[k].GetBinContent(ibin):
                    upmax_ibin=cr_histos[k].GetBinContent(ibin)
                if downmax_ibin>cr_histos[k].GetBinContent(ibin):
                    downmax_ibin=cr_histos[k].GetBinContent(ibin)
               
                
                otherUncs[k] = uncerUnfoldHisto[k].Clone()
                otherUncs[k].Sumw2()
                otherUncs[k] = normalise_hist(otherUncs[k].Clone())
                otherUncs[k].Scale(1,'width')
                otherUncs[k].Divide(unfoldHistowoUnc.Clone())# = convert_syst_shift_to_error_ratio_hist(otherUncs[k].Clone(), unfoldHistoTotUnc.Clone())
                
                #if 'model'in text.lower(): legend.AddEntry( otherUncs[k], 'Physics Model', 'l' )
                #elif 'mass'in text.lower(): legend.AddEntry( otherUncs[k], 'Choice of m_{top}', 'l' )
                if 'cr1' in text.lower(): legend.AddEntry( otherUncs[k], 'CR1', 'l' )
                elif 'cr2' in text.lower(): legend.AddEntry( otherUncs[k], 'CR2', 'l' )
                elif 'erdon' in text.lower(): legend.AddEntry( otherUncs[k], 'erdOn', 'l' )
                dummy = dummy+1
                
            #print (upmax_ibin,downmax_ibin)
            cr_maxup.SetBinContent(ibin,upmax_ibin)
            cr_maxdown.SetBinContent(ibin,downmax_ibin)
            '''        
    #print ("OtherUncs", otherUncs)
    modelUnc = uncerUnfoldHisto[modelkey].Clone()
    modelUnc.Sumw2()
    modelUnc = normalise_hist(modelUnc.Clone())
    modelUnc.Scale(1,'width')
    modelUnc = convert_syst_shift_to_error_ratio_hist(modelUnc.Clone(), unfoldHistoTotUnc.Clone())
    modelUnc.SetLineStyle(1)
    modelUnc.SetLineWidth(1)
    modelUnc.SetMarkerSize(0)
    modelUnc.SetLineColor(colors[dummy])
    modelUnc.SetFillColor(0)

               
                
    dataStatErrHist = unfoldHistoDataStatUnc.Clone()
    dataStatErrHist.Sumw2()
    dataStatErrHist.Divide(unfoldHistowoUnc)
    rmStatErrHist = unfoldHistoRMStatUnc.Clone()
    rmStatErrHist.Sumw2()
    bkgSubErrHist = unfoldHistoBkgSubUnc.Clone()
    bkgSubErrHist.Sumw2()
    totalErrHist = unfoldHistoTotUnc.Clone()
    totalErrHist.Sumw2()
    totalErrHist.Divide(unfoldHistowoUnc)
    
    totalErrHist.SetLineWidth(0)
    totalErrHist.GetYaxis().SetTitle('Variation/nominal')
    totalErrHist.GetYaxis().SetTitleSize(0.05)
    totalErrHist.GetYaxis().SetRangeUser(-0.5,2.5)
    totalErrHist.GetXaxis().SetTitle('#'+labelX.split('#')[1])
    totalErrHist.SetLineStyle(2)
    totalErrHist.SetFillColor(ROOT.kGray+3)
    totalErrHist.SetMarkerSize(0)
    totalErrHist.SetFillStyle(3154)
    totalErrHist.SetLineColor(1)
    totalErrHist.Draw(' E5')
    
    dataStatErrHist.SetLineWidth(0)
    dataStatErrHist.SetLineStyle(3)
    dataStatErrHist.SetMarkerSize(0)
    dataStatErrHist.SetFillStyle(3245)
    dataStatErrHist.SetFillColor(ROOT.kAzure+7)
    dataStatErrHist.SetLineColor(88)
    dataStatErrHist.Draw('E5 same')
    
    '''
    ###CR unc
    
    cr_maxup.SetLineColor(208)
    cr_maxdown.SetLineColor(208)
    cr_maxup.SetMarkerColor(208)
    cr_maxdown.SetMarkerColor(208)
    cr_maxup.SetMarkerStyle(upstyles[up_counter])
    cr_maxdown.SetMarkerStyle(downstyles[down_counter])
    cr_maxup.SetMarkerSize(2)
    cr_maxdown.SetMarkerSize(2)
    print (up_counter,down_counter)
    
    cr_maxup.SetMarkerSize(2)
    cr_maxdown.SetMarkerSize(2)
    cr_maxup.Draw('P same')
    cr_maxdown.Draw('P same')
    up_counter=up_counter+1
    down_counter=down_counter+1
    print (up_counter,down_counter)
    '''
    h1 = convert_error_bars_to_error_ratio_hist(rmStatErrHist.Clone(),-1)
    rmStatErrHist = convert_error_bars_to_error_ratio_hist(rmStatErrHist.Clone(),1)

    rmStatErrHist.SetLineWidth(2)
    h1.SetLineWidth(2)
    rmStatErrHist.SetLineStyle(9)
    h1.SetLineStyle(9)
    h1.SetLineColor(1)
    rmStatErrHist.SetLineColor(1)
    h1.SetMarkerSize(0)
    rmStatErrHist.SetMarkerSize(0)
    rmStatErrHist.Draw('L same ')
    h1.Draw("L same")
    #h.Delete()
    
    h2 = convert_error_bars_to_error_ratio_hist(bkgSubErrHist.Clone(),-1)
    bkgSubErrHist = convert_error_bars_to_error_ratio_hist(bkgSubErrHist.Clone(),1)
    
    bkgSubErrHist.SetLineWidth(2)
    bkgSubErrHist.SetLineStyle(7)
    h2.SetLineWidth(2)
    h2.SetLineStyle(7)
    bkgSubErrHist.SetLineColor(50)
    h2.SetLineColor(50)
    h2.SetMarkerSize(0)
    bkgSubErrHist.SetMarkerSize(0)
    bkgSubErrHist.Draw('L same ')
    h2.Draw("L same")
    
    #h3 = convert_error_bars_to_error_ratio_hist(modelUnc.Clone(),-1)
    #modelUnc = convert_error_bars_to_error_ratio_hist(modelUnc.Clone(),1)
    modelUnc.Draw('L same')
    #h3.Draw('L same')
    
    
    for k in otherUncs:
        text = (k.split('_shifthist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
        print (text, k)
        #h0 = 0
        h0 = convert_error_bars_to_error_ratio_hist(otherUncs[k].Clone(),-1)
        otherUncs[k] = convert_error_bars_to_error_ratio_hist(otherUncs[k].Clone(),1)
        otherUncs[k].Draw('L same')
        h0.Draw('L same')
    
    
    
    for ibin in range(1,jesHistoUpMax.GetNbinsX()+1):
        jesHistoUpMax.SetBinContent(ibin,1)
        jesHistoDownMax.SetBinContent(ibin,1)
        upmax_ibin = 1
        downmax_ibin = 1
        for k in normeduncerUnfoldHistoshiftsUp:
            text = (k.split('_shifthist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
            text=text.upper()
            if 'JES' in text:
                if upmax_ibin<normeduncerUnfoldHistoshiftsUp[k].GetBinContent(ibin):
                    upmax_ibin=normeduncerUnfoldHistoshiftsUp[k].GetBinContent(ibin)
        
                
        for k in normeduncerUnfoldHistoshiftsDown:
            text = (k.split('_shifthist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
            text=text.upper()
            if 'JES' in text:
                if downmax_ibin>normeduncerUnfoldHistoshiftsDown[k].GetBinContent(ibin):
                    downmax_ibin=normeduncerUnfoldHistoshiftsDown[k].GetBinContent(ibin)
        #print ("JES",upmax_ibin,downmax_ibin)
        jesHistoUpMax.SetBinContent(ibin,upmax_ibin)
        jesHistoDownMax.SetBinContent(ibin,downmax_ibin)
        
    #legend.AddEntry(cr_maxup,'CR model', 'p')
    legend.AddEntry(jesHistoUpMax,'JES', 'p')
    jesHistoUpMax.SetLineColor(51)
    jesHistoDownMax.SetLineColor(51)
    jesHistoUpMax.SetMarkerColor(51)
    jesHistoDownMax.SetMarkerColor(51)
    jesHistoUpMax.SetMarkerStyle(upstyles[up_counter])
    jesHistoDownMax.SetMarkerStyle(downstyles[down_counter])
    jesHistoUpMax.SetMarkerSize(2)
    jesHistoDownMax.SetMarkerSize(2)
    jesHistoUpMax.Draw('P same')
    jesHistoDownMax.Draw('P same')
    
    for k in normeduncerUnfoldHistoshiftsUp:
        if 'jes' in k.lower() or 'model'in k.lower() or 'bkg' in k.lower() or 'crtotal' in k.lower(): 
            continue
        normeduncerUnfoldHistoshiftsUp[k].Draw("P same")
        
        text = (k.split('_shiftHist')[0].replace('Up','').replace('Down','').replace('Weight', '')).split(ivar+'_')[1]
        text=text.upper()
        
        if 'damp' in k: 
            normeduncerUnfoldHistoshiftsDown[k.replace('UP', 'DOWN')].Draw("P same")
            legend.AddEntry( normeduncerUnfoldHistoshiftsUp[k], 'h_{damp}', 'p' )
        elif 'mtop' in k:
            normeduncerUnfoldHistoshiftsDown[k.replace('Up', 'Down')].Draw("P same")
            legend.AddEntry( normeduncerUnfoldHistoshiftsUp[k], 'Choice of m_{top}', 'p' )
        else: 
            normeduncerUnfoldHistoshiftsDown[k.replace('Up', 'Down')].Draw("P same")
            legend.AddEntry( normeduncerUnfoldHistoshiftsUp[k], text, 'p' )
        
        #print (text)

    
    
    legend.AddEntry( modelUnc, 'Physics Model', 'l' )    
    legend.AddEntry( bkgSubErrHist, 'Bkg. stat.', 'l' )    
    legend.AddEntry( dataStatErrHist, 'Data Stat.', 'f' )    
    legend.AddEntry( rmStatErrHist, 'RM Stat.', 'l' )    
    legend.AddEntry( totalErrHist, 'Total Unc.', 'f' )   
    CMS_lumi.extraText = "Preliminary"
    CMS_lumi.lumi_13TeV = "13 TeV, "+ ( '2017+2018' if year.startswith('all') else year )
    CMS_lumi.relPosX = 0.11
    CMS_lumi.CMS_lumi(canUnc, 4, 0)
    #canUnc.SetLogy()
    canUnc.Update()
    
    legend.Draw()
    png = outputName.split('.pdf')[0]+'.png'
    canUnc.SaveAs(outputName)
    canUnc.SaveAs(png)
    
    

In [27]:
def plotSysComparison2( nomHisto, dictUncHistos, outputName, labelX='', log=False, version='', ext='png', year='2017', outputDir='Plots/' ):
    """docstring for plot"""
    colors = [ 2, 4,  9, 8, 28, 30, 42, 13, 12, 40, 46, 3, 24, 26, 219, 92, 48, 49, 37, 38, 33, 17, 50, 205, 225, 94, 221, 16,  225, 128]
    
    
    ROOT.gStyle.SetPadRightMargin(0.05)
    ROOT.gStyle.SetPadLeftMargin(0.15)
    canUnc = ROOT.TCanvas('canUnc', 'canUnc',  10, 10, 750, 500 )
    #if log: canUnc.SetLogy()
    

    outputFileName = outputName+'_'+version+'.'+ext
    #print ('Processing.......', outputFileName)

    binWidth = nomHisto.GetBinWidth(1)

    legend=ROOT.TLegend(0.35,0.6,0.80,0.9)
    legend.SetFillStyle(0)
    legend.SetNColumns(3)
    legend.SetTextSize(0.02)
    legend.SetBorderSize(0)

    #multiGraph = ROOT.TMultiGraph()
    gnom = nomHisto.Clone()
    gnom.Divide( nomHisto.Clone() )
    gnom.SetLineColor(ROOT.kBlack)
    gnom.SetMarkerStyle(1)
    gnom.SetLineWidth(2)
    legend.AddEntry( gnom, 'Nominal' , 'l' )
    #multiGraph.Add( gnom )
    dictShifts = {}
    dummy=0
    
    gnom.GetYaxis().SetTitle( 'Ratio Unc/Nominal' )
    gnom.GetXaxis().SetTitle( labelX )
    gnom.SetMaximum( 3. )
    gnom.SetMinimum( -1.)
    gnom.Draw('L')

    #print (dictUncHistos)
    for ih in dictUncHistos:
        #print(ih, dummy, len(colors))
        dictShifts[ih] = dictUncHistos[ih].Clone()
        dictShifts[ih].Divide( nomHisto)
        
        if not dummy==len(colors)-1:
            dictShifts[ih].SetLineColor( colors[dummy] )
            dictShifts[ih].SetLineStyle( 2 )
        else:
            dummy = dummy-len(colors)+2
            dictShifts[ih].SetLineColor( colors[dummy] )
            dictShifts[ih].SetLineStyle( 3 )
        
        if 'jes' in ih: dictShifts[ih].SetLineStyle( 1 )
        dictShifts[ih].SetMarkerStyle(0)
        dictShifts[ih].SetLineWidth( 1 )
        
        if 'jes' in ih and ('2017' in ih or '2018' in ih): 
            print (ih)
            legend.AddEntry( dictShifts[ih], ih.split('_')[1] , 'l' )
        else: legend.AddEntry( dictShifts[ih], ih.split('_')[1] , 'l' )
        dummy=dummy+1
        dictShifts[ih].Draw("L SAME")
        
    CMS_lumi.cmsTextOffset = 0.0
    CMS_lumi.relPosX = 0.13
    CMS_lumi.extraText = "Preliminary"
    CMS_lumi.lumi_13TeV = "13 TeV, "+year
    CMS_lumi.CMS_lumi(canUnc, 4, 0)
    legend.Draw()

    canUnc.SaveAs( outputDir + outputFileName )
    if ext.startswith('pdf'):
        canUnc.SaveAs( outputDir + outputFileName.replace('pdf', 'png') )
    del canUnc

In [28]:
colors = [ 2, 4,  9, 8, 28, 30, 42, 13, 12, 40, 46, 3, 24, 26, 41, 45, 48, 49, 37, 38, 33, 17]
##########################################################################
def runTUnfold( dataFile, sigFiles, bkgFiles, variables, sel, sysUncert, process, ext, runMLU=False, sysSigFiles=[], varSigFiles=[]):

    """docstring for createDataCards"""

    for ivar in variables:
        print (ivar)
        outputDir=outputFolder+sel.split('_')[1]+'/'+year+'/Unfolding/'+ivar+'/'+process+'/'
        if not os.path.exists(outputDir): os.makedirs(outputDir)

        if year.startswith('all'):
            signalHistos = {
                    signalLabel+'_resp'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(signalLabel+'_resp'+ivar+'_nom'+sel),
                    signalLabel+'_reco'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(signalLabel+'_reco'+ivar+'_nom'+sel),
                    signalLabel+'_truereco'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(signalLabel+'_truereco'+ivar+'_nom'+sel),
                    signalLabel+'_fakereco'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(signalLabel+'_fakereco'+ivar+'_nom'+sel),
                    signalLabel+'_accepgen'+ivar+sel : dataFile[ivar+'_2017'].Get(signalLabel+'_accepgen'+ivar+sel),
                    signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin': dataFile[ivar+'_2017'].Get(signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin')
                    }
            signalHistos[ signalLabel+'_resp'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_resp'+ivar+'_nom'+sel) )
            signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_reco'+ivar+'_nom'+sel) )
            signalHistos[ signalLabel+'_truereco'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_truereco'+ivar+'_nom'+sel) )
            signalHistos[ signalLabel+'_fakereco'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_fakereco'+ivar+'_nom'+sel) )
            signalHistos[ signalLabel+'_accepgen'+ivar+sel ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_accepgen'+ivar+sel) )
            signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin' ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin') )
            
            if not process.startswith('MCSelfClosure'):
                sysSignalHistos={}
                #print ("Loading up all syst. variations from the following:", sysUncert)
                for sys in sysUncert:
                    for upDown in [ 'Up', 'Down' ]:
                        #print (sys)
    
                        if sys.startswith(('_model', '_CR', '_erdON', '_mtop', '_hdamp', '_Tune')): continue
                        s = [i for i in sysSignalLabels if sys in i]
                        #print (s)
                        if ('2017' in sys or '2018' in sys) and len(s)>1:
                            if '2017' in s: s=[s[1]]
                            elif '2018' in s: s=[s[2]]
                        else:
                            s=[s[0]]
                        #print (s[0]+'_reco'+ivar+sys+upDown+sel)
                        
                        if not process.startswith('MCCrossClosure') and not '2017' in sys and not '2018' in sys: 
                            sysSignalHistos[ s[0]+'_reco'+ivar+sys+upDown+sel ] = dataFile[ivar+'_2017'].Get(s[0]+'_reco'+ivar+sys+upDown+sel)
                            sysSignalHistos[ s[0]+'_reco'+ivar+sys+upDown+sel ].Add( dataFile[ivar+'_2018'].Get(s[0]+'_reco'+ivar+sys+upDown+sel) )
                            sysSignalHistos[ s[0]+'_resp'+ivar+sys+upDown+sel ] = dataFile[ivar+'_2017'].Get(s[0]+'_resp'+ivar+sys+upDown+sel)
                            sysSignalHistos[ s[0]+'_resp'+ivar+sys+upDown+sel ].Add( dataFile[ivar+'_2018'].Get(s[0]+'_resp'+ivar+sys+upDown+sel) )
                        
                        # dealing with uncorrelated jes unc sources below
                        elif not process.startswith('MCCrossClosure') and '2017' in sys and not '2018' in sys: 
                            sysSignalHistos[ s[0]+'_reco'+ivar+sys+upDown+sel ] = dataFile[ivar+'_2017'].Get(s[0]+'_reco'+ivar+sys+upDown+sel) #get previous errors from unfolding 2017 with 2017 sources
                            sysSignalHistos[ s[0]+'_reco'+ivar+sys+upDown+sel ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_reco'+ivar+'_nom'+sel))
                            sysSignalHistos[ s[0]+'_resp'+ivar+sys+upDown+sel ] = dataFile[ivar+'_2017'].Get(s[0]+'_resp'+ivar+sys+upDown+sel)
                            sysSignalHistos[ s[0]+'_resp'+ivar+sys+upDown+sel ].Add( dataFile[ivar+'_2018'].Get(signalLabel+'_resp'+ivar+'_nom'+sel))
                            
                        elif not process.startswith('MCCrossClosure') and '2018' in sys and not '2017' in sys: 
                            sysSignalHistos[ s[0]+'_reco'+ivar+sys+upDown+sel ] = dataFile[ivar+'_2018'].Get(s[0]+'_reco'+ivar+sys+upDown+sel)
                            sysSignalHistos[ s[0]+'_reco'+ivar+sys+upDown+sel ].Add( dataFile[ivar+'_2017'].Get(signalLabel+'_reco'+ivar+'_nom'+sel))
                            sysSignalHistos[ s[0]+'_resp'+ivar+sys+upDown+sel ] = dataFile[ivar+'_2018'].Get(s[0]+'_resp'+ivar+sys+upDown+sel)
                            sysSignalHistos[ s[0]+'_resp'+ivar+sys+upDown+sel ].Add( dataFile[ivar+'_2017'].Get(signalLabel+'_resp'+ivar+'_nom'+sel))
                        ################ added recohistos & resp matrices from nominal_2018(/2017) and jesUncorrUnc_2017(/2018) ########################
                        

                altSignalHistos = {
                    altSignalLabel+'_resp'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(altSignalLabel+'_resp'+ivar+'_nom'+sel),
                    altSignalLabel+'_reco'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(altSignalLabel+'_reco'+ivar+'_nom'+sel),
                    altSignalLabel+'_truereco'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(altSignalLabel+'_truereco'+ivar+'_nom'+sel),
                    altSignalLabel+'_fakereco'+ivar+'_nom'+sel : dataFile[ivar+'_2017'].Get(altSignalLabel+'_fakereco'+ivar+'_nom'+sel),
                    altSignalLabel+'_accepgen'+ivar+sel : dataFile[ivar+'_2017'].Get(altSignalLabel+'_accepgen'+ivar+sel),
                    }

                altSignalHistos[ altSignalLabel+'_resp'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(altSignalLabel+'_resp'+ivar+'_nom'+sel) )
                altSignalHistos[ altSignalLabel+'_reco'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(altSignalLabel+'_reco'+ivar+'_nom'+sel) )
                altSignalHistos[ altSignalLabel+'_fakereco'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(altSignalLabel+'_fakereco'+ivar+'_nom'+sel) )
                altSignalHistos[ altSignalLabel+'_accepgen'+ivar+sel].Add( dataFile[ivar+'_2018'].Get(altSignalLabel+'_accepgen'+ivar+sel) )
                
                if process.startswith('data') and selection.startswith(('_W','_top')):
                    varSignalHistos={}
                    s=[]
                    
                    '''
                    for sys in sysUncert:
                        if sys.startswith(('_CR', '_erdON', '_mtop', '_hdamp', '_Tune')): 
                            f = [i for i in varSignalLabels if sys in i and i not in s]
                            s.append()
                    print (s)
                    s = list(set(s))
                    print ("sys",sysUncert, s)
                    '''
                    #print ("Processing signal variations from amongst the foll.:", sysUncert)

                    for sys in sysUncert:
                        #print (sys)
                        s = [i for i in varSignalLabels if (sys.split('_')[1] in i)]
                        for j in s:
                            #print (j+'_reco'+ivar+'_nom'+sel)
                            varSignalHistos[ j+'_reco'+ivar+'_nom'+sel ] = dataFile[ivar+'_2017'].Get(j+'_reco'+ivar+'_nom'+sel)
                            varSignalHistos[ j+'_reco'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(j+'_reco'+ivar+'_nom'+sel) )
                            varSignalHistos[ j+'_resp'+ivar+'_nom'+sel ] = dataFile[ivar+'_2017'].Get(j+'_resp'+ivar+'_nom'+sel)
                            varSignalHistos[ j+'_resp'+ivar+'_nom'+sel ].Add( dataFile[ivar+'_2018'].Get(j+'_resp'+ivar+'_nom'+sel) )

                
                
            allHistos = {
                    'dataHisto' : dataFile[ivar+'_2017'].Get( 'dataHisto' ),
                    'dataHistoGenBin' : dataFile[ivar+'_2017'].Get( 'dataHistoGenBin' )
                    }
            allHistos[ 'dataHisto' ].Add( dataFile[ivar+'_2018'].Get( 'dataHisto' ) )
            allHistos[ 'dataHistoGenBin' ].Add( dataFile[ivar+'_2018'].Get( 'dataHistoGenBin' ) )

            dataHistos = { }
            bkgHistos = { }

        else:
            print('|-------> Running single year '+year)
            ### Getting input histos
            mainSigFiles = { k:v for (k,v) in sigFiles.items() if k.startswith(signalLabelBegin)  }
            signalHistos = loadHistograms( mainSigFiles, ivar, sel, sysUnc=[], respOnly=False, lumi=lumi, year=year, process=process, variables=variables )
            tmp2SigFiles = { k:v for (k,v) in sigFiles.items() if k.startswith(altSignalLabelBegin)  }
            if not process.startswith('MCSelfClosure'): altSignalHistos = loadHistograms( tmp2SigFiles, ivar, sel, sysUnc=[], isMC=True, respOnly=False, lumi=lumi, year=year, process=process, variables=variables)
            if not process.startswith('MCSelfClosure'): sysSignalHistos = loadHistograms( sysSigFiles, ivar, sel, sysUnc=sysUncert, respOnly=False, isMC=True, lumi=lumi, year=year, process=process, variables=variables)
            if process.startswith('data') and selection.startswith(('_W','_top')): varSignalHistos = loadHistograms( varSigFiles, ivar, sel, sysUnc=[], respOnly=False, isMC=True, lumi=lumi, year=year, process=process, variables=variables)
            bkgHistos = loadHistograms( bkgFiles, ivar, sel, sysUnc=[], lumi=lumi, year=year, process=process, variables=variables) if process.startswith('data') else {}

            #print ("Alt histos:", bkgHistos)
            
            ####### Fix fake and true reco
            signalHistos[signalLabel+'_truereco'+ivar+'_nom'+sel] = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionY()
            signalHistos[signalLabel+'_fakereco'+ivar+'_nom'+sel] = signalHistos[signalLabel+'_reco'+ivar+'_nom'+sel].Clone()
            signalHistos[signalLabel+'_fakereco'+ivar+'_nom'+sel].Add( signalHistos[signalLabel+'_truereco'+ivar+'_nom'+sel], -1 )

            signalHistos[signalLabel+'_accepgen'+ivar+sel] = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionX()
            signalHistos[signalLabel+'_missgen'+ivar+sel] = signalHistos[signalLabel+'_gen'+ivar+sel].Clone()
            signalHistos[signalLabel+'_missgen'+ivar+sel].Add( signalHistos[signalLabel+'_accepgen'+ivar+sel], -1 )
            
            if not process.startswith('MCSelfClosure'):
                #print(altSignalHistos)
                altSignalHistos[altSignalLabel+'_truereco'+ivar+'_nom'+sel]= altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].ProjectionY()
                altSignalHistos[altSignalLabel+'_fakereco'+ivar+'_nom'+sel] = altSignalHistos[altSignalLabel+'_reco'+ivar+'_nom'+sel].Clone()
                altSignalHistos[altSignalLabel+'_fakereco'+ivar+'_nom'+sel].Add( altSignalHistos[altSignalLabel+'_truereco'+ivar+'_nom'+sel], -1 )

                altSignalHistos[altSignalLabel+'_accepgen'+ivar+sel] = altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].ProjectionX()
                altSignalHistos[altSignalLabel+'_missgen'+ivar+sel] = altSignalHistos[altSignalLabel+'_gen'+ivar+sel].Clone()
                altSignalHistos[altSignalLabel+'_missgen'+ivar+sel].Add( altSignalHistos[altSignalLabel+'_accepgen'+ivar+sel], -1 )          
              
            if sel.startswith('_dijet'): 
                dataHistostrue = loadHistograms( dataFile, ivar, sel, isMC= False, lumi=lumi, year=year, process=process, variables=variables )
                ######## Cross check: plotting data vs all MC Scaled
                print ('|------> Cross check: plotting data vs all MC')
                allHistos = {}
                allHistos[ 'allBkgHisto' ] = dataHistostrue['data_reco'+ivar+'_nom'+sel].Clone()
                allHistos[ 'allBkgHisto' ].Reset()
                allHistos[ 'allBkgHistoGenBin' ] = dataHistostrue['data_reco'+ivar+'_nom'+sel+'_genBin'].Clone()
                allHistos[ 'allBkgHistoGenBin' ].Reset()
                if process.startswith('data'):
                    for ibkg in bkgHistos:
                        if ibkg.endswith('_reco'+ivar+'_nom'+sel): allHistos[ 'allBkgHisto' ].Add( bkgHistos[ibkg].Clone() )
                        if ibkg.endswith('_reco'+ivar+'_nom'+sel+'_genBin'): allHistos[ 'allBkgHistoGenBin' ].Add( bkgHistos[ibkg].Clone() )
                allHistos[ 'allMCHisto' ] = allHistos[ 'allBkgHisto' ].Clone()
                allHistos[ 'allMCHisto' ].Add( signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel ].Clone() )
                allHistos[ 'allMCHistoGenBin' ] = allHistos[ 'allBkgHistoGenBin' ].Clone()
                allHistos[ 'allMCHistoGenBin' ].Add( signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin' ].Clone() )

            
            
            else:
                if process.startswith("MC"):
                    genBin = variables[ivar]['bins']
                    dataHistos = { 'data_reco'+k.split(('_truereco'))[1] : v for (k,v) in signalHistos.items() if '_truereco' in k }
                    dataHistos['data_reco'+ivar+'_nom'+sel+'_genBin'] = dataHistos['data_reco'+ivar+'_nom'+sel].Clone()
                    dataHistos['data_reco'+ivar+'_nom'+sel+'_genBin'] = dataHistos['data_reco'+ivar+'_nom'+sel+'_genBin'].Rebin( len(genBin)-1, 'data_reco'+ivar+'_nom'+sel+'_genBin', array( 'd', genBin ) )
                else:
                    genBin = variables[ivar]['bins']
                    dataHistos = loadHistograms( dataFile, ivar, sel, isMC= False, lumi=lumi, year=year, process=process, variables=variables )
            
                #print ('|------> Cross check: plotting data vs all MC')
                allHistos = {}
                allHistos[ 'allBkgHisto' ] = dataHistos['data_reco'+ivar+'_nom'+sel].Clone()
                allHistos[ 'allBkgHisto' ].Reset()
                allHistos[ 'allBkgHistoGenBin' ] = dataHistos['data_reco'+ivar+'_nom'+sel+'_genBin'].Clone()
                allHistos[ 'allBkgHistoGenBin' ].Reset()
                if process.startswith('data'):
                    for ibkg in bkgHistos:
                        if ibkg.endswith('_reco'+ivar+'_nom'+sel): allHistos[ 'allBkgHisto' ].Add( bkgHistos[ibkg].Clone() )                            
                        if ibkg.endswith('_reco'+ivar+'_nom'+sel+'_genBin'): allHistos[ 'allBkgHistoGenBin' ].Add( bkgHistos[ibkg].Clone().Rebin( len(genBin)-1, 'ibkg_rebin', array( 'd', genBin ) ) )
                            
                allHistos[ 'allMCHisto' ] = allHistos[ 'allBkgHisto' ].Clone()
                allHistos[ 'allMCHisto' ].Add( signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel ].Clone() )
                allHistos[ 'allMCHistoGenBin' ] = allHistos[ 'allBkgHistoGenBin' ].Clone()
                allHistos[ 'allMCHistoGenBin' ].Add( signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin' ].Clone() )

            ### For dijet, scale QCD to data
            scaleFactor =1
            if sel.startswith('_dijet'):
                scaleFactor = dataHistostrue['data_reco'+ivar+'_nom'+sel].Integral() / allHistos[ 'allMCHisto' ].Integral()
                scaleFactorGenBin = dataHistostrue['data_reco'+ivar+'_nom'+sel+'_genBin'].Integral() / allHistos[ 'allMCHistoGenBin' ].Integral()
                allHistos[ 'allMCHisto' ].Scale( scaleFactor )
                if process=='data':
                    allHistos[ 'allBkgHisto' ].Scale( scaleFactor )
                    allHistos[ 'allBkgHistoGenBin' ].Scale( scaleFactorGenBin )
                for ihsig in signalHistos:
                    if ihsig.endswith(sel):
                        #print (ihsig)
                        signalHistos[ihsig].Scale( scaleFactor )
                    if ihsig.endswith('genBin'): signalHistos[ihsig].Scale( scaleFactorGenBin )
                    #if 'resp' in ihsig: signalHistos[ihsig].Scale( scaleFactor )   ### dont notice the difference
                if not process.startswith('MC'):
                    for ihsig in sysSignalHistos:
                        if ihsig.endswith(sel):
                            #print (ihsig)
                            sysSignalHistos[ihsig].Scale( scaleFactor )
                        if ihsig.endswith('genBin'): sysSignalHistos[ihsig].Scale( scaleFactorGenBin )
            
                if process.startswith("MC"):
                    genBin = variables[ivar]['bins']
                    dataHistos = { 'data_reco'+k.split(('_truereco'))[1] : v for (k,v) in signalHistos.items() if '_truereco' in k }
                    dataHistos['data_reco'+ivar+'_nom'+sel+'_genBin'] = dataHistos['data_reco'+ivar+'_nom'+sel].Clone()
                    dataHistos['data_reco'+ivar+'_nom'+sel+'_genBin'] = dataHistos['data_reco'+ivar+'_nom'+sel+'_genBin'].Rebin( len(genBin)-1, 'data_reco'+ivar+'_nom'+sel+'_genBin', array( 'd', genBin ) )
                else: 
                    dataHistos = dataHistostrue
                plotSimpleComparison( dataHistos['data_reco'+ivar+'_nom'+sel].Clone(), 'data', allHistos[ 'allMCHisto' ].Clone(), 'allBkgs', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_nom", rebinX=variables[ivar]['bins'], version=sel+'_'+version, outputDir=outputDir )

            print ('|------> Unfolding '+ivar)

           
            
            
            
           ######## Adding missgen to overflow and underflow
#            for ibin in range( 1, signalHistos[signalLabel+'_missgen'+ivar+sel].GetNbinsX()+1 ):
#                signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].SetBinContent(  signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetBin( 0, ibin ), signalHistos[signalLabel+'_missgen'+ivar+sel].GetBinContent(ibin) )
#                signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].SetBinError(  signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetBin( 0, ibin ), signalHistos[signalLabel+'_missgen'+ivar+sel].GetBinError(ibin) )
#                signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].SetBinContent(  signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetBin( -1, ibin ), signalHistos[signalLabel+'_missgen'+ivar+sel].GetBinContent(ibin) )
#                signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].SetBinError(  signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetBin( -1, ibin ), signalHistos[signalLabel+'_missgen'+ivar+sel].GetBinError(ibin) )
#                altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].SetBinContent(  altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].GetBin( 0, ibin ), altSignalHistos[altSignalLabel+'_missgen'+ivar+sel].GetBinContent(ibin) )
#                altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].SetBinError(  altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].GetBin( 0, ibin ), altSignalHistos[altSignalLabel+'_missgen'+ivar+sel].GetBinError(ibin) )
#                altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].SetBinContent(  altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].GetBin( -1, ibin ), altSignalHistos[altSignalLabel+'_missgen'+ivar+sel].GetBinContent(ibin) )
#                altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].SetBinError(  altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].GetBin( -1, ibin ), altSignalHistos[altSignalLabel+'_missgen'+ivar+sel].GetBinError(ibin) )
##                #for sys in sysUncert:
##                #    for upDown in [ 'Up', 'Down' ]:
##                #        signalHistos[signalLabel+'_resp'+ivar+sys+upDown+sel].SetBinContent(  signalHistos[signalLabel+'_resp'+ivar+sys+upDown+sel].GetBin( ibin, 0 ), signalHistos[signalLabel+'_missgen'+ivar+sel].GetBinContent(ibin) )
##                #        signalHistos[signalLabel+'_resp'+ivar+sys+upDown+sel].SetBinContent(  signalHistos[signalLabel+'_resp'+ivar+sys+upDown+sel].GetBin( ibin, -1 ), signalHistos[signalLabel+'_missgen'+ivar+sel].GetBinContent(ibin) )

            ####### Cross check response matrix
            tmpGenHisto = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionX()
            plotSimpleComparison( tmpGenHisto, 'projection', signalHistos[signalLabel+'_accepgen'+ivar+sel].Clone(), 'Regular AccepGen', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_TestProjectionGen", rebinX=1, version=sel+'_'+version, outputDir=outputDir )
            tmpRecoHisto = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionY()
            plotSimpleComparison( tmpRecoHisto, 'projection', signalHistos[signalLabel+'_truereco'+ivar+'_nom'+sel].Clone(), 'Regular TrueReco', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_TestProjectionReco", rebinX=1, version=sel+'_'+version, outputDir=outputDir )
            tmpRecoHisto.Scale( scaleFactor )
            
            ####### plotting Removing of bkgs from data
            fakeHistos = { k:v for (k,v) in signalHistos.items() if 'fakereco' in k }
            for ih in fakeHistos:
                if ih.endswith(ivar+'_nom'+sel): allHistos[ 'allBkgHisto' ].Add( fakeHistos[ih] )
                if ih.endswith(ivar+'_nom'+sel+'_genBin'): allHistos[ 'allBkgHistoGenBin' ].Add( fakeHistos[ih] )
            plotSimpleComparison( dataHistos[ 'data_reco'+ivar+'_nom'+sel ].Clone(), 'data', allHistos[ 'allBkgHisto' ].Clone(), 'Bkg+fakes', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_TestDataBkgFakes", rebinX=1, version=sel+'_'+version, outputDir=outputDir )

            allHistos[ 'dataHisto' ] = dataHistos[ 'data_reco'+ivar+'_nom'+sel ].Clone()
            #allHistos[ 'dataHisto' ].Add( allHistos[ 'allBkgHisto' ].Clone(), -1 )
            #allHistos[ 'dataHisto' ].Scale( 1/allHistos[ 'dataHisto' ].Integral() )
            allHistos[ 'dataHistoGenBin' ] = dataHistos[ 'data_reco'+ivar+'_nom'+sel+'_genBin'].Clone()
            #allHistos[ 'dataHistoGenBin' ].Add( allHistos[ 'allBkgHistoGenBin' ].Clone(), -1 )
            #allHistos[ 'dataHistoGenBin' ].Scale( 1/allHistos[ 'dataHistoGenBin' ].Integral() )

        if process.startswith('data') and not year.startswith('all'):
            allHistos[ 'dataMinusBkgs' ] = dataHistos[ 'data_reco'+ivar+'_nom'+sel ].Clone()
            allHistos[ 'dataMinusBkgs' ].Add( allHistos[ 'allBkgHisto' ].Clone(), -1 )
            #allHistos[ 'dataMinusBkgs' ].Scale( 1/allHistos[ 'dataMinusBkgs' ].Integral() )
            allHistos[ 'dataMinusBkgsGenBin' ] = dataHistos[ 'data_reco'+ivar+'_nom'+sel+'_genBin'].Clone()
            allHistos[ 'dataMinusBkgsGenBin' ].Add( allHistos[ 'allBkgHistoGenBin' ].Clone(), -1 )
            #allHistos[ 'dataMinusBkgsGenBin' ].Scale( 1/allHistos[ 'dataMinusBkgsGenBin' ].Integral() )

            tmpHisto = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionY()
            #tmpHisto.Scale( 1/tmpHisto.Integral() )

            tmpHisto = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionY()
            #tmpHisto.Scale( 1/tmpHisto.Integral() )
            plotSimpleComparison( allHistos[ 'dataMinusBkgs' ].Clone(), 'data-Bkgs', tmpHisto.Clone(), 'signal true reco', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_TestDataMinusBkgs", rebinX=1, version=sel+'_'+version, outputDir=outputDir )
        
        elif process.startswith('data') and year.startswith('all'):
            
            print ('|------> Cross check: plotting data vs all MC')
            allHistos[ 'allBkgHisto' ] = allHistos['dataHisto'].Clone()
            allHistos[ 'allBkgHisto' ].Reset()
            allHistos[ 'allBkgHistoGenBin' ] = allHistos['dataHistoGenBin'].Clone()
            allHistos[ 'allBkgHistoGenBin' ].Reset()
            if process.startswith('data'):
                for ibkg in bkgHistos:
                    if ibkg.endswith('_reco'+ivar+'_nom'+sel): allHistos[ 'allBkgHisto' ].Add( bkgHistos[ibkg].Clone() )
                    if ibkg.endswith('_reco'+ivar+'_nom'+sel+'_genBin'): allHistos[ 'allBkgHistoGenBin' ].Add( bkgHistos[ibkg].Clone().Rebin( len(genBin)-1, 'ibkg_rebin', array( 'd', genBin ) ) )
            allHistos[ 'allMCHisto' ] = allHistos[ 'allBkgHisto' ].Clone()
            allHistos[ 'allMCHisto' ].Add( signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel ].Clone() )
            allHistos[ 'allMCHistoGenBin' ] = allHistos[ 'allBkgHistoGenBin' ].Clone()
            allHistos[ 'allMCHistoGenBin' ].Add( signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin' ].Clone() )

            allHistos[ 'dataMinusBkgs' ] = allHistos[ 'dataHisto' ].Clone()
            allHistos[ 'dataMinusBkgs' ].Add( allHistos[ 'allBkgHisto' ].Clone(), -1 )
            #allHistos[ 'dataMinusBkgs' ].Scale( 1/allHistos[ 'dataMinusBkgs' ].Integral() )
            allHistos[ 'dataMinusBkgsGenBin' ] = allHistos[ 'dataHistoGenBin'].Clone()
            allHistos[ 'dataMinusBkgsGenBin' ].Add( allHistos[ 'allBkgHistoGenBin' ].Clone(), -1 )
            #allHistos[ 'dataMinusBkgsGenBin' ].Scale( 1/allHistos[ 'dataMinusBkgsGenBin' ].Integral() )

            tmpHisto = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionY()
            #tmpHisto.Scale( 1/tmpHisto.Integral() )

            tmpHisto = signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].ProjectionY()
            #tmpHisto.Scale( 1/tmpHisto.Integral() )
            plotSimpleComparison( allHistos[ 'dataMinusBkgs' ].Clone(), 'data-Bkgs', tmpHisto.Clone(), 'signal true reco', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_TestDataMinusBkgs", rebinX=1, version=sel+'_'+version, outputDir=outputDir )

        #print(sysSignalHistos)
            
        ######## Cross check: plotting response matrix
        print ('|------> Cross check: plotting response matrix for signal')
        ROOT.gStyle.SetPadRightMargin(0.15)
        #ROOT.gStyle.SetPalette(ROOT.kGistEarth)
        #ROOT.TColor.InvertPalette()
        can2D = ROOT.TCanvas(ivar+'can2D', ivar+'can2D', 750, 500 )
        signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetXaxis().SetTitle('Accepted Gen '+variables[ivar]['label'])
        signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetYaxis().SetTitle('True Reco '+variables[ivar]['label'])
        signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetYaxis().SetTitleOffset( 0.8 )
        #signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].GetYaxis().SetRange( variables[ivar]['bins'][0], variables[ivar]['bins'][-1] )
        signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].Draw("colz")
        CMS_lumi.extraText = "Simulation Preliminary"
        CMS_lumi.lumi_13TeV = "13 TeV, "+ ( '2017+2018' if year.startswith('all') else year )
        CMS_lumi.relPosX = 0.12
        CMS_lumi.CMS_lumi(can2D, 4, 0)
        can2D.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+sel+'_responseMatrix'+version+'.'+ext)

        

        ######## TUnfold part
        print ('|------> TUnfolding starts:')

        ##### Defining options for TUnfold
        tunfolder = ROOT.TUnfoldDensity(
                                            signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel], ### response matrix. According to TUnfold, this distribution does NOT have to be normalized
                                            ROOT.TUnfold.kHistMapOutputHoriz,  #### kHistMapOutputVert if x->reco and y->gen, kHistMapOutputHoriz if x->gen and y->reco
                                            ROOT.TUnfold.kRegModeCurvature,   ##### Regularization Mode : ROOT.TUnfold.kRegModeCurvature regularizes based on the 2nd derivative of the output. More information wrt the other options can be gained from reading the source code
                                            ROOT.TUnfold.kEConstraintNone,    ##### Constraint : TUnfold.kEConstraintNone meaning we do not constrain further, the other option is to force constraint of area. (Need to look into this!!)
                                            ROOT.TUnfoldDensity.kDensityModeBinWidth  ##### Density Mode: ROOT.TUnfoldDensity.kDensityModeBinWidth uses the bin width to normalize the event rate in a given bin, accounting for non-uniformity in bin widths as discussed in section 7.2.1 of the TUnfold paper
                                            )

        ##### Defining input (data recoJet )
        print ('|------> TUnfolding adding input:')
        #tunfolder.SetInput( dataHistos[ 'data_reco'+ivar+'_nom'+sel ].Clone() )
        #print (allHistos.keys())
        tunfolder.SetInput( allHistos[ 'dataHisto' ])
        
        if process.startswith('MCCrossClosure'): 
            tunfolder_cross = ROOT.TUnfoldDensity(
                                            altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel], ### response matrix. According to TUnfold, this distribution does NOT have to be normalized
                                            ROOT.TUnfold.kHistMapOutputHoriz,  #### kHistMapOutputVert if x->reco and y->gen, kHistMapOutputHoriz if x->gen and y->reco
                                            ROOT.TUnfold.kRegModeCurvature,   ##### Regularization Mode : ROOT.TUnfold.kRegModeCurvature regularizes based on the 2nd derivative of the output. More information wrt the other options can be gained from reading the source code
                                            ROOT.TUnfold.kEConstraintNone,    ##### Constraint : TUnfold.kEConstraintNone meaning we do not constrain further, the other option is to force constraint of area. (Need to look into this!!)
                                            ROOT.TUnfoldDensity.kDensityModeBinWidth  ##### Density Mode: ROOT.TUnfoldDensity.kDensityModeBinWidth uses the bin width to normalize the event rate in a given bin, accounting for non-uniformity in bin widths as discussed in section 7.2.1 of the TUnfold paper
                                            )

            ##### Defining input (data recoJet )
            print ('|------> TUnfolding adding input:')
            #tunfolder.SetInput( dataHistos[ 'data_reco'+ivar+'_nom'+sel ].Clone() )
            #print (allHistos.keys())
            tunfolder_cross.SetInput( allHistos[ 'dataHisto' ])
        
        if process.startswith('data'):
            print ("Subtracting backgrounds")
            dummy=0
            bkgSources = []
            if sel.startswith(('_W','_top')):
            

                for ibkg in bkgHistos:
                    if ibkg.endswith('_reco'+ivar+'_nom'+sel):
                        #print (ibkg.split('_')[0]+ '%d'%dummy)
                        tunfolder.SubtractBackground( bkgHistos[ibkg].Clone(), ibkg.split('_')[0]+ '%d'%dummy )
                        dummy=dummy+1
                        bkgSources.append(ibkg.split('_')[0]+ '%d'%dummy)
                    if ibkg.endswith('_reco'+ivar+'_nom'+sel+'_genBin'): allHistos[ 'allBkgHistoGenBin' ].Add( bkgHistos[ibkg].Clone() )

            tunfolder.SubtractBackground( signalHistos[signalLabel+'_fakereco'+ivar+'_nom'+sel], 'fakes')
            bkgSources.append('fakes')
        jes_uncorr_list = [
                            '_jesAbsolute_2017', '_jesBBEC1_2017', '_jesEC2_2017', '_jesHF_2017', '_jesRelativeSample_2017',
                            '_jesAbsolute_2018', '_jesBBEC1_2018', '_jesEC2_2018', '_jesHF_2018', '_jesRelativeSample_2018'
                          ]
        jes_corr_list = ['_jesAbsolute', '_jesBBEC1', '_jesEC2', '_jesFlavorQCD', '_jesHF', '_jesRelativeBal']
        jes_sources_names_uncorr = []
        jes_sources_names_corr = []
        ###### Adding SYS unc
        
        if len(sysUncert)>0 and process.startswith('data'):
            print ('|------> TUnfolding adding uncert:')
            dictUncHistos = {}
            #print (sysSignalHistos)
            for sys in sysUncert:
                #print (sys)
                
                if sys.startswith(('_jer', '_isrWeight', '_fsrWeight', '_puWeight', '_pdfWeight', '_jes')):
                    #print('|------> TUnfolding adding %sUnc'%sys)
                    
                    s = [i for i in sysSignalLabels if sys in i]
                        #print (s)
                    if ('2017' in sys or '2018' in sys) and len(s)>1:
                        if '2017' in s: s=[s[1]]
                        elif '2018' in s: s=[s[2]]
                    else:
                        s=[s[0]]
                    
                    dictUncHistos[sys+'Up'] = sysSignalHistos[s[0]+'_reco'+ivar+sys+'Up'+sel].Clone()
                    dictUncHistos[sys+'Down'] = sysSignalHistos[s[0]+'_reco'+ivar+sys+'Down'+sel].Clone()
                    for upDown in [ 'Up', 'Down' ]:
                        #print (sys+upDown)
                        tunfolder.AddSysError(
                                            sysSignalHistos[s[0]+'_resp'+ivar+sys+upDown+sel],
                                            sys+upDown,
                                            ROOT.TUnfold.kHistMapOutputHoriz,
                                            ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                            )
                        can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+sys+upDown, ivar+'can2DNorm'+sys+upDown, 750, 500 )
                        sysSignalHistos[s[0]+'_resp'+ivar+sys+upDown+sel].Draw("colz")
                        can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+s[0]+sel+upDown+'Normalized_responseMatrix'+version+'.'+ext)

                #### adding model uncertainty
                elif sys.startswith(('_model')):
                    #if not process.startswith('MCSelfClosure'):
                    #print('|------> TUnfolding adding modelUnc')
                    tunfolder.AddSysError(
                                        altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel],
                                        'modelUncTotal',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNormAltSignal', ivar+'can2DNormAltSignal', 750, 500 )
                    altSignalHistos[altSignalLabel+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+altSignalLabel+sel+'Normalized_alt_responseMatrix'+version+'.'+ext)
                    dictUncHistos[sys] = altSignalHistos[altSignalLabel+'_reco'+ivar+'_nom'+sel].Clone()
            
            
                elif sys.startswith('_hdamp'): 
                    #if process.startswith('MC'): continue
                    #print('|------> TUnfolding adding hdampUnc')
                    #dictUncHistos[sys+'Up'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Up'+sel].Clone()
                    #dictUncHistos[sys+'Down'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Down'+sel].Clone()
                    tunfolder.AddSysError(
                                        varSignalHistos['varTTToSemileptonic_hdampUP_TuneCP5'+'_resp'+ivar+'_nom'+sel],
                                        '_hdampUP',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'_hdampUP', ivar+'can2DNorm'+'_hdampUP', 750, 500 )
                    varSignalHistos['varTTToSemileptonic_hdampUP_TuneCP5'+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_hdampUP'+'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                    tunfolder.AddSysError(
                                        varSignalHistos['varTTToSemileptonic_hdampDOWN_TuneCP5'+'_resp'+ivar+'_nom'+sel],
                                        '_hdampDOWN',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'_hdampDOWN', ivar+'can2DNorm'+'_hdampDOWN', 750, 500 )
                    varSignalHistos['varTTToSemileptonic_hdampDOWN_TuneCP5'+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_hdampDOWN'+'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                    dictUncHistos['_hdampUP'] = varSignalHistos['varTTToSemileptonic_hdampUP_TuneCP5'+'_reco'+ivar+'_nom'+sel].Clone()
                    dictUncHistos['_hdampDOWN'] = varSignalHistos['varTTToSemileptonic_hdampDOWN_TuneCP5'+'_reco'+ivar+'_nom'+sel].Clone()

                elif sys.startswith('_Tune'):
                    #if process.startswith('MC'): continue
                    #print('|------> TUnfolding adding TuneCP5Unc')
                    #dictUncHistos[sys+'Up'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Up'+sel].Clone()
                    #dictUncHistos[sys+'Down'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Down'+sel].Clone()
                    tunfolder.AddSysError(
                                        varSignalHistos['varTTToSemileptonic_TuneCP5Up'+'_resp'+ivar+'_nom'+sel],
                                        '_TuneCP5Up',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'_TuneCP5Up', ivar+'can2DNorm'+'_TuneCP5Up', 750, 500 )
                    varSignalHistos['varTTToSemileptonic_TuneCP5Up'+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_TuneCP5Up'+'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                    tunfolder.AddSysError(
                                        varSignalHistos['varTTToSemileptonic_TuneCP5Down'+'_resp'+ivar+'_nom'+sel],
                                        '_TuneCP5Down',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'_TuneCP5Down', ivar+'can2DNorm'+'_TuneCP5Down', 750, 500 )
                    varSignalHistos['varTTToSemileptonic_TuneCP5Down'+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_TuneCP5Down'+'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                    dictUncHistos['_TuneCP5Up'] = varSignalHistos['varTTToSemileptonic_TuneCP5Up'+'_reco'+ivar+'_nom'+sel].Clone()
                    dictUncHistos['_TuneCP5Down'] = varSignalHistos['varTTToSemileptonic_TuneCP5Down'+'_reco'+ivar+'_nom'+sel].Clone()

                elif sys.startswith('_CR'):
                    #if process.startswith('MC'): continue
                    #print('|------> TUnfolding adding Colour reconnection Unc')
                    #dictUncHistos[sys+'Up'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Up'+sel].Clone()
                    #dictUncHistos[sys+'Down'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Down'+sel].Clone()
                    tunfolder.AddSysError(
                                        varSignalHistos['varTTToSemileptonic_TuneCP5CR1'+'_resp'+ivar+'_nom'+sel],
                                        '_CR1',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'TuneCP5CR1', ivar+'can2DNorm'+'TuneCP5CR1', 750, 500 )
                    varSignalHistos['varTTToSemileptonic_TuneCP5CR1'+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_TuneCP5CR1'+'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                    tunfolder.AddSysError(
                                        varSignalHistos['varTTToSemileptonic_TuneCP5CR2'+'_resp'+ivar+'_nom'+sel],
                                        '_CR2',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'TuneCP5CR2', ivar+'can2DNorm'+'TuneCP5CR2', 750, 500 )
                    varSignalHistos['varTTToSemileptonic_TuneCP5CR2'+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_TuneCP5CR2'+'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                    dictUncHistos['_CR1'] = varSignalHistos['varTTToSemileptonic_TuneCP5CR1'+'_reco'+ivar+'_nom'+sel].Clone()
                    dictUncHistos['_CR2'] = varSignalHistos['varTTToSemileptonic_TuneCP5CR2'+'_reco'+ivar+'_nom'+sel].Clone()

                elif sys.startswith('_erdON'): 
                    #if process.startswith('MC'): continue
                    #print('|------> TUnfolding adding erdONUnc')
                    #dictUncHistos[sys+'Up'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Up'+sel].Clone()
                    #dictUncHistos[sys+'Down'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Down'+sel].Clone()
                    tunfolder.AddSysError(
                                        varSignalHistos['varTTToSemileptonic_TuneCP5_erdON'+'_resp'+ivar+'_nom'+sel],
                                        '_erdON',
                                        ROOT.TUnfold.kHistMapOutputHoriz,
                                        ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                    can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'TuneCP5_erdON', ivar+'can2DNorm'+'TuneCP5_erdON', 750, 500 )
                    varSignalHistos['varTTToSemileptonic_TuneCP5_erdON'+'_resp'+ivar+'_nom'+sel].Draw("colz")
                    can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_TuneCP5_erdON'+'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                    dictUncHistos['_erdON'] = varSignalHistos['varTTToSemileptonic_TuneCP5_erdON'+'_reco'+ivar+'_nom'+sel].Clone()

                elif sys.startswith('_mtop'): 
                    #if process.startswith('MC'): continue
                    #print('|------> TUnfolding adding mtopUnc')
                    mass_list = [ '171p5','173p5' ] #'166p5',
                    #dictUncHistos[sys+'Up'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Up'+sel].Clone()
                    #dictUncHistos[sys+'Down'] = signalHistos[signalLabel+'_reco'+ivar+sys+'Down'+sel].Clone()

                    for m in mass_list:
                        tunfolder.AddSysError(
                                             varSignalHistos['varTTToSemileptonic_mtop%s_TuneCP5'%m+'_resp'+ivar+'_nom'+sel],
                                             '_mtop%s'%m,
                                         ROOT.TUnfold.kHistMapOutputHoriz,
                                         ROOT.TUnfoldSys.kSysErrModeMatrix, #### kSysErrModeMatrix the histogram sysError corresponds to an alternative response matrix. kSysErrModeShift the content of the histogram sysError are the absolute shifts of the response matrix. kSysErrModeRelative the content of the histogram sysError specifies the relative uncertainties
                                        )
                        can2DNorm = ROOT.TCanvas(ivar+'can2DNorm'+'_mtop%s_TuneCP5'%m, ivar+'can2DNorm'+'_mtop%s_TuneCP5'%m, 750, 500 )
                        varSignalHistos['varTTToSemileptonic_mtop%s_TuneCP5'%m+'_resp'+ivar+'_nom'+sel].Draw("colz")
                        can2DNorm.SaveAs(outputDir+ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+'TTToSemileptonic_mtop%s_TuneCP5'%m +'_resp'+sel+'Normalized_responseMatrix'+version+'.'+ext)

                        dictUncHistos['_mtop%s'%m] = varSignalHistos['varTTToSemileptonic_mtop%s_TuneCP5'%m+'_reco'+ivar+'_nom'+sel].Clone()

            '''
            ### Making unc plot
            plotSysComparison2( signalHistos[signalLabel+'_reco'+ivar+'_nom'+sel].Clone(),
                                dictUncHistos,
                                ivar+'_'+signalLabel+'_allSys',
                                labelX=variables[ivar]['label'],
                                version=sel+'_'+version,
                                year= ( '2017+2018' if year.startswith('all') else year ),
                                outputDir=outputDir
                                )
            '''
        ###### Running the unfolding
        print ('|------> TUnfolding doUnfold:')
        tunfolder.DoUnfold(0)
        if process.startswith('MCCrossClosure'): tunfolder_cross.DoUnfold(0) 
            
        ##### Get output of unfolding ###############################################################
        allHistos [ 'unfoldHisto'+ivar ] = tunfolder.GetOutput("unfoldHisto"+ivar).Clone()
        allHistos [ 'unfoldHisto'+ivar ].Sumw2()
        if process.startswith('MCCrossClosure'): allHistos [ 'unfoldHistoCross'+ivar ] = tunfolder_cross.GetOutput("unfoldHistoCross"+ivar).Clone()
        unfoldingtot = allHistos [ 'unfoldHisto'+ivar ].Integral()

        allHistos [ 'foldHisto'+ivar ] = tunfolder.GetFoldedOutput("folded"+ivar).Clone()
        if process.startswith('data'): 
            plotSimpleComparison( allHistos[ 'dataMinusBkgs' ].Clone(), 'data-Bkgs',  allHistos [ 'foldHisto'+ivar ].Clone(), 'folded', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_Test", rebinX=1, version=sel+'_'+version, outputDir=outputDir )
            plotSimpleComparison( allHistos[ 'unfoldHisto'+ ivar ].Clone(), 'unfold',  signalHistos[signalLabel+'_accepgen'+ivar+sel].Clone(), 'accepgen', ivar+'_from'+('Data' if process.startswith('data') else 'MC')+'_'+signalLabel+"_Test", rebinX=1, version=sel+'_'+version, outputDir=outputDir )

        #### Get Probability matrix ###############################################################
        allHistos[ 'probaMatrix'+ivar ] = tunfolder.GetProbabilityMatrix('probaMatrix'+ivar).Clone()
        
        
        ###################################################### Get systematic shifts of output #######################################################
        uncerUnfoldHisto = OrderedDict() #storing individual systematics totals (ie, up/down or other variations), background subtraction systematics, and then the overall systematic unc (individual systs + bkgs)
        uncerUnfoldSystCov = OrderedDict()
        if len(sysUncert)>0 and process.startswith('data'):
            print ('|------> TUnfolding uncertainties:')

            
            
            for sys in sysUncert:
                
                sys_cov_up = tunfolder.GetEmatrixSysUncorr("cov_%s_up"%sys+ivar)
                sys_cov_down = tunfolder.GetEmatrixSysUncorr("cov_%s_down"%sys+ivar)
                '''
                if sys in jes_uncorr_list and year.startswith('all') and sys not in jes_corr_list: 
                    
                    print('|------> TUnfolding extracting %sUnc info to root file but from per year unfoldings'%sys)
                    s = [i for i in sysSignalLabels if sys in i]
                    #print (s)
                        
                    if ('2017' in sys or '2018' in sys) and len(s)>1:
                        print ("this list should have only one item, 2.0")
                    else:
                        s=[s[0]]
                    
                    dictUncHistos[sys+'Up'] = sysSignalHistos[s[0]+'_reco'+ivar+sys+'Up'+sel].Clone()
                    dictUncHistos[sys+'Down'] = sysSignalHistos[s[0]+'_reco'+ivar+sys+'Down'+sel].Clone()
                        
                    for upDown in [ 'Up', 'Down' ]:
                        #print (sys+upDown)
                        
                        uncerUnfoldHisto[ivar+sys+upDown] = dictUncHistos[sys+upDown]#tunfolder.GetDeltaSysSource(sys+upDown, "unfoldHisto_"+ivar+sys+upDown+"shift", "-1#sigma")
                        try: uncerUnfoldHisto[ivar+sys+upDown].SetLineStyle(1)
                        except ReferenceError: uncerUnfoldHisto.pop( ivar+sys+upDown, None )
                        

                    # Create total uncertainty and sys uncertainty plots.
                    uncerUnfoldHisto[ivar+sys.upper()+'Total'] = allHistos[ 'unfoldHisto'+ivar ].Clone()       # Syst uncertainty
                    uncerUnfoldHisto[ivar+sys.upper()+'Total'].Reset()
                    for i in range( 0, allHistos[ 'unfoldHisto'+ivar ].GetNbinsX() + 1):
                        try: yup = abs(  uncerUnfoldHisto[ivar+sys+'Up'].GetBinContent(i) )
                        except KeyError: yup = 0
                        try: ydn = abs( uncerUnfoldSystCov['systcov_'+ivar+sys+'Down'].GetBinContent(i,i) )
                        except KeyError: ydn = 0
                                                        
                        dy = 0.5*(yup + ydn) 
                        uncerUnfoldHisto[ivar+sys.upper()+'Total'].SetBinContent( i, dy )
                    print ("Done with adding %s to tot syst unc"%sys )    
                    
                
                if sys in jes_corr_list and year.startswith('all') and sys not in jes_uncorr_list:
                    
                    tunfolder.GetEmatrixSysSource(sys_cov_up, "systcov_"+ivar+sys+'Up'+"shift")
                    tunfolder.GetEmatrixSysSource(sys_cov_down, "systcov_"+ivar+sys+'Down'+"shift")
                    
                    #print (tunfolder.GetEmatrixSysSource(sys_cov_up, "systcov_"+ivar+sys+'Up'+"shift"))
                    uncerUnfoldSystCov['systcov_'+ivar+sys+'Up'] = sys_cov_up.Clone()
                    uncerUnfoldSystCov['systcov_'+ivar+sys+'Down'] = sys_cov_down.Clone()

                    
                    for upDown in [ 'Up', 'Down' ]:
                        #print (sys+upDown)
                        uncerUnfoldHisto[ivar+sys+upDown] = tunfolder.GetDeltaSysSource(sys+upDown, "unfoldHisto_"+ivar+sys+upDown+"shift", "-1#sigma")
                        try: uncerUnfoldHisto[ivar+sys+upDown].SetLineStyle(1)
                        except ReferenceError: uncerUnfoldHisto.pop( ivar+sys+upDown, None )
                        

                    # Create total uncertainty and sys uncertainty plots.
                    uncerUnfoldHisto[ivar+sys.upper()+'Total'] = allHistos[ 'unfoldHisto'+ivar ].Clone()       # Syst uncertainty
                    uncerUnfoldHisto[ivar+sys.upper()+'Total'].Reset()
                    for i in range( 0, allHistos[ 'unfoldHisto'+ivar ].GetNbinsX() + 1):
                        try: yup = abs(  uncerUnfoldHisto[ivar+sys+'Up'].GetBinContent(i) )
                        except KeyError: yup = 0
                        try: ydn = abs( uncerUnfoldSystCov['systcov_'+ivar+sys+'Down'].GetBinContent(i,i) )
                        except KeyError: ydn = 0
                                                        
                        dy = 0.5*(yup + ydn) 
                        uncerUnfoldHisto[ivar+sys.upper()+'Total'].SetBinContent( i, dy )
                    print ("Done with adding %s to tot syst unc"%sys )    
                '''
                if not sys.startswith(('_model', '_CR', '_erdON', '_mtop', '_hdamp', '_TuneCP5')):
                    #if 'jes' in sys and year.startswith('all'): continue
                    
                    tunfolder.GetEmatrixSysSource(sys_cov_up, sys+'Up')
                    tunfolder.GetEmatrixSysSource(sys_cov_down, sys+'Down')
                    
                    uncerUnfoldSystCov['systcov_'+ivar+sys+'Up'] = sys_cov_up.Clone()
                    uncerUnfoldSystCov['systcov_'+ivar+sys+'Down'] = sys_cov_down.Clone()
                    for upDown in [ 'Up', 'Down' ]:
                        #print (sys+upDown)
                        uncerUnfoldHisto[ivar+sys+upDown] = tunfolder.GetDeltaSysSource(sys+upDown, "unfoldHisto_"+ivar+sys+upDown+"shift", "-1#sigma")
                        #print (uncerUnfoldHisto[ivar+sys+upDown])
                        if uncerUnfoldHisto[ivar+sys+upDown]: uncerUnfoldHisto[ivar+sys+upDown+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+sys+upDown].Clone(),
                                                                                               allHistos [ 'unfoldHisto'+ivar ].Clone())
                        #uncerUnfoldSystCov['systcov_'+ivar+sys+upDown] = tunfolder.GetEmatrixSysSource(sys+upDown, "systcov_"+ivar+sys+upDown+"shift")
                        try: uncerUnfoldHisto[ivar+sys+upDown].SetLineStyle(1)
                        except ReferenceError: uncerUnfoldHisto.pop( ivar+sys+upDown, None )
                        

                    # Create total uncertainty and sys uncertainty plots.
                    uncerUnfoldHisto[ivar+sys.upper()+'Total'] = allHistos[ 'unfoldHisto'+ivar ].Clone()       # Syst uncertainty
                    uncerUnfoldHisto[ivar+sys.upper()+'Total'].Reset()
                    for i in range( 1, allHistos[ 'unfoldHisto'+ivar ].GetNbinsX() + 1):
                        try: yup = abs(  uncerUnfoldHisto[ivar+sys+'Up'].GetBinContent(i) )
                        except KeyError: yup = 0
                        try: ydn = abs(  uncerUnfoldHisto[ivar+sys+'Down'].GetBinContent(i) )
                        except KeyError: ydn = 0
                                                        
                        dy = 0.5*( (yup + ydn) )
                        uncerUnfoldHisto[ivar+sys.upper()+'Total'].SetBinContent( i, dy )
                    uncerUnfoldHisto[ivar+sys.upper()+'Total'+"_shiftHist"] = get_syst_shifted_hist( uncerUnfoldHisto[ivar+sys.upper()+'Total'].Clone(),
                                                                                                    allHistos [ 'unfoldHisto'+ivar ].Clone())
                    #print ("Done with adding %s to tot syst unc"%sys )    

                elif sys.startswith('_model'):
                    #if not process.startswith('MCSelfClosure'):
                    uncerUnfoldHisto[ivar+'_Physics ModelTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_modelUncTotal')
                    uncerUnfoldHisto[ivar+'_Physics ModelTotal'].Reset()
                    tmpModelHisto = tunfolder.GetDeltaSysSource('modelUncTotal', "unfoldHisto_"+ivar+"_modelUncTotalshift", "-1#sigma")
                    #uncerUnfoldHisto[ivar+'_Physics Model'+"_shiftHist"] = get_syst_shifted_hist(tmpModelHisto.Clone().Clone(),
                    #                                                                                allHistos [ 'unfoldHisto'+ivar ].Clone())
                    tunfolder.GetEmatrixSysSource(sys_cov_up, "modelUncTotal")
                    uncerUnfoldSystCov['systcov_'+ivar+'_Physics ModelTotal'] = sys_cov_up.Clone()
                    for i in range( 1, tmpModelHisto.GetNbinsX() + 1):
                        uncerUnfoldHisto[ivar+'_Physics ModelTotal'].SetBinContent( i, abs(tmpModelHisto.GetBinContent(i)))
                    uncerUnfoldHisto[ivar+'_Physics Model'+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+'_Physics ModelTotal'].Clone(),
                                                                                                    allHistos [ 'unfoldHisto'+ivar ].Clone())
                    #print('_modelUncTotal')
                    
                elif sys.startswith('_Tune'):
                    tunfolder.GetEmatrixSysSource(sys_cov_up, '_TuneCP5Up')
                    tunfolder.GetEmatrixSysSource(sys_cov_down, '_TuneCP5Down')
                    
                    uncerUnfoldSystCov['systcov_'+ivar+'_TuneCP5Up'] = sys_cov_up.Clone()
                    uncerUnfoldSystCov['systcov_'+ivar+'_TuneCP5Down'] = sys_cov_down.Clone()
                    for s in ['_TuneCP5Up', '_TuneCP5Down' ]:
                        uncerUnfoldHisto[ivar+s] = tunfolder.GetDeltaSysSource(s, "unfoldHisto_" + ivar + "%sshift"%s, "-1#sigma")
                        if uncerUnfoldHisto[ivar+s]: uncerUnfoldHisto[ivar+s+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+s].Clone(),
                                                                         allHistos [ 'unfoldHisto'+ivar ].Clone())

                    uncerUnfoldHisto[ivar+'_UE tuneTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_TuneCP5Up')
                    uncerUnfoldHisto[ivar+'_UE tuneTotal'].Reset()

                    for i in range( 1, uncerUnfoldHisto[ivar+'_UE tuneTotal'].GetNbinsX() + 1):
                        try: yup = abs(uncerUnfoldHisto[ivar+'_TuneCP5Up'].GetBinContent(i) )
                        except KeyError: yup = 0
                        try: ydn = abs( uncerUnfoldHisto[ivar+'_TuneCP5Down'].GetBinContent(i) )
                        except KeyError: ydn = 0
                        dy = 0.5*(yup + ydn) 
                        uncerUnfoldHisto[ivar+'_UE tuneTotal'].SetBinContent( i, dy )
                    uncerUnfoldHisto[ivar+'_UE tuneTotal'+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+'_UE tuneTotal'].Clone(),
                                                                                                    allHistos [ 'unfoldHisto'+ivar ].Clone())

                elif sys.startswith('_hdamp'):
                    tunfolder.GetEmatrixSysSource(sys_cov_up, '_hdampUP')
                    tunfolder.GetEmatrixSysSource(sys_cov_down, '_hdampDOWN')
                    
                    uncerUnfoldSystCov['systcov_'+ivar+'_hdampUP'] = sys_cov_up.Clone()
                    uncerUnfoldSystCov['systcov_'+ivar+'_hdampDown'] = sys_cov_down.Clone()
                    for s in ['_hdampUP', '_hdampDOWN' ]:
                        uncerUnfoldHisto[ivar+s] = tunfolder.GetDeltaSysSource(s, "unfoldHisto_" + ivar + "%sshift"%s, "-1#sigma")
                        if uncerUnfoldHisto[ivar+s]: uncerUnfoldHisto[ivar+s+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+s].Clone(),
                                                                         allHistos [ 'unfoldHisto'+ivar ].Clone())

                    uncerUnfoldHisto[ivar+'_hdampTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_hdampUP')
                    uncerUnfoldHisto[ivar+'_hdampTotal'].Reset()

                    for i in range( 1, uncerUnfoldHisto[ivar+'_hdampTotal'].GetNbinsX() + 1):
                        #uncerUnfoldHisto[ivar+'_Colour reconnectionTotal'].SetBinContent( i, abs(tmpModelHisto.GetBinContent(i)) )
                        try: yup = abs(uncerUnfoldHisto[ivar+'_hdampUP'].GetBinContent(i) )
                        except KeyError: yup = 0
                        try: ydn = abs(uncerUnfoldHisto[ivar+'_hdampDOWN'].GetBinContent(i) )
                        except KeyError: ydn = 0
                        dy = 0.5*(yup + ydn) 
                        uncerUnfoldHisto[ivar+'_hdampTotal'].SetBinContent( i, dy )
                    uncerUnfoldHisto[ivar+'_hdampTotal'+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+'_hdampTotal'].Clone(),
                                                                                                    allHistos [ 'unfoldHisto'+ivar ].Clone())


                elif sys.startswith(('_CR','_erdON')):
                    #if not process.startswith('MCSelfClosure'):
                    tunfolder.GetEmatrixSysSource(sys_cov_up, '_CR1')
                    tunfolder.GetEmatrixSysSource(sys_cov_down,'_CR2')
                    
                    uncerUnfoldSystCov['systcov_'+ivar+'_CR1'] = sys_cov_up.Clone()
                    uncerUnfoldSystCov['systcov_'+ivar+'_CR2'] = sys_cov_down.Clone()
                    
                    
                    tunfolder.GetEmatrixSysSource(sys_cov_down, '_erdON')
                    uncerUnfoldSystCov['systcov_'+ivar+'_erdON'] = sys_cov_down.Clone()
                    
                    for CR in ['_CR1', '_CR2', '_erdON' ]:
                        uncerUnfoldHisto[ivar+CR] = tunfolder.GetDeltaSysSource(CR, "unfoldHisto_" + ivar + "%sshift"%CR, "-1#sigma")
                        if uncerUnfoldHisto[ivar+CR]: uncerUnfoldHisto[ivar+CR+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+CR].Clone(),
                                                                                       allHistos [ 'unfoldHisto'+ivar ].Clone())

                    uncerUnfoldHisto[ivar+'_CRTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_CR1')
                    uncerUnfoldHisto[ivar+'_CRTotal'].Reset()

                    for i in range( 1, uncerUnfoldHisto[ivar+'_CRTotal'].GetNbinsX() + 1):
                        #uncerUnfoldHisto[ivar+'_Colour reconnectionTotal'].SetBinContent( i, abs(tmpModelHisto.GetBinContent(i)) )
                        unfHistoBC = allHistos['unfoldHisto'+ivar].GetBinContent(i)
                        yup = (abs(uncerUnfoldHisto[ivar+'_CR1'].GetBinContent(i) )) #mnemonics for fun
                        ydn = (abs(uncerUnfoldHisto[ivar+'_CR2'].GetBinContent(i) ))
                        ymid = (abs(uncerUnfoldHisto[ivar+'_erdON'].GetBinContent(i) ))
                        dy = np.max([yup,ydn,ymid])-unfHistoBC
                        uncerUnfoldHisto[ivar+'_CRTotal'].SetBinContent( i, dy ) # considering uncertainty as an envelope
                    uncerUnfoldHisto[ivar+'_CRTotal'+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+'_CRTotal'].Clone(),
                                                                                                    allHistos [ 'unfoldHisto'+ivar ].Clone())

                    #print('_CRTotal')

                #elif sys.startswith('_erdON'):
                #    #if not process.startswith('MCSelfClosure'):
                #    uncerUnfoldHisto[ivar+'_erdONTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_erdON')
                #    uncerUnfoldHisto[ivar+'_erdONTotal'].Reset()
                #    tmpModelHisto = tunfolder.GetDeltaSysSource('_erdON', "unfoldHisto_"+ivar+"_erdONshift", "-1#sigma")
                #    for i in range( 0, tmpModelHisto.GetNbinsX() + 1):
                #        uncerUnfoldHisto[ivar+'_erdONTotal'].SetBinContent( i, abs(tmpModelHisto.GetBinContent(i)) )
                #    #print('_erdONTotal')

                elif sys.startswith('_mtop'):
                    tunfolder.GetEmatrixSysSource(sys_cov_up, '_mtop173p5')
                    tunfolder.GetEmatrixSysSource(sys_cov_down, '_mtop171p5')
                    
                    uncerUnfoldSystCov['systcov_'+ivar+'_mtop171p5'] = sys_cov_down.Clone()
                    uncerUnfoldSystCov['systcov_'+ivar+'_mtop173p5'] = sys_cov_up.Clone()
                    
                    for m,l in zip(mass_list,['Down','Up']):
                        print ("mtop:", m,l)
                        uncerUnfoldHisto[ivar+'_mtop%s'%m] = tunfolder.GetDeltaSysSource('_mtop%s'%m, "unfoldHisto_"+ivar+"_mtop%sshift"%m, "-1#sigma")
                        if uncerUnfoldHisto[ivar+'_mtop%s'%m]: uncerUnfoldHisto[ivar+'_mtop%s'%l+'_shiftHist'] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+'_mtop%s'%m].Clone(),
                                                                                                  allHistos [ 'unfoldHisto'+ivar ].Clone())
                    uncerUnfoldHisto[ivar+'_Top MassTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_mtop171p5')
                    uncerUnfoldHisto[ivar+'_Top MassTotal'].Reset()

                    #if not process.startswith('MCSelfClosure'):
                    for i in range( 0, uncerUnfoldHisto[ivar+'_Top MassTotal'].GetNbinsX() + 1):
                        yup = (abs( uncerUnfoldHisto[ivar+'_mtop173p5'].GetBinContent(i) ))
                        ydn = (abs( uncerUnfoldHisto[ivar+'_mtop171p5'].GetBinContent(i) ))
                        dy = np.max([yup,ydn])-np.min([yup,ydn])
                        uncerUnfoldHisto[ivar+'_Top MassTotal'].SetBinContent( i, dy ) # considering uncertainty as an envelope
                    uncerUnfoldHisto[ivar+'_Top MassTotal'+"_shiftHist"] = get_syst_shifted_hist(uncerUnfoldHisto[ivar+'_Top MassTotal'].Clone(),
                                                                                                    allHistos [ 'unfoldHisto'+ivar ].Clone())
                    
        #####################################################################################################################################################
        
        #print (uncerUnfoldSystCov)
        
        ################################################################################  Get various covariances  ###########################################################################################################
        '''
        GetEmatrixSysUncorr(): uncorrelated errors on the input matrix histA, taken as the errors provided with the histogram. These are typically statistical errors from finite Monte Carlo samples.
        GetEmatrixSysSource()(GetDeltaSysSource()): correlated shifts of the input matrix histA. These shifts are taken as one-sigma effects when switchig on a given error soure. Several such error sources may be defined
        GetEmatrixSysBackgroundUncorr(): uncorrelated errors on background sources, originating from the errors provided with the background histograms
        GetEmatrixInput(): statistical uncertainty of the input (the measurement)
        
        '''
        #print ("Here's a list of all available uncerUnfoldHistos:", uncerUnfoldHisto)
        print ('|------> TUnfolding covariances')
        allHistos[ 'cov'+ivar ] = tunfolder.GetEmatrixTotal("cov"+ivar, "Total Covariance Matrix")
        allHistos[ 'cov_uncorr_data_'+ivar ] = tunfolder.GetEmatrixInput("cov_uncorr_data"+ivar, "Covariance Matrix coming from input data distributions")
        allHistos[ 'cov_uncorr_'+ivar ] = tunfolder.GetEmatrixSysUncorr("cov_uncorr"+ivar, "Covariance Matrix at hadron level coming from RM")
        allHistos[ 'cov_uncorr_bkg_'+ivar ] = tunfolder.GetEmatrixSysBackgroundUncorr('fakes', "Covariance Matrix from uncorrelated errors of Background sources")
        
        if process.startswith('data'):
            if sel.startswith(('_W','_top')):
                for ibkg in bkgSources:
                    if 'fakes' not in ibkg: allHistos[ 'cov_uncorr_bkg_'+ivar ].Add(tunfolder.GetEmatrixSysBackgroundUncorr(ibkg, "Covariance Matrix from uncorrelated errors of Background sources"))
        
        #### cov = cov_uncorr + cov_uncorr_data + other uncertaitnies
        #### stat = cov_uncorr + cov_uncorr_data
        
        

        
        ############### Build correlation matrix for unfolding#################################
        allHistos['correlation_matrix_'+ivar] = allHistos[ 'cov'+ivar ].Clone()
        allHistos['correlation_matrix_'+ivar].Reset()
        allHistos['correlation_matrix_'+ivar] = correlation_from_covariance(allHistos[ 'cov'+ivar ].Clone(),allHistos['correlation_matrix_'+ivar])
        
        
        '''
        for ibinx in range( 1, allHistos[ 'cov'+ivar ].GetNbinsX()):
            variance = allHistos[ 'cov'+ivar ].GetBinContent(ibinx,ibinx)

            for ibiny in range( 1, allHistos[ 'cov'+ivar ].GetNbinsY()):
                cov_xy = allHistos[ 'cov'+ivar ].GetBinContent(ibinx,ibiny)
                if variance!=0: 
                    allHistos['correlation_matrix_'+ivar].SetBinContent(ibinx,ibiny,cov_xy/variance)
        '''
        ########################################################################################    
        
        # Create total uncertainty and sys uncertainty histos for plots 
        
        # first build up histos of systematic uncertainties from the BACKGROUND SUBTRACTION 
        uncerUnfoldHisto[ivar+'_BkgTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_BkgTotal')
        uncerUnfoldHisto[ivar+'_BkgTotal'].Reset()
        for ibin in range( 1, allHistos[ 'unfoldHisto'+ivar ].GetNbinsX()+1 ):
            bkg_tot = np.sqrt(allHistos[ 'cov_uncorr_bkg_'+ivar ].GetBinContent(ibin,ibin))
            uncerUnfoldHisto[ivar+'_BkgTotal'].SetBinContent(ibin, bkg_tot)
            
        # second build up histos of total systematic uncertainties
        uncerUnfoldHisto[ivar+'_SystTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_SystTotal')
        uncerUnfoldHisto[ivar+'_SystTotal'].Reset()        
        
        tmp = OrderedDict()
        dummyM = hist2array(allHistos[ 'cov'+ivar ].Clone())
        print (dummyM.shape)
        systcovTotal = np.zeros(dummyM.shape)
        #print (systcovTotal.shape)
        for k in uncerUnfoldHisto:
            corrflag = False
            sysErr=np.zeros(uncerUnfoldHisto[k].GetNbinsX())
            if not k.endswith('Total') or k.endswith(('SystTotal')): continue

            for x in jes_corr_list:
                if corrflag==True: break
                if x.upper() in k:
                    corrflag=True
                    continue
                    
            #print ("CORRFLAG",corrflag)
            for i in range( 0, uncerUnfoldHisto[k].GetNbinsX()):


                sysErr[i] = uncerUnfoldHisto[k].GetBinContent(i+1)
                if corrflag: 
                    systcovTotal+=np.outer(sysErr,sysErr)
                    #print ("CORRFLAG",corrflag)
                else: systcovTotal+=np.diag(sysErr*sysErr)

        #print (systcovTotal.shape,corrflag)

        allHistos['cov_systTotal'+ivar] = allHistos[ 'cov'+ivar ].Clone()
        allHistos['cov_systTotal'+ivar].Reset()
        allHistos['cov_systTotal'+ivar] = array2hist(systcovTotal,allHistos['cov_systTotal'+ivar])
        
        tmp = OrderedDict()
        for i in range( 1, allHistos[ 'unfoldHisto'+ivar ].GetNbinsX() + 1):
            tmp[i] = 0
            for k in uncerUnfoldHisto:
                if k.endswith('Total') and not k.endswith(('SystTotal')):
                    tmp[i] = tmp[i] + ( uncerUnfoldHisto[k].GetBinContent( i )**2 )
                    #print(i, k, tmp[i], uncerUnfoldHisto[k].GetBinContent( i ), ( uncerUnfoldHisto[k].GetBinContent( i )**2 ))
        
        # adding covariances from bkg subtraction and RM finite stats to the overall systematics covariance matrix
        
                
        allHistos['cov_systTotal'+ivar].Add(allHistos[ 'cov_uncorr_'+ivar ])
        allHistos['cov_systTotal'+ivar].Add(allHistos[ 'cov_uncorr_bkg_'+ivar ])
        
        if len(sysUncert)>0: 
            for i,j in tmp.items():
                uncerUnfoldHisto[ivar+'_SystTotal'].SetBinContent( i, ROOT.TMath.Sqrt( j ) )    
                    
        #storing unnormalized unfoldings and uncs here, 
        #will normalize unfoldHisto and unc plot objects in the draw functions    
        
        
        uncerUnfoldHisto[ivar+'_StatTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_StatTotal')
        uncerUnfoldHisto[ivar+'_StatTotal'].Reset()
        uncerUnfoldHisto[ivar+'_TotalUnc'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_TotalUnc')
        uncerUnfoldHisto[ivar+'_TotalUnc'].Reset()
        
        uncerUnfoldHisto[ivar+'_CMErrTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_CMErrTotal')
        uncerUnfoldHisto[ivar+'_CMErrTotal'].Reset()
        uncerUnfoldHisto[ivar+'_CMMCStatErrTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_CMMCStatErrTotal')
        uncerUnfoldHisto[ivar+'_CMMCStatErrTotal'].Reset()
        uncerUnfoldHisto[ivar+'_CMDataStatErrTotal'] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+'_CMDataStatErrTotal')
        uncerUnfoldHisto[ivar+'_CMDataStatErrTotal'].Reset()
        
        
        allHistos[ 'unfoldHistowoUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone()        # No unc
        allHistos[ 'unfoldHistoStatUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+"unfoldHistoStatUnc")     # Unfolding and stat unc
        allHistos[ 'unfoldHistoBkgUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+"unfoldHistoBkgStatUnc")   # Bkg subtraction unc.
        allHistos[ 'unfoldHistoSystUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone(ivar+"unfoldHistoSystUnc")     # Unc. from systematics and variations
        #allHistos[ 'unfoldHistoTotUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone("unfoldHistoTotUnc")       # Total uncertainty

        
        ratioHistos = OrderedDict()
        ratioHistos[ 'StatUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone('StatUnc'+ivar)   
        ratioHistos[ 'StatUnc'+ivar ].Reset()
        ratioHistos[ 'TotalUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone('TotalUnc'+ivar)   
        ratioHistos[ 'TotalUnc'+ivar ].Reset()
        ratioHistos[ 'SystUnc'+ivar ] = allHistos[ 'unfoldHisto'+ivar ].Clone('SystUnc'+ivar)
        ratioHistos[ 'SystUnc'+ivar ].Reset()
        
        #print ("BC of unfHist", "systot+cov in quadrature", "tot from cov", "syst tot", 'stat+unf unc from unfhisto')
        
        for ibin in range( 1, allHistos[ 'unfoldHisto'+ivar ].GetNbinsX()+1 ):
            
            unc_tot = np.sqrt( allHistos[ 'cov'+ivar ].GetBinContent(ibin,ibin) ) #total error extracted from from total error matrix from TUnfold
            bkg_tot = np.sqrt(allHistos[ 'cov_uncorr_bkg_'+ivar ].GetBinContent(ibin,ibin))
            datastat_tot = np.sqrt( allHistos[ 'cov_uncorr_data_'+ivar ].GetBinContent(ibin,ibin))
            rmstat_tot = np.sqrt( allHistos[ 'cov_uncorr_'+ivar ].GetBinContent(ibin,ibin))
            #if len(sysUncert)>0: syst_tot = uncerUnfoldHisto[ivar+'_SystTotal'].GetBinContent(ibin)
            #else: syst_tot=0
            orig_statunfunc = allHistos[ 'unfoldHisto'+ivar ].GetBinError(ibin) #obtain the stat + unf uncertatinties directly from output (which by default contains no systematics)
            
            norm_unc = abs(allHistos[ 'unfoldHisto'+ivar ].GetBinContent(ibin))
            if unc_tot<=0.: 
                unc_tot=0.
            if datastat_tot<=0.: 
                datastat_tot=0.
            if rmstat_tot<=0.: 
                rmstat_tot=0.
               
            
            allHistos[ 'unfoldHisto'+ivar ].SetBinError(ibin, unc_tot)
            allHistos[ 'unfoldHistoBkgUnc'+ivar ].SetBinError(ibin, bkg_tot )
            allHistos[ 'unfoldHistowoUnc'+ivar ].SetBinError(ibin, 0. )        # No unc
        
            uncerUnfoldHisto[ivar+'_TotalUnc'].SetBinContent(ibin, unc_tot )
            uncerUnfoldHisto[ivar+'_CMErrTotal'].SetBinContent(ibin, unc_tot )
            uncerUnfoldHisto[ivar+'_CMMCStatErrTotal'].SetBinContent(ibin, rmstat_tot)
            uncerUnfoldHisto[ivar+'_CMDataStatErrTotal'].SetBinContent(ibin, datastat_tot)
            #uncerUnfoldHisto[ivar+'_StatTotal'].SetBinContent(ibin, orig_statunfunc)
            
            ratioHistos[ 'TotalUnc'+ivar ].SetBinContent( ibin, 1. )
            ratioHistos[ 'StatUnc'+ivar ].SetBinContent( ibin, 1. )
            #ratioHistos[ 'SystUnc'+ivar ].SetBinContent( ibin, 1. )

            if norm_unc!=0:
                ratioHistos[ 'TotalUnc'+ivar ].SetBinError( ibin, unc_tot)#+syst_tot**2
                ratioHistos[ 'StatUnc'+ivar ].SetBinError( ibin, datastat_tot)
                #if len(sysUncert)>0: ratioHistos[ 'SystUnc'+ivar ].SetBinError( ibin, syst_tot/norm_unc)
            #print (norm_unc, np.sqrt(unc_tot**2 ), unc_tot, orig_statunfunc)

        allHistos [ 'foldHisto'+ivar ] = get_folded_unfolded(folded=tunfolder.GetFoldedOutput("folded"+ivar).Clone(),
                                                            unfolded=allHistos['unfoldHisto'+ivar].Clone(), 
                                                            cov_tot=allHistos['cov'+ivar].Clone(), 
                                                             probaM=allHistos[ 'probaMatrix'+ivar ]
                                                            
                                                             )
        
        
        #####################################
        #print (allHistos[ 'unfoldHisto'+ivar ].Clone())
        ###### Plot unfolding results

        print ('|------> Drawing unfold plot:')
        if not 'Closure' in process:
            drawUnfold(ivar=ivar, 
                       selection=sel, year=year,
                       process=process,
                       dataJetHisto=allHistos[ 'dataHistoGenBin' ].Clone(),
                       genJetHisto=signalHistos[ signalLabel+'_accepgen'+ivar+sel ].Clone(),
                       unfoldHisto=allHistos[ 'unfoldHisto'+ivar ].Clone(),
                       unfoldHistowoUnc=allHistos[ 'unfoldHistowoUnc'+ivar ].Clone(),
                       foldHisto=tunfolder.GetFoldedOutput("folded"+ivar).Clone(),
                       recoJetHisto=signalHistos[ signalLabel+'_reco'+ivar+'_nom'+sel+'_genBin' ].Clone(),
                       cov_datastat_tot=allHistos['cov_uncorr_data_'+ivar].Clone(),#ratiototUncHisto=ratioHistos[ 'TotalUnc'+ivar ].Clone(),
                       cov_tot=allHistos['cov'+ivar].Clone(),#ratioUncHisto=ratioHistos[ 'StatUnc'+ivar ].Clone(),
                       #ratiosystUncHisto =ratioHistos[ 'SystUnc'+ivar ].Clone(),
                       altMCHisto =  altSignalHistos[altSignalLabel+'_accepgen'+ivar+sel].Clone(),
                       labelX=variables[ivar]['label'],
                       maxX=variables[ivar]['bins'][-1],
                       tlegendAlignment=variables[ivar]['alignLeg'],
                       
                       outputName=outputDir+ivar+sel+'_from'+('Data' if process.startswith('data') else 'MC')+signalLabel+'_TUnfold_'+version+'.'+ext
                       )
        else: 
            if 'Cross' in process:
                drawClosures(ivar=ivar, selection=sel, year=year, process=process,
                             
                             genJetHistoCross=altSignalHistos[altSignalLabel+'_accepgen'+ivar+sel].Clone(), 
                             unfoldHistoCross=allHistos[ 'unfoldHistoCross'+ivar ].Clone() ,
                             
                             genJetHisto=signalHistos[ signalLabel+'_accepgen'+ivar+sel ].Clone(),
                             unfoldHisto=allHistos[ 'unfoldHisto'+ivar ].Clone(),
                             
                             ratioUncHisto=ratioHistos[ 'StatUnc'+ivar ].Clone(),
                             ratiototUncHisto=ratioHistos[ 'TotalUnc'+ivar ].Clone(),
                             ratiosystUncHisto =ratioHistos[ 'SystUnc'+ivar ].Clone(),
                             labelX=variables[ivar]['label'],
                             maxX=variables[ivar]['bins'][-1],
                             tlegendAlignment=variables[ivar]['alignLeg'],
                             outputName=outputDir+ivar+sel+'_from'+process+signalLabel+'_TUnfold_'+version+'.'+ext
                             )
            else:
                drawClosures(ivar=ivar, selection=sel, year=year, process=process,
                             genJetHistoCross=[], 
                             unfoldHistoCross=[] ,
                             genJetHisto=signalHistos[ signalLabel+'_accepgen'+ivar+sel ].Clone(),
                             unfoldHisto=allHistos[ 'unfoldHisto'+ivar ].Clone(),
                             ratioUncHisto=ratioHistos[ 'StatUnc'+ivar ].Clone(),
                             ratiototUncHisto=ratioHistos[ 'TotalUnc'+ivar ].Clone(),
                             ratiosystUncHisto =ratioHistos[ 'SystUnc'+ivar ].Clone(),
                             labelX=variables[ivar]['label'],
                             maxX=variables[ivar]['bins'][-1],
                             tlegendAlignment=variables[ivar]['alignLeg'],
                             outputName=outputDir+ivar+sel+'_from'+process+signalLabel+'_TUnfold_'+version+'.'+ext
                             )
                
        ######### Plotting Uncertainties
        print ('|------> Drawing unfolding uncertainty plot:')
        
        if not 'Closure' in process: drawUncertainties_normalizedshifts(ivar=ivar,unfoldHistoTotUnc=allHistos[ 'unfoldHisto'+ivar ].Clone(),
                                                                        unfoldHistowoUnc=allHistos[ 'unfoldHistowoUnc'+ivar ],
                                                                        uncerUnfoldHisto=uncerUnfoldHisto, 
                                                                        cov_tot=allHistos['cov'+ivar].Clone(), 
                                                                        cov_datastat_tot=allHistos['cov_uncorr_data_'+ivar].Clone(), 
                                                                        cov_rmstat_tot=allHistos['cov_uncorr_'+ivar].Clone(), 
                                                                        cov_bkg_tot=allHistos['cov_uncorr_bkg_'+ivar].Clone(),
                                                                        labelX=variables[ivar]['label'], 
                                                                        tlegendAlignment=variables[ivar]['alignLeg'],
                                                                        outputName=outputDir+ivar+sel+'_from'+('Data' if process.startswith('data') else 'MC')+'_Tunfold_UNC_'+version+'.'+ext,
                                                                        year=year, unftot=unfoldingtot
                                                                        )
        
        ######### Plotting 2D matrices of various kinds
        print ('|------> Drawing various 2D matrices:')
        draw2D( ivar,  tunfolder.GetRhoItotal("rhoI"+ivar, "Global correlations"), variables[ivar], outputLabel='data_rhoI', outputDir=outputDir)
        draw2D( ivar,  allHistos[ 'correlation_matrix_'+ivar ].Clone(), variables[ivar], outputLabel='data_correlationMatrix', outputDir=outputDir)
        draw2D( ivar,  allHistos[ 'probaMatrix'+ivar ].Clone(), variables[ivar], outputLabel='data_probaMatrix', outputDir=outputDir, addCorrelation=True, addCondition=True )
        draw2D( ivar, signalHistos[signalLabel+'_resp'+ivar+'_nom'+sel].Clone(), variables[ivar], outputLabel='data_respMatrix', outputDir=outputDir, addCorrelation=True )
        draw2D( ivar, allHistos[ 'cov'+ivar].Clone(), variables[ivar], outputLabel='dataTotal_covMatrix', outputDir=outputDir, addCorrelation=True)
        draw2D( ivar, allHistos[ 'cov_uncorr_'+ivar].Clone(), variables[ivar], outputLabel='uncorrUncRM_covMatrix', outputDir=outputDir, addCorrelation=True)
        draw2D( ivar, allHistos[ 'cov_uncorr_data_'+ivar].Clone(), variables[ivar], outputLabel='dataInpStats_covMatrix', outputDir=outputDir, addCorrelation=True)
        draw2D( ivar, allHistos[ 'cov_uncorr_bkg_'+ivar].Clone(), variables[ivar], outputLabel='BkgSubtractionSyst_covMatrix', outputDir=outputDir, addCorrelation=True)
        draw2D( ivar, allHistos[ 'cov_systTotal'+ivar].Clone(), variables[ivar], outputLabel='Syst_covMatrix', outputDir=outputDir, addCorrelation=True)

        normed_covs = OrderedDict()
        for i in allHistos:
            if 'cov' in i: 
                _, normed_covs['Normed'+i] = GetNormalizedTMatrixandTH2( allHistos[i].Clone(), allHistos[i].GetTitle()+'Normed',
                                                            allHistos['unfoldHisto'+ivar].Clone() )
                #normed_covs.append(normed_cov)
                draw2D( ivar, normed_covs['Normed'+i].Clone(), variables[ivar], outputLabel='Normed_'+i, outputDir=outputDir)
        
        ############### Build correlation matrix for unfolding#################################
        allHistos['Normed_correlation_matrix_'+ivar] = allHistos[ 'cov'+ivar ].Clone()
        allHistos['Normed_correlation_matrix_'+ivar].Reset()
        allHistos['Normed_correlation_matrix_'+ivar] = correlation_from_covariance(normed_covs[ 'Normed'+'cov'+ivar ].Clone(),allHistos['correlation_matrix_'+ivar])
        draw2D( ivar,  allHistos['Normed_correlation_matrix_'+ivar].Clone(), variables[ivar], outputLabel='Normed_data_correlationMatrix', outputDir=outputDir)

    
        '''
        draw2D( ivar, normed_cov['Normed'+'cov_uncorr_'+ivar].Clone(), variables[ivar], outputLabel='Normed_uncorrUncRM_covMatrix', outputDir=outputDir, addCorrelation=True)
        draw2D( ivar, normed_cov['Normed'+'cov_uncorr_data_'+ivar].Clone(), variables[ivar], outputLabel='Normed_dataInpStats_covMatrix', outputDir=outputDir, addCorrelation=True)
        draw2D( ivar, normed_cov['Normed'+'cov_uncorr_bkg_'+ivar].Clone(), variables[ivar], outputLabel='Normed_BkgSubtractionSyst_covMatrix', outputDir=outputDir, addCorrelation=True)
        draw2D( ivar, normed_cov['Normed'+'cov_systTotal'+ivar].Clone(), variables[ivar], outputLabel='Normed_Syst_covMatrix', outputDir=outputDir, addCorrelation=True)
        '''
        
        
        ######### Saving Histograms
        def renamingHistos( dictHistos ):
            for isam, hist in dictHistos.items():
                ihis = hist.Clone()
                ihis.SetName(isam)
                ihis.SetTitle(isam)
                ihis.Write()

        outputRootName = outputDir+'/outputHistograms_main_'+signalLabel+'_alt_'+altSignalLabel+'.root'
        #print ('|------> Saving histograms in rootfile: ', outputRootName)
        outputRoot = ROOT.TFile.Open( outputRootName, 'recreate' )
        renamingHistos( signalHistos )
        if not process.startswith('MCSelfClosure'):
            renamingHistos( sysSignalHistos )
            renamingHistos( altSignalHistos )
        if process.startswith('data') and  selection.startswith(('_W','_top')): 
            renamingHistos( varSignalHistos )
            renamingHistos(uncerUnfoldSystCov)
            renamingHistos(normed_covs)
        #renamingHistos( dataHistos )
        #print ("adding varsighistos", varSignalHistos.items())
        renamingHistos( dataHistos )
        renamingHistos( bkgHistos )
        renamingHistos( allHistos )
        renamingHistos( uncerUnfoldHisto )
        
        tunfolder.Write()
        outputRoot.Close()

        #print ('|------> Saving histograms in yodafile: ', outputRootName.replace('.root', '.yoda'))
        #histToYoda = [  yoda.root.to_yoda( allHistos [ 'unfoldHisto'+ivar ] ) ]
        #yoda.writeYODA( histToYoda, outputRootName.replace('.root', '.yoda') )


In [29]:
import yoda
from yoda import *


In [30]:
import gc

In [31]:
def loadFiles(year):
    
    #### Files
    dataFile = {}
    sigFiles = {}
    bkgFiles = {}
    sysSigFiles = {}
    varSigFiles = {}
    lumi=0.    
    ### Lumi

    for iy in ( ['2017', '2018'] if year.startswith('all') else [ year ] ):
        lumi = lumi + checkDict( ( 'JetHT' if selection.startswith('_dijet') else 'SingleMuon' ), dictSamples )[iy]['lumi']

    #### All data runs from single year files
    if year.startswith('all'):
        print('|------> Running combination of years')
        if not inputFolder:
            print('|------> For running all the data you must specify the input folder.\n Have a nice day :)')
            sys.exit(0)

        for ivar in variables.keys():
            #print (inputFolder+'/'+selection.split('_')[1]+'/2017/Unfolding/'+ivar+'/'+process+'/outputHistograms_main_'+signalLabel+'_alt_'+altSignalLabel+'.root')
            dataFile[ivar+'_2017'] = ROOT.TFile.Open( inputFolder+'/'+selection.split('_')[1]+'/2017/Unfolding/'+ivar+'/'+process+'/outputHistograms_main_'+signalLabel+'_alt_'+altSignalLabel+'.root' )
            dataFile[ivar+'_2018'] = ROOT.TFile.Open( inputFolder+'/'+selection.split('_')[1]+'/2018/Unfolding/'+ivar+'/'+process+'/outputHistograms_main_'+signalLabel+'_alt_'+altSignalLabel+'.root' )
        if selection.startswith('_dijet'):
            return lumi, dataFile, sigFiles, bkgFiles, sysSigFiles
        else:
            return lumi, dataFile, sigFiles, bkgFiles, varSigFiles, sysSigFiles
        
        
    #### Single year unfolding runs on skimmers
    else:
        print('|------> Running single year')
        
        dataFile['data'] = [ ROOT.TFile.Open(inputFolder+checkDict( ('JetHT' if selection.startswith("_dijet") else 'SingleMuon'), dictSamples )[year]['skimmerHisto']) ]
        
        
        if selection.startswith('_dijet'):
            jesList = [i.split('_HT')[0] for i in sysSignalLabels if 'jes' in i ]
            jes_year_corrList = [i for i in jesList if ('2017' in i or '2018' in i)]
            jesList = [i for i in jesList if not ('2017' in i or '2018' in i)]
            #print (jesList,jes_year_corrList)
            
            for isam in dictSamples:
            #print (isam, isam.startswith( signalLabelBegin ))
                if 'MuEnriched' in isam: continue
                try: 
                    if not checkDict( isam, dictSamples )[year]['skimmerHisto']: continue
                except KeyError: continue
                    
                if not checkDict( isam, dictSamples )[year]['skimmerHisto'].endswith('root'):continue
                
                if isam.startswith( signalLabelBegin ) and not signalLabel.startswith((sysSignalLabelBegin,altSignalLabelBegin )):
                    sigFiles[isam.split('_Tune')[0]] = [
                                    ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                    checkDict( isam, dictSamples )
                                ]

                if isam.startswith( altSignalLabelBegin ) and not ( altSignalLabel.startswith( signalLabelBegin ) ):
                    sigFiles[isam.split('_Tune')[0]] = [
                                    ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                    checkDict( isam, dictSamples )]
                    
                
            for s in sysUnc:
                #print (s)
                
                for isam in dictSamples:
                    if 'MuEnriched' in isam: continue
                    
                    try: 
                        if not checkDict( isam, dictSamples )[year]['skimmerHisto']: 
                            #print ("Samples not there", isam, year)
                            continue
                    except KeyError: continue
                    #print (isam)
                    if not(s in isam): continue

                    if (isam.startswith(sysSignalLabelBegin) and 'jes' in s and s in isam):
                        #if ('2017' in s and not '2017' in isam) or ('2018' in s and not '2018' in isam) or ('2018' in s and not '2017' in isam) or ('2017' in s and not '2018' in isam): 
                        #print (s,isam)
                        #    continue
                        if (not '2017' in s and not '2018' in s):
                            if ('2017' in isam or '2018' in isam): continue
                            else: 
                                #print ("jes",s,isam)
                                sysSigFiles[isam.split('_Tune')[0]] = [
                                                ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                                checkDict( isam, dictSamples )
                                            ] 
                            
                        else:
                            if isam.startswith(sysSignalLabelBegin) and 'jes'in isam:# and not ('2017' in isam or '2018' in isam):
                                #print ("jes",s,isam)
                                sysSigFiles[isam.split('_Tune')[0]] = [
                                                ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                                checkDict( isam, dictSamples )
                                            ] 

                    elif (isam.startswith(sysSignalLabelBegin) and s in isam) and 'jes' not in isam  :
                        #print ("No jes", isam,s)
                        sysSigFiles[isam.split('_Tune')[0]] = [
                                            ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                            checkDict( isam, dictSamples )
                                        ] 
                    
                        '''
                        elif isam.startswith(sysSignalLabelBegin) and 'jes':# and isam.startswith((tuple(jes_year_corrList))):
                            print ("jes",isam, jes_year_corrList)
                            sysSigFiles[isam.split('_Tune')[0]] = [
                                            ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                            checkDict( isam, dictSamples )
                                        ] 
                        '''    
            return lumi, dataFile, sigFiles, bkgFiles, sysSigFiles
        
        else:
            
            jesList = [i for i in sysSignalLabels if 'jes' in i ]
            #print (jesList)
                
                
            for isam in dictSamples:
                if isam.startswith(('ST', 'W', 'Z', 'TTTo2L2Nu', 'QCD')):
                    bkgFiles[isam.split('_Tune')[0]] = [
                                    ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                    checkDict( isam, dictSamples )]
            #print ("Background Files:", bkgFiles)     
            sigFiles['TTToSemiLeptonic'] = [
                                    ROOT.TFile.Open( inputFolder+checkDict( 'TTToSemiLeptonic_TuneCP5_13TeV-powheg-pythia8', dictSamples )[year]['skimmerHisto'] ),
                                    checkDict( 'TTToSemiLeptonic_TuneCP5_13TeV-powheg-pythia8', dictSamples )
                                ]
            
            for isam in dictSamples:
                if isam.startswith( altSignalLabelBegin ) and not ( altSignalLabel.startswith( signalLabelBegin ) ):
                    sigFiles['TTJets'] = [
                                    ROOT.TFile.Open( inputFolder+checkDict( 'TTJets_TuneCP5_13TeV-amcatnloFXFX-pythia8', dictSamples)[year]['skimmerHisto'] ),
                                    checkDict( 'TTJets_TuneCP5_13TeV-amcatnloFXFX-pythia8', dictSamples)]
               

            for isam in dictSamples:
                if isam.startswith( varSignalLabelBegin ) :
                    varSigFiles[isam.split('_13TeV')[0]] = [
                                        ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                        checkDict( isam, dictSamples )
                                    ]

            for isam in dictSamples:
                try: 
                    if not checkDict( isam, dictSamples )[year]['skimmerHisto']: continue
                except KeyError: continue

                
                if isam.startswith(sysSignalLabelBegin) and 'jes'not in isam :
                    sysSigFiles[isam.split('_13TeV')[0]] = [
                                        ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                        checkDict( isam, dictSamples )
                                    ] 
                else:
                    
                    for i in jesList:
                        if isam.startswith(i):
                            sysSigFiles[isam.split('_13TeV')[0]] = [
                                            ROOT.TFile.Open( inputFolder+checkDict( isam, dictSamples )[year]['skimmerHisto'] ),
                                            checkDict( isam, dictSamples )
                                        ] 


            return lumi, dataFile, sigFiles, bkgFiles, varSigFiles, sysSigFiles

In [32]:
variables = nSubVariables_dijetSel

In [30]:
taus = {
        "_tau_0p5_1": [0., 0.9, 900  ],
        "_tau_0p5_2": [0., 0.9, 900  ],
        "_tau_0p5_3": [0., 0.8, 800  ],
        "_tau_0p5_4": [0., 0.8, 800  ],
        "_tau_1_1": [ 0., 0.9, 900  ],
        "_tau_1_2": [ 0., 0.7, 700  ],
        "_tau_1_3": [ 0., 0.5, 500  ],
        "_tau_1_4": [ 0., 0.5, 500  ],
        "_tau_2_1": [ 0., 0.9, 900  ],
        "_tau_2_2": [ 0., 0.5, 500  ],
        "_tau_2_3": [ 0., 0.5, 500  ],
        "_tau_2_4": [ 0., 0.5, 500  ],
          }
file = ROOT.TFile.Open('../test/Samples/Dijet_V06/jetObservables_histograms_QCDHT1000to1500_nom_UL2017.root')
tree = file.Get('jetObservables')


for i in taus.keys()[0:1]:
    print (i)
    h_reco = tree.Get('truerecoJet1'+i+'_nom_dijetSel')
    h_resp = tree.Get('respJet1'+i+'_nom_dijetSel')
    h_gen = tree.Get('accepgenJet1'+i+'_nom_dijetSel')
    
    
TH2 *old; 
//the original histogram 
//create a new TH2 with your bin arrays spec 
double xbins[4]={0,70,130,400}; 
double ybins[4]={0,50,100,400}; 
TH2F *h = new TH2F("oldrebin",old->GetTitle(),nx,xbins,ny,ybins); 
TAxis *xaxis = old->GetXaxis(); 
TAxis *yaxis = old->GetYaxis(); 

for (int j=1; j<=yaxis->GetNbins();j++) 
    { for (int i=1; i<=xaxis->GetNbins();i++) 
         { h->Fill(xaxis->GetBinCenter(i), yaxis->GetBinCenter(j),old->GetBinContent(i,j)); } } } 
    

_tau_0p5_1
_tau_0p5_1 101 [-0.01, 0.0, 0.01, 0.02, 0.03, 0.04, 0.05, 0.06, 0.07, 0.08, 0.09, 0.1, 0.11, 0.12, 0.13, 0.14, 0.15, 0.16, 0.17, 0.18, 0.19, 0.2, 0.21, 0.22, 0.23, 0.24, 0.25, 0.26, 0.27, 0.28, 0.29, 0.3, 0.31, 0.32, 0.33, 0.34, 0.35000000000000003, 0.36, 0.37, 0.38, 0.39, 0.4, 0.41000000000000003, 0.42, 0.43, 0.44, 0.45, 0.46, 0.47000000000000003, 0.48, 0.49, 0.5, 0.51, 0.52, 0.53, 0.54, 0.55, 0.56, 0.5700000000000001, 0.58, 0.59, 0.6, 0.61, 0.62, 0.63, 0.64, 0.65, 0.66, 0.67, 0.68, 0.6900000000000001, 0.7000000000000001, 0.71, 0.72, 0.73, 0.74, 0.75, 0.76, 0.77, 0.78, 0.79, 0.8, 0.81, 0.8200000000000001, 0.8300000000000001, 0.84, 0.85, 0.86, 0.87, 0.88, 0.89, 0.9, 0.91, 0.92, 0.93, 0.9400000000000001, 0.9500000000000001, 0.96, 0.97, 0.98, 0.99]
_tau_0p5_2
_tau_0p5_2 81 [-0.01, 0.0, 0.01, 0.02, 0.03, 0.04, 0.05, 0.06, 0.07, 0.08, 0.09, 0.1, 0.11, 0.12, 0.13, 0.14, 0.15, 0.16, 0.17, 0.18, 0.19, 0.2, 0.21, 0.22, 0.23, 0.24, 0.25, 0.26, 0.27, 0.28, 0.29, 0.3, 0.31, 0.32, 0.33,

## All unfoldings

###  Unfold individual years (self-closure)

In [47]:
inputFolder = '../test/Samples/Dijet_V06/'
outputFolder = '../../../../../Results/Results_Aprilv2/'

main = 'HTbin'
alt = 'herwig'
process='MCSelfClosure'


if main.startswith('Ptbin'):
    signalLabelBegin = 'QCD_Pt_'
    signalLabel = 'QCD_Pt_3200toInf'
elif main.startswith('HTbin'):
    signalLabelBegin = 'QCD_HT'
    signalLabel = 'QCD_HT2000toInf'
elif main.startswith('herwig'):
    signalLabelBegin = 'QCD_Pt-'
    signalLabel = 'QCD_Pt-150to3000'
if alt.startswith('Ptbin'):
    altSignalLabelBegin = 'QCD_Pt_'
    altSignalLabel = 'QCD_Pt_3200toInf'
elif alt.startswith('HTbin'):
    altSignalLabelBegin = 'QCD_HT'
    altSignalLabel = 'QCD_HT2000toInf'
elif alt.startswith('herwig'):
    altSignalLabelBegin = 'QCD_Pt-'
    altSignalLabel = 'QCD_Pt150to3000'
    #altSignalLabel = 'QCD_Pt-15to7000'

sysSignalLabelBegin = 'sysQCD_' 

In [48]:
for selection in ['_dijetSel']:
    print ("#######################")
    print ("#####%s selection#####"%((selection.split('_')[1])).split('Sel')[0])
    print ("#######################")
    
    variables = nSubVariables_dijetSel
    version = '_April'
    
    if selection.startswith('_W'): sysUnc = []#'_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', '_jesTotal', '_model', '_hdamp', '_Tune', '_erdON', '_CR', '_mtop']
    elif selection.startswith('_top'): sysUnc = []#'_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', '_jesTotal', '_model', '_hdamp', '_Tune', '_erdON', '_CR', '_mtop']
    elif selection.startswith('_dijet'): sysUnc = [ ]#'_jer', '_isrWeight', '_fsrWeight', '_puWeight', '_pdfWeight', '_jesTotal', '_model' ]
 
    
    for year in (['2017', '2018']):
       
        if '2017'in year:
            
            sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2017_HT2000toInf',
                   'sysQCD_jesBBEC1_2017_HT2000toInf',
                   'sysQCD_jesEC2_2017_HT2000toInf',
                   'sysQCD_jesHF_2017_HT2000toInf',
                   'sysQCD_jesRelativeSample_2017_HT2000toInf',
                  ]
        elif '2018'in year:
            
            sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2018_HT2000toInf',
                   'sysQCD_jesBBEC1_2018_HT2000toInf',
                   'sysQCD_jesEC2_2018_HT2000toInf',
                   'sysQCD_jesHF_2018_HT2000toInf',
                   'sysQCD_jesRelativeSample_2018_HT2000toInf',
                  ]
        lumi, dataFile, sigFiles, bkgFiles, sysSigFile = loadFiles(year)
        #print (sigFiles.keys(),bkgFiles.keys(),dataFile.keys())
        print ("#######################")
        print ("#####year=%s#####"%year)
        print ("#######################")
        
        print ("#######################")
        print ("####Selection=%s#####"%selection)
        print ("#######################")
        
        runTUnfold(dataFile=dataFile, sigFiles=sigFiles, bkgFiles=bkgFiles, sysSigFiles={},
                       variables=variables, sel=selection, sysUncert=sysUnc, process=process ,ext='pdf')
        
        #runTUnfold(dataFile=dataFile, sigFiles=sigFiles, altFiles=altSigFiles, varFiles=varSigFiles, bkg=bkgFiles, sysSigFiles=sysSigFiles, 
        #               variables=variables, sel=selection, sysUncert=sysUnc,process='data' ,ext='png')
        gc.collect()

#######################
#####dijet selection#####
#######################
|------> Running single year
#######################
#####year=2017#####
#######################
#######################
####Selection=_dijetSel#####
#######################
Jet1_tau_0p5_1
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(8, 8)
|------> Drawing unfold plot:


/tmp/ipykernel_1272/681485682.py:5: RuntimeWarning: invalid value encountered in true_divide
  correlation = covariance / outer_v


|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.42
Jet1_tau_0p5_2
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_2
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  4.25
Jet1_tau_0p5_3
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D

Jet2_tau_1_4
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_1_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  3.0
Jet2_tau_2_1
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_2_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  1.78
Jet2_tau_2_2
|-------> Running single year 2017
|------> Cross check: plotting da

|-----> Condition Number:  2.09
Jet2_tau_0p5_2
|-------> Running single year 2018
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_0p5_2
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  3.28
Jet2_tau_0p5_3
|-------> Running single year 2018
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_0p5_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.91
Jet2_tau_0p5_4
|-------> Running single 

Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Info in <TCanvas::Print>: png file ../../../../../Results/Results_Aprilv2/dijetSel/2017/Unfolding/Jet1_tau_0p5_1/MCSelfClosure/Jet1_tau_0p5_1_fromMC_QCD_HT2000toInf_nom_dataallBkgs_simpleComparisonPlot_dijetSel__April.png has been created
Info in <TCanvas::Print>: png file ../../../../../Results/Results_Aprilv2/dijetSel/2017/Unfolding/Jet1_tau_0p5_1/MCSelfClosure/Jet1_tau_0

###  Unfold combination of years (self-closure)

In [49]:
inputFolder = '../../../../../Results/Results_Aprilv2/'
outputFolder = '../../../../../Results/Results_Aprilv2/'
main = 'HTbin'
#alt = 'herwig'
process='MCSelfClosure'


if main.startswith('Ptbin'):
    signalLabelBegin = 'QCD_Pt_'
    signalLabel = 'QCD_Pt_3200toInf'
elif main.startswith('HTbin'):
    signalLabelBegin = 'QCD_HT'
    signalLabel = 'QCD_HT2000toInf'
elif main.startswith('herwig'):
    signalLabelBegin = 'QCD_Pt-'
    signalLabel = 'QCD_Pt-150to3000'
if alt.startswith('Ptbin'):
    altSignalLabelBegin = 'QCD_Pt_'
    altSignalLabel = 'QCD_Pt_3200toInf'
elif alt.startswith('HTbin'):
    altSignalLabelBegin = 'QCD_HT'
    altSignalLabel = 'QCD_HT2000toInf'
elif alt.startswith('herwig'):
    altSignalLabelBegin = 'QCD_Pt-'
    altSignalLabel = 'QCD_Pt150to3000'
    #altSignalLabel = 'QCD_Pt-15to7000'

sysSignalLabelBegin = 'sysQCD_' 


In [50]:
for selection in ['_dijetSel']:
    print ("#######################")
    print ("#####%s selection#####"%((selection.split('_')[1])).split('Sel')[0])
    print ("#######################")
    
    variables = nSubVariables_dijetSel
    version = '_April'
    
    sysUnc = [
                '_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', 'model',
                '_jesAbsolute', '_jesBBEC1', '_jesEC2', '_jesFlavorQCD', '_jesHF', '_jesRelativeBal' ,
                '_jesAbsolute_2017', '_jesBBEC1_2017', '_jesEC2_2017', '_jesHF_2017', '_jesRelativeSample_2017',
                '_jesAbsolute_2018', '_jesBBEC1_2018', '_jesEC2_2018', '_jesHF_2018', '_jesRelativeSample_2018',
             ]
                                                   
 
    
    for year in (['all']):
        
        sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2017_HT2000toInf',
                   'sysQCD_jesBBEC1_2017_HT2000toInf',
                   'sysQCD_jesEC2_2017_HT2000toInf',
                   'sysQCD_jesHF_2017_HT2000toInf',
                   'sysQCD_jesRelativeSample_2017_HT2000toInf',
                   'sysQCD_jesAbsolute_2018_HT2000toInf',
                   'sysQCD_jesBBEC1_2018_HT2000toInf',
                   'sysQCD_jesEC2_2018_HT2000toInf',
                   'sysQCD_jesHF_2018_HT2000toInf',
                   'sysQCD_jesRelativeSample_2018_HT2000toInf',
                  ]
        
        lumi, dataFile, sigFiles, bkgFiles, sysSigFile = loadFiles(year)
        #print (sigFiles.keys(),bkgFiles.keys(),dataFile.keys())
        print ("#######################")
        print ("#####year=%s#####"%year)
        print ("#######################")
        
        print ("#######################")
        print ("####Selection=%s#####"%selection)
        print ("#######################")
        
        
        runTUnfold(dataFile=dataFile, sigFiles=sigFiles, bkgFiles=bkgFiles, sysSigFiles={},
                       variables=variables, sel=selection, sysUncert=sysUnc, process=process ,ext='pdf')
        
        #runTUnfold(dataFile=dataFile, sigFiles=sigFiles, altFiles=altSigFiles, varFiles=varSigFiles, bkg=bkgFiles, sysSigFiles=sysSigFiles, 
        #               variables=variables, sel=selection, sysUncert=sysUnc,process='data' ,ext='png')
        gc.collect()

#######################
#####dijet selection#####
#######################
|------> Running combination of years
#######################
#####year=all#####
#######################
#######################
####Selection=_dijetSel#####
#######################
Jet1_tau_0p5_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(8, 8)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.45


/tmp/ipykernel_1272/681485682.py:5: RuntimeWarning: invalid value encountered in true_divide
  correlation = covariance / outer_v


Jet1_tau_0p5_2
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  4.22
Jet1_tau_0p5_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  3.62
Jet1_tau_0p5_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing variou

Info in <TCanvas::Print>: pdf file ../../../../../Results/Results_Aprilv2/dijetSel/all/Unfolding/Jet1_tau_0p5_1/MCSelfClosure/Jet1_tau_0p5_1_fromMC_QCD_HT2000toInf_dijetSel_responseMatrix_April.pdf has been created
Info in <TUnfold::SetConstraint>: fConstraint=0
Warning in <TUnfold::TUnfold>: 3 output bins do not depend on the input data  0 8-9
Info in <TUnfold::TUnfold>: 16 input bins and 7 output bins
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #0 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[ufl])
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #8 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[0.84,0.98])
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #9 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[ofl])
Info in <TUnfoldDensity::RegularizeOneDistribution>: regularizing xaxis regMode=3 densityMode=1 axisSteering=*[UOB]
Warning in <TUnfoldDensity::SetInput>: 2/16 input bins have zero error, and are ignored.
Warning in <TH1D::Sumw2>: Sum of squa

###  Unfold individual years (physics model bias test)

In [51]:
inputFolder = '../test/Samples/Dijet_V06/'
outputFolder = '../../../../../Results/Results_Aprilv2/'
main = 'HTbin'
alt = 'herwig'
process='MCCrossClosure'


if main.startswith('Ptbin'):
    signalLabelBegin = 'QCD_Pt_'
    signalLabel = 'QCD_Pt_3200toInf'
elif main.startswith('HTbin'):
    signalLabelBegin = 'QCD_HT'
    signalLabel = 'QCD_HT2000toInf'
elif main.startswith('herwig'):
    signalLabelBegin = 'QCD_Pt-'
    signalLabel = 'QCD_Pt150to3000'
if alt.startswith('Ptbin'):
    altSignalLabelBegin = 'QCD_Pt_'
    altSignalLabel = 'QCD_Pt_3200toInf'
elif alt.startswith('HTbin'):
    altSignalLabelBegin = 'QCD_HT'
    altSignalLabel = 'QCD_HT2000toInf'
elif alt.startswith('herwig'):
    altSignalLabelBegin = 'QCD_Pt-'
    altSignalLabel = 'QCD_Pt-150to3000'
    #altSignalLabel = 'QCD_Pt-15to7000'

sysSignalLabelBegin = 'sysQCD_' 


In [52]:
for selection in ['_dijetSel']:
    print ("#######################")
    print ("#####%s selection#####"%((selection.split('_')[1])).split('Sel')[0])
    print ("#######################")
    
    variables = nSubVariables_dijetSel
    version = '_April'
    
    if selection.startswith('_W'): sysUnc = ['_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', '_jesTotal', '_model', '_hdamp', '_Tune', '_erdON', '_CR', '_mtop']
    elif selection.startswith('_top'): sysUnc = ['_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', '_jesTotal', '_model', '_hdamp', '_Tune', '_erdON', '_CR', '_mtop']
    elif selection.startswith('_dijet'): sysUnc = [ ]#'_jer', '_isrWeight', '_fsrWeight', '_puWeight', '_pdfWeight', '_jesTotal', '_model' ]
 
    
    for year in (['2017','2018']):
        if '2017'in year:
            
            sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2017_HT2000toInf',
                   'sysQCD_jesBBEC1_2017_HT2000toInf',
                   'sysQCD_jesEC2_2017_HT2000toInf',
                   'sysQCD_jesHF_2017_HT2000toInf',
                   'sysQCD_jesRelativeSample_2017_HT2000toInf',
                  ]
        elif '2018'in year:
            
            sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2018_HT2000toInf',
                   'sysQCD_jesBBEC1_2018_HT2000toInf',
                   'sysQCD_jesEC2_2018_HT2000toInf',
                   'sysQCD_jesHF_2018_HT2000toInf',
                   'sysQCD_jesRelativeSample_2018_HT2000toInf',
                  ]
        lumi, dataFile, sigFiles, bkgFiles, sysSigFile = loadFiles(year)
        #print (sigFiles.keys(),bkgFiles.keys(),dataFile.keys())
        print ("#######################")
        print ("#####year=%s#####"%year)
        print ("#######################")
        
        print ("#######################")
        print ("####Selection=%s#####"%selection)
        print ("#######################")
        
        
        runTUnfold(dataFile=dataFile, sigFiles=sigFiles, bkgFiles=bkgFiles, sysSigFiles={},
                       variables=variables, sel=selection, sysUncert=sysUnc, process=process ,ext='pdf')
        
        #runTUnfold(dataFile=dataFile, sigFiles=sigFiles, altFiles=altSigFiles, varFiles=varSigFiles, bkg=bkgFiles, sysSigFiles=sysSigFiles, 
        #               variables=variables, sel=selection, sysUncert=sysUnc,process='data' ,ext='png')
        gc.collect()

#######################
#####dijet selection#####
#######################
|------> Running single year
#######################
#####year=2017#####
#######################
#######################
####Selection=_dijetSel#####
#######################
Jet1_tau_0p5_1
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(8, 8)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:


/tmp/ipykernel_1272/681485682.py:5: RuntimeWarning: invalid value encountered in true_divide
  correlation = covariance / outer_v


|-----> Condition Number:  2.42
Jet1_tau_0p5_2
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_2
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  4.25
Jet1_tau_0p5_3
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|---

|-----> Condition Number:  2.35
Jet2_tau_1_3
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_1_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  3.51
Jet2_tau_1_4
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_1_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Cond

|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(5, 5)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  4.49
Jet1_tau_2_4
|-------> Running single year 2018
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_2_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(5, 5)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  8.63
Jet2_tau_0p5_1
|-------> Running single year 2018
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_0p5_1
|------>

Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TCanvas::Constructor>: Deleting canvas with same name: c1Jet1_tau_0p5_1_fromMC_QCD_HT2000toInf_nom
Info in <TCanvas::Print>: png file ../../../../../Results/Results_Aprilv2/dijetSel/2017/Unfolding/Jet1_tau_0p5_1/MCCrossClosure/Jet1_tau_0p5_1_fromMC_QCD_HT2000toInf_nom_dataallBkgs_simpl

###  Unfold combination of years (physics model bias test)

In [53]:
inputFolder = '../../../../../Results/Results_Aprilv2/'
outputFolder = '../../../../../Results/Results_Aprilv2/'
main = 'HTbin'
alt = 'herwig'
process='MCCrossClosure'


if main.startswith('Ptbin'):
    signalLabelBegin = 'QCD_Pt_'
    signalLabel = 'QCD_Pt_3200toInf'
elif main.startswith('HTbin'):
    signalLabelBegin = 'QCD_HT'
    signalLabel = 'QCD_HT2000toInf'
elif main.startswith('herwig'):
    signalLabelBegin = 'QCD_Pt-'
    signalLabel = 'QCD_Pt-150to3000'
if alt.startswith('Ptbin'):
    altSignalLabelBegin = 'QCD_Pt_'
    altSignalLabel = 'QCD_Pt_3200toInf'
elif alt.startswith('HTbin'):
    altSignalLabelBegin = 'QCD_HT'
    altSignalLabel = 'QCD_HT2000toInf'
elif alt.startswith('herwig'):
    altSignalLabelBegin = 'QCD_Pt-'
    altSignalLabel = 'QCD_Pt-150to3000'
    #altSignalLabel = 'QCD_Pt-15to7000'

sysSignalLabelBegin = 'sysQCD_' 


In [54]:
for selection in ['_dijetSel']:
    print ("#######################")
    print ("#####%s selection#####"%((selection.split('_')[1])).split('Sel')[0])
    print ("#######################")
    
    variables = nSubVariables_dijetSel
    version = '_April'
    
    sysUnc = [
                '_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', '_model',
                '_jesAbsolute', '_jesBBEC1', '_jesEC2', '_jesFlavorQCD', '_jesHF', '_jesRelativeBal' ,
                '_jesAbsolute_2017', '_jesBBEC1_2017', '_jesEC2_2017', '_jesHF_2017', '_jesRelativeSample_2017',
                '_jesAbsolute_2018', '_jesBBEC1_2018', '_jesEC2_2018', '_jesHF_2018', '_jesRelativeSample_2018',
             ]
                                                   
 
    
    for year in (['all']):
        
        sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2017_HT2000toInf',
                   'sysQCD_jesBBEC1_2017_HT2000toInf',
                   'sysQCD_jesEC2_2017_HT2000toInf',
                   'sysQCD_jesHF_2017_HT2000toInf',
                   'sysQCD_jesRelativeSample_2017_HT2000toInf',
                   'sysQCD_jesAbsolute_2018_HT2000toInf',
                   'sysQCD_jesBBEC1_2018_HT2000toInf',
                   'sysQCD_jesEC2_2018_HT2000toInf',
                   'sysQCD_jesHF_2018_HT2000toInf',
                   'sysQCD_jesRelativeSample_2018_HT2000toInf',
                  ]
        
        lumi, dataFile, sigFiles, bkgFiles, sysSigFile = loadFiles(year)
        #print (sigFiles.keys(),bkgFiles.keys(),dataFile.keys())
        print ("#######################")
        print ("#####year=%s#####"%year)
        print ("#######################")
        
        print ("#######################")
        print ("####Selection=%s#####"%selection)
        print ("#######################")
        
        
        runTUnfold(dataFile=dataFile, sigFiles=sigFiles, bkgFiles=bkgFiles, sysSigFiles=sysSigFile,
                       variables=variables, sel=selection, sysUncert=sysUnc, process=process ,ext='pdf')
        
        #runTUnfold(dataFile=dataFile, sigFiles=sigFiles, altFiles=altSigFiles, varFiles=varSigFiles, bkg=bkgFiles, sysSigFiles=sysSigFiles, 
        #               variables=variables, sel=selection, sysUncert=sysUnc,process='data' ,ext='png')
        gc.collect()

#######################
#####dijet selection#####
#######################
|------> Running combination of years
#######################
#####year=all#####
#######################
#######################
####Selection=_dijetSel#####
#######################
Jet1_tau_0p5_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(8, 8)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.45


/tmp/ipykernel_1272/681485682.py:5: RuntimeWarning: invalid value encountered in true_divide
  correlation = covariance / outer_v


Jet1_tau_0p5_2
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  4.22
Jet1_tau_0p5_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  3.62
Jet1_tau_0p5_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(6,

|-----> Condition Number:  3.99
Jet2_tau_2_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
|------> TUnfolding adding input:
|------> TUnfolding doUnfold:
|------> TUnfolding covariances
(5, 5)
|------> Drawing unfold plot:
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  7.26


Info in <TCanvas::Print>: pdf file ../../../../../Results/Results_Aprilv2/dijetSel/all/Unfolding/Jet1_tau_0p5_1/MCCrossClosure/Jet1_tau_0p5_1_fromMC_QCD_HT2000toInf_dijetSel_responseMatrix_April.pdf has been created
Info in <TUnfold::SetConstraint>: fConstraint=0
Warning in <TUnfold::TUnfold>: 3 output bins do not depend on the input data  0 8-9
Info in <TUnfold::TUnfold>: 16 input bins and 7 output bins
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #0 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[ufl])
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #8 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[0.84,0.98])
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #9 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[ofl])
Info in <TUnfoldDensity::RegularizeOneDistribution>: regularizing xaxis regMode=3 densityMode=1 axisSteering=*[UOB]
Warning in <TUnfoldDensity::SetInput>: 2/16 input bins have zero error, and are ignored.
Info in <TUnfold::SetConstraint>: fC

###  Unfold individual years (data)

In [32]:
inputFolder = '../test/Samples/Dijet_V06/'
outputFolder = '../../../../../Results/Results_Aprilv2/'
main = 'HTbin'
alt = 'herwig'
process='data'
if main.startswith('Ptbin'):
    signalLabelBegin = 'QCD_Pt_'
    signalLabel = 'QCD_Pt_3200toInf'
elif main.startswith('HTbin'):
    signalLabelBegin = 'QCD_HT'
    signalLabel = 'QCD_HT2000toInf'
elif main.startswith('herwig'):
    signalLabelBegin = 'QCD_Pt-'
    signalLabel = 'QCD_Pt-150to3000'
if alt.startswith('Ptbin'):
    altSignalLabelBegin = 'QCD_Pt_'
    altSignalLabel = 'QCD_Pt_3200toInf'
elif alt.startswith('HTbin'):
    altSignalLabelBegin = 'QCD_HT'
    altSignalLabel = 'QCD_HT2000toInf'
elif alt.startswith('herwig'):
    altSignalLabelBegin = 'QCD_Pt-'
    altSignalLabel = 'QCD_Pt-150to3000'
    #altSignalLabel = 'QCD_Pt-15to7000'

sysSignalLabelBegin = 'sysQCD_' 


In [40]:
for selection in ['_dijetSel']:
    ##############PROBLEM with herwig 7 flatpower7 sample for 2017: it does not exist in V06, so using v04 herwig samples for this 
    print ("#######################")
    print ("#####%s selection#####"%((selection.split('_')[1])).split('Sel')[0])
    print ("#######################")
    
    variables = nSubVariables_dijetSel
    version = '_April'
    
    
    
    for year in (['2017','2018']):
        if '2017'in year:
            
            sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2017_HT2000toInf',
                   'sysQCD_jesBBEC1_2017_HT2000toInf',
                   'sysQCD_jesEC2_2017_HT2000toInf',
                   'sysQCD_jesHF_2017_HT2000toInf',
                   'sysQCD_jesRelativeSample_2017_HT2000toInf',
                  ]
            sysUnc = [
                '_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', '_model',
                '_jesAbsolute', '_jesBBEC1', '_jesEC2', '_jesFlavorQCD', '_jesHF', '_jesRelativeBal' ,
                '_jesAbsolute_2017', '_jesBBEC1_2017', '_jesEC2_2017', '_jesHF_2017', '_jesRelativeSample_2017',
             ]
        else:
            
            sysSignalLabels = ['sysQCD_puWeight_HT2000toInf',
                   'sysQCD_isrWeight_HT2000toInf',
                   'sysQCD_fsrWeight_HT2000toInf',
                   'sysQCD_jer_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_pdfWeight_HT2000toInf',
                   'sysQCD_jesAbsolute_HT2000toInf',
                   'sysQCD_jesFlavorQCD_HT2000toInf',
                   'sysQCD_jesHF_HT2000toInf',
                   'sysQCD_jesRelativeBal_HT2000toInf',
                   'sysQCD_jesBBEC1_HT2000toInf',
                   'sysQCD_jesEC2_HT2000toInf',
                   'sysQCD_jesAbsolute_2018_HT2000toInf',
                   'sysQCD_jesBBEC1_2018_HT2000toInf',
                   'sysQCD_jesEC2_2018_HT2000toInf',
                   'sysQCD_jesHF_2018_HT2000toInf',
                   'sysQCD_jesRelativeSample_2018_HT2000toInf',
                  ]
            sysUnc = [
                '_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', '_model',
                '_jesAbsolute', '_jesBBEC1', '_jesEC2', '_jesFlavorQCD', '_jesHF', '_jesRelativeBal' ,
                '_jesAbsolute_2018', '_jesBBEC1_2018', '_jesEC2_2018', '_jesHF_2018', '_jesRelativeSample_2018',
             ]
        lumi, dataFile, sigFiles, bkgFiles, sysSigFiles = loadFiles(year)
        print ("#######################")
        print ("#####year=%s#####"%year)
        print ("#######################")
        
        print ("#######################")
        print ("####Selection=%s#####"%selection)
        print ("#######################")
        
        print (sysSigFiles,sigFiles)
        runTUnfold(dataFile=dataFile, sigFiles=sigFiles, bkgFiles=bkgFiles, sysSigFiles=sysSigFiles,
                       variables=variables, sel=selection, sysUncert=sysUnc, process='data' ,ext='pdf')
        
        #runTUnfold(dataFile=dataFile, sigFiles=sigFiles, altFiles=altSigFiles, varFiles=varSigFiles, bkg=bkgFiles, sysSigFiles=sysSigFiles, 
        #               variables=variables, sel=selection, sysUncert=sysUnc,process='data' ,ext='png')
        gc.collect()

#######################
#####dijet selection#####
#######################
|------> Running single year
#######################
#####year=2017#####
#######################
#######################
####Selection=_dijetSel#####
#######################
{'sysQCD_jer_HT100to200': [<cppyy.gbl.TFile object at 0x5560cf53dad0>, {'2017': {'skimmerHisto': 'jetObservables_histograms_QCDHT100to200_jer_UL2017.root', 'nGenWeights': 76745700.0}, '2018': {'skimmerHisto': 'jetObservables_histograms_QCDHT100to200_jer_UL2018.root', 'nGenWeights': 70101398.0}, 'selection': 'dijet', 'XS': 23620000.0, 'label': 'QCD MG5+Pythia8', 'color': 616}], 'sysQCD_jer_HT200to300': [<cppyy.gbl.TFile object at 0x5560ce70da50>, {'2017': {'skimmerHisto': 'jetObservables_histograms_QCDHT200to300_jer_UL2017.root', 'nGenWeights': 56892662.0}, '2018': {'skimmerHisto': 'jetObservables_histograms_QCDHT200to300_jer_UL2018.root', 'nGenWeights': 22793054.0}, 'selection': 'dijet', 'XS': 1555000.0, 'label': 'QCD MG5+Pythia8', 'color': 6

|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(8, 8)


/tmp/ipykernel_1269/681485682.py:5: RuntimeWarning: invalid value encountered in true_divide
  correlation = covariance / outer_v


|------> Drawing unfold plot:
Outer AK8 jet #tau_{1}^{(0.5)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.42
Jet1_tau_0p5_2
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_2
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
Outer AK8 jet #tau_{2}^{(0.5)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  4.25
Jet1_tau_0p5_3
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding

|------> Drawing unfold plot:
Central AK8 jet #tau_{3}^{(0.5)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.93
Jet2_tau_0p5_4
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_0p5_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
Central AK8 jet #tau_{4}^{(0.5)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.83
Jet2_tau_1_1
|-------> Running single year 2017
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_1_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding

|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_1
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(8, 8)
|------> Drawing unfold plot:
Outer AK8 jet #tau_{1}^{(0.5)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.48
Jet1_tau_0p5_2
|-------> Running single year 2018
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet1_tau_0p5_2
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
Outer AK8 jet #tau

|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_0p5_3
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
Central AK8 jet #tau_{3}^{(0.5)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.91
Jet2_tau_0p5_4
|-------> Running single year 2018
|------> Cross check: plotting data vs all MC
|------> Unfolding Jet2_tau_0p5_4
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
Central AK8 jet 

Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure already created
Warning in <TH2F::Sumw2>: Sum of squares of weights structure al

###  Unfold combination of years (data)

In [55]:
inputFolder = '../../../../../Results/Results_Aprilv2/'
outputFolder = '../../../../../Results/Results_Aprilv2/'
main = 'HTbin'
alt = 'herwig'
process='data'

In [56]:
for selection in ['_dijetSel']:
    print ("#######################")
    print ("#####%s selection#####"%((selection.split('_')[1])).split('Sel')[0])
    print ("#######################")
    
    variables = nSubVariables_dijetSel
    
    version = '_April'
    year = 'all'

    sysSignalLabels = [
                            'sysQCD_puWeight_HT2000toInf',
                            'sysQCD_isrWeight_HT2000toInf',
                            'sysQCD_fsrWeight_HT2000toInf',
                            'sysQCD_jer_HT2000toInf',
                            'sysQCD_jesAbsolute_HT2000toInf',
                            'sysQCD_jesBBEC1_HT2000toInf',
                            'sysQCD_jesEC2_HT2000toInf',
                            'sysQCD_jesFlavorQCD_HT2000toInf',
                            'sysQCD_jesHF_HT2000toInf',
                            'sysQCD_jesRelativeBal_HT2000toInf',
                            'sysQCD_jesAbsolute_2017_HT2000toInf',
                            'sysQCD_jesBBEC1_2017_HT2000toInf',
                            'sysQCD_jesEC2_2017_HT2000toInf',
                            'sysQCD_jesHF_2017_HT2000toInf',
                            'sysQCD_jesRelativeSample_2017_HT2000toInf',
                            'sysQCD_jesAbsolute_2018_HT2000toInf',
                            'sysQCD_jesBBEC1_2018_HT2000toInf',
                            'sysQCD_jesEC2_2018_HT2000toInf',
                            'sysQCD_jesHF_2018_HT2000toInf',
                            'sysQCD_jesRelativeSample_2018_HT2000toInf',
                            'sysQCD_pdfWeight_HT2000toInf'
                      ]

    sysUnc = [
                '_jer', '_isrWeight', '_fsrWeight','_pdfWeight', '_puWeight', 
                '_jesAbsolute', '_jesBBEC1', '_jesEC2', '_jesFlavorQCD', '_jesHF', '_jesRelativeBal' ,
                '_jesAbsolute_2017', '_jesBBEC1_2017', '_jesEC2_2017', '_jesHF_2017', '_jesRelativeSample_2017',
                '_jesAbsolute_2018', '_jesBBEC1_2018', '_jesEC2_2018', '_jesHF_2018', '_jesRelativeSample_2018',
                '_model'
             ]      



    for year in (['all']):
        lumi, dataFile, sigFiles, bkgFiles, sysSigFile = loadFiles(year)
        #print (sigFiles.keys(),bkgFiles.keys(),dataFile.keys())
        print ("#######################")
        print ("#####year=%s#####"%year)
        print ("#######################")
        
        print ("#######################")
        print ("####Selection=%s#####"%selection)
        print ("#######################")
        
        
        runTUnfold(dataFile=dataFile, sigFiles=sigFiles, bkgFiles=bkgFiles, sysSigFiles=sysSigFile,
                       variables=variables, sel=selection, sysUncert=sysUnc, process='data' ,ext='pdf')
        
        #runTUnfold(dataFile=dataFile, sigFiles=sigFiles, altFiles=altSigFiles, varFiles=varSigFiles, bkg=bkgFiles, sysSigFiles=sysSigFiles, 
        #               variables=variables, sel=selection, sysUncert=sysUnc,process='data' ,ext='png')
        gc.collect()

#######################
#####dijet selection#####
#######################
|------> Running combination of years
#######################
#####year=all#####
#######################
#######################
####Selection=_dijetSel#####
#######################
Jet1_tau_0p5_1
|------> Cross check: plotting data vs all MC
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(8, 8)
|------> Drawing unfold plot:
Outer AK8 jet #tau_{1}^{(0.5)}


/tmp/ipykernel_1272/681485682.py:5: RuntimeWarning: invalid value encountered in true_divide
  correlation = covariance / outer_v


|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.45
Jet1_tau_0p5_2
|------> Cross check: plotting data vs all MC
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(7, 7)
|------> Drawing unfold plot:
Outer AK8 jet #tau_{2}^{(0.5)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  4.22
Jet1_tau_0p5_3
|------> Cross check: plotting data vs all MC
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfo

|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.5
Jet2_tau_1_2
|------> Cross check: plotting data vs all MC
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold plot:
Central AK8 jet #tau_{2}^{(1)}
|------> Drawing unfolding uncertainty plot:
|------> Drawing various 2D matrices:
|-----> Condition Number:  2.33
Jet2_tau_1_3
|------> Cross check: plotting data vs all MC
|------> Cross check: plotting response matrix for signal
|------> TUnfolding starts:
|------> TUnfolding adding input:
Subtracting backgrounds
|------> TUnfolding adding uncert:
|------> TUnfolding doUnfold:
|------> TUnfolding uncertainties:
|------> TUnfolding covariances
(6, 6)
|------> Drawing unfold pl

Info in <TCanvas::Print>: png file ../../../../../Results/Results_Aprilv2/dijetSel/all/Unfolding/Jet1_tau_0p5_1/data/Jet1_tau_0p5_1_fromData_QCD_HT2000toInf_TestDataMinusBkgs_data-Bkgssignal true reco_simpleComparisonPlot_dijetSel__April.png has been created
Info in <TCanvas::Print>: pdf file ../../../../../Results/Results_Aprilv2/dijetSel/all/Unfolding/Jet1_tau_0p5_1/data/Jet1_tau_0p5_1_fromData_QCD_HT2000toInf_dijetSel_responseMatrix_April.pdf has been created
Info in <TUnfold::SetConstraint>: fConstraint=0
Warning in <TUnfold::TUnfold>: 3 output bins do not depend on the input data  0 8-9
Info in <TUnfold::TUnfold>: 16 input bins and 7 output bins
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #0 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[ufl])
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #8 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.5)}[0.84,0.98])
Info in <TUnfoldDensity::TUnfold>: *NOT* unfolding bin #9 (xaxis:Accepted Gen Outer AK8 jet #tau_{1}^{(0.

In [ ]:

TH2 *old; 
//the original histogram 
//create a new TH2 with your bin arrays spec 
double xbins[4]={0,70,130,400}; 
double ybins[4]={0,50,100,400}; 
TH2F *h = new TH2F("oldrebin",old->GetTitle(),nx,xbins,ny,ybins); 
TAxis *xaxis = old->GetXaxis(); 
TAxis *yaxis = old->GetYaxis(); 

for (int j=1; j<=yaxis->GetNbins();j++) 
    { for (int i=1; i<=xaxis->GetNbins();i++) 
         { h->Fill(xaxis->GetBinCenter(i), yaxis->GetBinCenter(j),old->GetBinContent(i,j)); } } }